# Setup

## Import

In [ ]:
import cgtools as cg
import collections
from cycler import cycler
import copy
import decimal
import glob
import gromacstools as gt
from gromacstools.general import WorkingDir, run_bash
import itertools
import json
import math
import matplotlib.pyplot as plt
import matplotlib as mpl
import numpy as np
from numpy.polynomial import Polynomial
import os
import pandas as pd
import re
import shutil
import scipy.constants as const
import subprocess
import sys
import tempfile
import xml.etree.ElementTree as ET
import importlib

In [ ]:
sys.path.append('/home/marvin/research/code/votca/csg/share/scripts/inverse/')
import csg_functions as csg
import iie

In [ ]:
class oconst: pass
oconst.k_gro = const.k * const.N_A * 1e-3
oconst.h_gro = const.h * const.N_A * 1e-3 * 1e12
oconst.f_gro = 138.935458  # electric conversion factor: V = f q²/r
oconst.epsilon_0_gro = const.epsilon_0 * const.N_A * 1e3
oconst.rec_cm_per_THz = 1e12 / const.c / 100
oconst.bar_per_md_pressure = 10**28 * const.u

## often used helper functions

In [ ]:
def check_job_stati(jobids, remote_host):
    stati = gt.remote.check_slurm_jobs(jobids, remote_host)

    # print status for each job
    completed_jobids = []
    for jobid, status in zip(jobids, stati):
        print(jobid, status)
        if (status in ('FAILED', 'COMPLETED', None)
            or status.startswith('CANCELLED')):
            completed_jobids.append(jobid)

    # remove jobids which are completed
    new_jobids = [jobid for jobid in jobids if jobid not in completed_jobids]
    return new_jobids

In [ ]:
def gen_moltype_list(fg_topology, statepoint):
    """Generate moltype_list from fg_topology and statepoint."""
    moltype_list = [{'name': moltype_key, **moltype}
                    for moltype_key, moltype in fg_topology['moltypes'].items()
                    if statepoint['composition'][moltype_key] > 0]
    for moltype in moltype_list:
        moltype['atoms'] = moltype.pop('beads')
        moltype['atoms'] = [{'name': atom_key,
                             'mass': fg_topology['beadtypes'][atom['type']]['mass'],
                             **atom}
                            for atom_key, atom in moltype['atoms'].items()]
        moltype['nmols'] = statepoint['composition'][moltype['name']]
    return moltype_list

In [ ]:
def compare_dict_tree(dict1, dict2):
    if json.dumps(dict1, sort_keys=True) == json.dumps(dict2, sort_keys=True):
        return True
    else:
        return False

In [ ]:
def replace_dict_tree(sub_dict, sub_repl_dict, create_non_existing=True):
    for k, v in sub_repl_dict.items():
        if not create_non_existing:
            if k not in sub_dict.keys():
                continue
        if isinstance(v, dict) and k in sub_dict.keys():
            sub_dict[k] = replace_dict_tree(sub_dict[k], sub_repl_dict[k], create_non_existing)
        else:
            sub_dict[k] = sub_repl_dict[k]
    return sub_dict

In [ ]:
def test_replace_dict_tree():
    orig = {'a': {'b': {'c1': 1, 'c2': 2}}, 'x': {'y': 100, 'z': 100}}
    repl = {'a': {'b': {'c2': 3}}, 'x': {'z': 200}, 'foo': 'bar'}
    print(replace_dict_tree(orig, repl))

test_replace_dict_tree()

In [ ]:
def apply_and_replace_string_function_tuples(sub_dict, values_dict):
    """Go through a dict structure recursively replacing (string, functin) tuples."""
    for k, v in sub_dict.items():
        if isinstance(v, tuple) and len(v) == 2 and isinstance(v[0], str) and callable(v[1]) and v[0] in values_dict.keys():
            sub_dict[k] = v[1](values_dict[v[0]])  # call functions
            if isinstance(sub_dict[k], dict) or (isinstance(sub_dict[k], tuple) and len(sub_dict[k]) == 2 and isinstance(sub_dict[k][0], str) and callable(sub_dict[k][1])):
                sub_dict[k] = apply_and_replace_string_function_tuples(sub_dict[k], values_dict)  # go through resulting dict, too
        elif isinstance(v, dict):
            sub_dict[k] = apply_and_replace_string_function_tuples(sub_dict[k], values_dict)
    return sub_dict

In [ ]:
def test_apply_and_replace_string_function_tuples():
    #orig = {'a': {'b': {'c1': 1, 'c2': ('c', lambda x: 2*x)}}, 'x': {'y': 100, 'z': 100}}
    orig = {'a': {'b': {'c1': 1, 'c2': ('c', lambda c: c)}}, 'x': {'y': 100, 'z': 100, 'g': ('e', lambda e: e)}}
    #values_dict = {'c': 3}
    values_dict = {'c': {'foo': ('e', lambda e: e+1)}, 'e': 200}
    print(apply_and_replace_string_function_tuples(orig, values_dict))

test_apply_and_replace_string_function_tuples()

In [ ]:
def get_values_in_dict_tree(dict_tree, path):
    """Generate values in dict_tree that match path with None as wildcard"""
    if len(path) == 0:  # found element
        yield dict_tree
    else:
        if path[0] is None:
            for value in dict_tree.values():
                yield from get_values_in_dict_tree(value, path[1:])
        elif path[0] in dict_tree.keys():
            yield from get_values_in_dict_tree(dict_tree[path[0]], path[1:])

In [ ]:
def change_dict_tree_with_path(dict_tree, path, value, create_non_existing=True):
    # path elements can be lists to do multiple children
    if isinstance(path[0], list):
        all_path0 = path[0]
    else:
        all_path0 = [path[0]]
    for path0 in all_path0:
        # create something new
        if path0 not in dict_tree.keys() and create_non_existing:
            if len(path) == 1:  # found element
                # new end node
                dict_tree[path0] = value
            else:
                # create new child node
                dict_tree[path0] = {}
                change_dict_tree_with_path(dict_tree[path0], path[1:], value, create_non_existing=create_non_existing)
        # only substitute what is there
        elif path0 in dict_tree.keys():
            if len(path) == 1:  # found element
                # substitute by value
                dict_tree[path0] = value
            else:
                # substitue in sub-tree
                change_dict_tree_with_path(dict_tree[path0], path[1:], value, create_non_existing=create_non_existing)

In [ ]:
def readin_table(filename):
    data = np.loadtxt(filename, dtype=str, comments=['#', '@'])
    x = data[:, 0].astype(float)
    y = data[:, 1].astype(float)
    try:
        y_flag = data[:, 2].astype('S1')
    except:
        y_flag = [''] * len(x)
    return x, y, y_flag

In [ ]:
def readin_table_gromacs(filename, U_col=7, F_col=8):
    data = np.loadtxt(filename, dtype=str, comments=['#', '@'])
    x = data[:, 0].astype(float)
    U = data[:, U_col].astype(float)
    F = data[:, F_col].astype(float)
    return x, U, F

In [ ]:
def uniquify(seq):
    seen = set()
    seen_add = seen.add
    return [x for x in seq if not (x in seen or seen_add(x))]

In [ ]:
def gen_statepoints(state):
    # prepare statepoints
    if state['type'] == 'single':
        statepoints = [{'path': '.', **state}]
    elif state['type'] == 'multi':
        #statepoints = copy.deepcopy(cg_problem['state'])
        statepoints = []
        for i in range(len(state['names'])):
            statepoint = {key: value[i] for key, value in state.items() if key not in ('tags', 'type', 'composition', 'votca-settings')}
            statepoint['composition'] = {key: value[i] for key, value in state['composition'].items()}
            statepoint['path'] = statepoint['names']
            del statepoint['names']
            statepoint['type'] = "multi-sub"
            statepoints.append(statepoint)
    return statepoints

In [ ]:
def calc_potential(r, atom1, atom2, combination_fuction, cut_off, non_mixing_rule_factors, eps_r=1.0, potential_shift=True, add_coulomb=True):
    assert type(r) == np.ndarray
    with np.errstate(divide='ignore', invalid='ignore'):
        sig, eps = combination_fuction(atom1['sigma'], atom2['sigma'], atom1['epsilon'], atom2['epsilon'])
        # non mixing rule lambda factor
        lambda_ = 1.0
        if (key := frozenset({atom1['type'], atom2['type']})) in non_mixing_rule_factors:
            lambda_ = non_mixing_rule_factors[key]
        # calc LJ
        potential = lambda_ * 4 * eps * ((sig / r)**12 - (sig / r)**6)
        # shift such that pot=0 at cut-off
        if potential_shift:
            potential -= 4 * eps * ((sig / cut_off)**12 - (sig / cut_off)**6)
        potential[r > cut_off] = 0
        # calc Coulomb
        if add_coulomb:
            potential += oconst.f_gro * atom1['charge'] * atom2['charge'] / (eps_r * r)
    return potential

## Remote computing resource

In [ ]:
def gen_remote_stuff(remote_host, remote_partition, ntasks, votca=False, **kwargs):
    
    # DEFINE!
    remote_dir_base = os.path.join("/home/mbernhardt/run/projects/iie/simulations2")

    fg_gromacs_module = {
        'batch': 'gromacs /6zq3ypk',   # gromacs@2021.5~blas+cuda
        'batchgpu': 'gromacs /6zq3ypk',    # gromacs@2021.5~blas+cuda
        'milan': 'gromacs /furgxnd',    # gromacs@2021.5~blas+cuda
        'rtx3080': 'gromacs /furgxnd',    # gromacs@2021.5~blas+cuda
    }[remote_partition]
    votca_gromacs_module = {
        'batch': 'gromacs /ze62fhc',    # gromacs@2019.6~blas+cuda
        'batchgpu': 'gromacs /ze62fhc',    # gromacs@2019.6~blas+cuda
        'milan': 'gromacs /aeshyvv',    # gromacs@2019.6~blas+cuda
        'rtx3080': 'gromacs /aeshyvv',    # gromacs@2019.6~blas+cuda
    }[remote_partition]
    sbatch_arguments = [
        '--job-name=cg',
        f'--partition={remote_partition}',
        f"--ntasks={ntasks}",
        '--time=24:00:00',
    ]
    for key, arg in kwargs.items():
        if arg is not None:
            sbatch_arguments.append(f"--{key.replace('_', '-')}={arg}")
    sbatch_arguments_section = '\n'.join((f'#SBATCH {arg}' for arg in sbatch_arguments))
    votca_version = "votca-milan" if remote_partition in ['milan', 'rtx3080'] else "votca"
    remote_header = f"""#!/bin/sh
{sbatch_arguments_section}

set -eo pipefail  # -u does not work with VOTCA and/or conda?

# Create local directory
JOBTMP="/tmp/$(mktemp -u data${{SLURM_JOB_ID}}XXXXXXXXXXXXXX)"
mkdir $JOBTMP

# enable spack
export SPACK_PYTHON=/usr/bin/python3.6
export SPACK_ROOT=/shared/spack
. $SPACK_ROOT/share/spack/setup-env.sh

# load modules
module purge
spack unload --all
spack_gmx_for_fg="{fg_gromacs_module}"  # libraries for MD, load before calling votca
spack_gmx_for_votca="{votca_gromacs_module}"  # libraries for Votca, load before calling votca
spack load $spack_gmx_for_fg
"""
    if votca:
        remote_header += f"""
spack load /m67paft  # boost@1.78.0
spack load /b5wq7vk  # gsl@2.7~external-cblas
spack load /h5unuli  # fftw@3.3.10+mpi~openmp~pfft_patches precision=double,float

source ~/software/miniconda3/etc/profile.d/conda.sh
conda activate
source /home/mbernhardt/software/{votca_version}/bin/VOTCARC.bash
"""
    remote_footer = """
# Remove local directory
rm -rf $JOBTMP
"""
    return remote_dir_base, remote_header, remote_footer, {'remote_host': remote_host, 'remote_partion': remote_partition, 'ntasks': ntasks, 'votca': votca, **kwargs}

remote_host = 'sniffa'
def test():
    remote_dir_base, remote_header, remote_footer, remote_args = gen_remote_stuff(remote_host, 'rtx3080', ntasks=48, gres='gpu:1', votca=True)
    print(remote_header)
test()

In [ ]:
if 'jobids' not in locals():
    jobids = []

## Coarse-graining setup

### fg_sys_types

In [ ]:
combination_rule = {
    'oplsaa.ff': lambda sig1, sig2, eps1, eps2: ((sig1*sig2)**(1/2), (eps1*eps2)**(1/2)),  # geometric
    'ligpargen': lambda sig1, sig2, eps1, eps2: ((sig1*sig2)**(1/2), (eps1*eps2)**(1/2)),  # geometric
}

In [ ]:
fg_sys_types = {
    'hexane': {
        'tags': [],
        'md-settings': {
            'md-program': 'gromacs',
            'dt': 0.0005,
            'tau-t': 1,
            'tau-p': 10,
            'integrator+thermostat': 'md+v-rescale',
        },
        'topology': {
            'ff-key': 'ligpargen',
            'beadtypes': {
                'C': {'mass': 12.011},
                'H': {'mass': 1.008},
            },
            'moltypes': {
                'hexane': {
                    'itp': 'hexane.itp',
                    'short-name': 'HEX',
                    'beads': {
                        'C00': {'type': 'C', 'charge': -0.2388,},
                        'C01': {'type': 'C', 'charge': -0.1795,},
                        'C02': {'type': 'C', 'charge': -0.1784,},
                        'C03': {'type': 'C', 'charge': -0.1784,},
                        'C04': {'type': 'C', 'charge': -0.1795,},
                        'C05': {'type': 'C', 'charge': -0.2388,},
                        'H06': {'type': 'H', 'charge': 0.0807,},
                        'H07': {'type': 'H', 'charge': 0.0807,},
                        'H08': {'type': 'H', 'charge': 0.0807,},
                        'H09': {'type': 'H', 'charge': 0.0881,},
                        'H0A': {'type': 'H', 'charge': 0.0881,},
                        'H0B': {'type': 'H', 'charge': 0.0892,},
                        'H0C': {'type': 'H', 'charge': 0.0892,},
                        'H0D': {'type': 'H', 'charge': 0.0892,},
                        'H0E': {'type': 'H', 'charge': 0.0892,},
                        'H0F': {'type': 'H', 'charge': 0.0881,},
                        'H0G': {'type': 'H', 'charge': 0.0881,},
                        'H0H': {'type': 'H', 'charge': 0.0807,},
                        'H0I': {'type': 'H', 'charge': 0.0807,},
                        'H0J': {'type': 'H', 'charge': 0.0807,},
                    },
                },
            },
        },
    },
    'neon-argon': {
        'tags': [],
        'md-settings': {
            'md-program': 'gromacs',
            'dt': 0.005,
            'tau-t': 1,
            'tau-p': 10,
            'integrator+thermostat': 'md+v-rescale-nodispcorr',
        },
        'topology': {
            'ff-key': 'oplsaa.ff',
            'beadtypes': {
                'Ne': {'mass': 20.1797},
                'Ar': {'mass': 39.948},
            },
            'moltypes': {
                'neon': {
                    'itp': 'neon.itp',
                    'short-name': 'neon',
                    'beads': {
                        'NE': {'type': 'Ne', 'charge': 0.0, 'sigma': 2.78000e-01, 'epsilon': 2.88696e-01},
                    },
                },
                'argon': {
                    'itp': 'argon.itp',
                    'short-name': 'argon',
                    'beads': {
                        'AR': {'type': 'Ar', 'charge': 0.0, 'sigma': 3.40100e-01, 'epsilon': 9.78638e-01},
                    },
                },
            },
        },
    },
}

### states

In [ ]:
states = {
    'pure': {
        'hexane': {
            'tags': [],
            'type': 'single',
            'composition': {
                'hexane': 3000
            },
            'temperature': 293.15,
            #'pressure-fg': 1,
            'volume-fg': 8.68171**3,
            #'volume-cg': 'fg conf',
            'volume-cg': 8.68171**3,
            'votca-settings': {'inverse': {
                'gauss_newton': {'pressure_constraint': 1},
                'cleanlist': "../jobtmp/traj.xtc",
                'gromacs': {'traj': "../jobtmp/traj.xtc"},
            }},
        },
    },
    'x0.5': {
        'neon-argon': {
            'tags': [],
            'type': 'single',
            'composition': {
                'neon': 1500,
                'argon': 1500,
            },
            # assumed to mix and be liquid based on phase diagram in Nasrabad et al. 2004
            'temperature': 100,
            #'pressure-fg': 1000,
            'volume-fg': 4.82748**3,
            #'volume-cg': 'fg conf',
            'volume-cg': 4.82748**3,
            'votca-settings': {'inverse': {
                'iie': {'pressure_constraint': 1},
                'cleanlist': "../jobtmp/traj.xtc",
                'gromacs': {'traj': "../jobtmp/traj.xtc"},
            }},
        },
    },
}

### mappings

In [ ]:
mappings = {
    '2heavy': {
        'tags': [],
        'pos-weighting': 'mass-unity',
        'charge-weighting': 'zero',
    },
    'unity': {
        'tags': [],
        'pos-weighting': 'mass-unity',
        'charge-weighting': 'zero',
    },
}

### cg_sys_types

In [ ]:
# define either bonds -> the bond has to be definded by the type of the two beads (works not for A4 naphtalene)
# or define bondtypes -> the bondtypes can have arbitrary names

cg_sys_types = {
    ('hexane', '2heavy'): {
        'tags': [],
        'md-settings': {
            'md-program': 'gromacs',
            'dt': 0.0015,
            'tau-t': 0.5,
        },
        'topology': {
            'moltypes': {
                'hexane': {
                    'short-name': 'HEXCG',
                    'bonds': frozenset({
                        frozenset({'A1', 'B'}),
                        frozenset({'A2', 'B'}),
                    }),
                },
            },
        },
        'votca-settings': {},
        'functional-votca-settings-input': {
            'cut': 1.2,
            'cut_gn_res': 1.6,
            'cut_max': 4.2,
            'Delta_r': 0.004,
            'md-program': 'gromacs',
        },
        'votca-settings': {
            'bond': {'min': 0.15, 'max': 0.35, 'step': 0.0005},
        },

    },
    ('neon-argon', 'unity'): {
        'tags': [],
        'md-settings': {
            'md-program': 'gromacs',
            'dt': 0.005,
            'tau-t': 2,
        },
        'topology': {
            'moltypes': {
                'neon': {
                    'short-name': 'NECG',
                    'bonds': frozenset({}),
                },
                'argon': {
                    'short-name': 'ARCG',
                    'bonds': frozenset({}),
                },
            },
        },
        'functional-votca-settings-input': {
            'cut': 0.9,
            'cut_gn_res': 0.9,
            'cut_max': 2.4,
            'Delta_r': 0.002,
            'md-program': 'gromacs',
        },
    },
}


In [ ]:
mapping_moltypes_dict = {
    ('hexane', '2heavy'): {
        'hexane': {
            'A1': {'type': 'A', 'fg-beads': ('C00', 'C01', 'H06', 'H07', 'H08', 'H09', 'H0A')},
            'B': {'type': 'B', 'fg-beads': ('C02', 'C03', 'H0B', 'H0C', 'H0D', 'H0E')},
            'A2': {'type': 'A', 'fg-beads': ('C04', 'C05', 'H0F', 'H0G', 'H0H', 'H0I', 'H0J')},
        },
    },
    ('neon-argon', 'unity'): {
        'neon': {
            'NE': {'type': 'NE', 'fg-beads': ('NE',)},
        },
        'argon': {
            'AR': {'type': 'AR', 'fg-beads': ('AR',)},
        },
    },
}


In [ ]:
def gen_mapping(fg_sys_type_key, mappings, mapping_key):
    """This function could also generate the mapping based on fg_sys_type.
    
    For now it uses a dictionary."""
    mapping = copy.deepcopy(mappings[mapping_key])
    mapping['moltypes'] = mapping_moltypes_dict[(fg_sys_type_key, mapping_key)]
    return mapping

### votca settings

In [ ]:
def gen_votca_settings():
    votca_settings = {
        'hncn-ibiintra': {
            'tags': set({}),
            'meta': {
                'singlestate': True, 'multistate': False,
                'all-interactions': True, 'selected-interactions': False,
                'max_step0': ('cut_max', lambda x: x),
                'every-step-imc-matrix': False,
            },
            'non-bonded': {
                'min': 0.0,
                'max': ('cut', lambda x: 2 * x),
                'step': ('Delta_r', lambda x: x),
                'inverse': {
                    'do_potential': "1",
                    'imc': {'group': 'all'},
                },
                'improve_dist_near_core': {
                    'target': 'true',
                    'new': 'true',
                    'fit_start_g': 0.0001,
                    'fit_end_g': 0.1,
                },
            },
            'bond': {
                'min': 0.0,
                'max': 0.6,
                'step': 0.001,
                'inverse': {
                    'do_potential': "0",
                    'post_update': "ibi extrapolate",
                    'post_update_options': {},
                    'imc': {'group': 'none'},
                }
            },
            'angle': {
                # borders at precisely π/2 will result in that bin having half height
                # this will result in spikes in the force
                # therefore subtract half the step
                'min': 0.0,
                'max': np.floor((np.pi-0.005)*1e5) / 1e5,
                'step': 0.01,
                'inverse': {
                    'do_potential': "0",
                    'post_update': "ibi extrapolate",
                    'post_update_options': {},
                    'imc': {'group': 'none'},
                },
            },
            'inverse': {
                'method': 'iie',
                'iterations_max': 20,
                'program': 'gromacs',
                'filelist': 'conf.gro grompp.mdp index.ndx topol.top table.xvg topology.xml',
                'cleanlist': '../jobtmp/traj.xtc',
                'gromacs': {
                    'equi_time': 100,
                    'table_end': ('cut', lambda x: x + 1.1),
                    'traj': None,  # set depending on state['type'] to ../jobtmp/traj.xtc or ../../jobtmp/traj-$state.xtc
                    'mdrun': {'opts': '-pin on'},
                },
                'dist_min': 1e-5,  # minimum for bond
                'topol_xml': 'topology.xml',
                'initial_guess': {
                    'method': 'ie',
                    'cut_off': ('cut', lambda x: x),
                    'ie': {
                        'closure': 'hnc',
                    }
                },
                'iie': {
                    'algorithm': 'newton',
                    'closure': 'hnc',
                    'use_target_dcdh': 'false',
                },
                'newton': {
                    'cut_off': ('cut', lambda x: x),
                },
                'verbose': 'step0+1',
            },
        },
    }
    votca_settings['hncnt-ibiintra'] = copy.deepcopy(votca_settings['hncn-ibiintra'])
    votca_settings['hncnt-ibiintra']['non-bonded']['max'] = ('cut', lambda x: x)
    votca_settings['hncnt-ibiintra']['inverse']['iie']['use_target_dcdh'] = 'true'
    
    votca_settings['hncn-altibiintra'] = copy.deepcopy(votca_settings['hncn-ibiintra'])
    votca_settings['hncn-altibiintra']['meta']['only-fg-sys-type'] = ['hexane']
    votca_settings['hncn-altibiintra']['non-bonded']['inverse']['do_potential'] = "0 1"
    votca_settings['hncn-altibiintra']['bond']['inverse']['post_update_options']['ibi'] = {'do': "1 0"}
    votca_settings['hncn-altibiintra']['angle']['inverse']['post_update_options']['ibi'] = {'do': "1 0"}
    votca_settings['hncn-altibiintra']['inverse']['iterations_max'] = 40
    
    votca_settings['hncnt-altibiintra'] = copy.deepcopy(votca_settings['hncn-altibiintra'])
    votca_settings['hncnt-altibiintra']['non-bonded']['max'] = ('cut', lambda x: x)
    votca_settings['hncnt-altibiintra']['inverse']['iie']['use_target_dcdh'] = 'true'
    
    # long for comparing accuracy to IMC
    votca_settings['hncnl-altibiintra'] = copy.deepcopy(votca_settings['hncn-altibiintra'])
    votca_settings['hncnl-altibiintra']['tags'].add('long-md')
    
    # constrained GN with cut-off of 1.2 nm
    votca_settings['phncgnt-altibiintra'] = copy.deepcopy(votca_settings['hncn-ibiintra'])
    votca_settings['phncgnt-altibiintra']['tags'].add('long-md')
    votca_settings['phncgnt-altibiintra']['meta']['only-fg-sys-type'] = ['hexane']
    votca_settings['phncgnt-altibiintra']['non-bonded']['max'] = 1.6
    votca_settings['phncgnt-altibiintra']['non-bonded']['inverse']['do_potential'] = "0 1"
    votca_settings['phncgnt-altibiintra']['bond']['inverse']['post_update_options']['ibi'] = {'do': "1 0"}
    votca_settings['phncgnt-altibiintra']['angle']['inverse']['post_update_options']['ibi'] = {'do': "1 0"}
    votca_settings['phncgnt-altibiintra']['inverse']['iterations_max'] = 40
    votca_settings['phncgnt-altibiintra']['inverse']['initial_guess']['cut_off'] = 1.2
    votca_settings['phncgnt-altibiintra']['inverse']['iie']['algorithm'] = 'gauss-newton'
    votca_settings['phncgnt-altibiintra']['inverse']['iie']['use_target_dcdh'] = 'true'
    del votca_settings['phncgnt-altibiintra']['inverse']['newton']
    votca_settings['phncgnt-altibiintra']['inverse']['gauss_newton'] = {
        'cut_off': 1.2,
        'cut_residual': 1.6,
        'pressure_constraint': 'changeme',
        'residual_weighting': 'r**2/(g_tgt+1e-30)',
    }
    
    votca_settings['PEhncgnt-altibiintra'] = copy.deepcopy(votca_settings['phncgnt-altibiintra'])
    votca_settings['PEhncgnt-altibiintra']['inverse']['gauss_newton'] = {
        'cut_off': 1.2,
        'cut_residual': 1.6,
        'potential_energy_constraint': -30.42,
        'residual_weighting': 'r**2/(g_tgt+1e-30)',
    }
    
    votca_settings['KBIhncgnt-altibiintra'] = copy.deepcopy(votca_settings['phncgnt-altibiintra'])
    votca_settings['KBIhncgnt-altibiintra']['inverse']['gauss_newton'] = {
        'cut_off': 1.2,
        'cut_residual': 1.6,
        'kirkwood_buff_constraint': 'true',
        'residual_weighting': 'r**2/(g_tgt+1e-30)',
    }
    
    votca_settings['KBIphncgnt-altibiintra'] = copy.deepcopy(votca_settings['phncgnt-altibiintra'])
    votca_settings['KBIphncgnt-altibiintra']['inverse']['gauss_newton'] = {
        'cut_off': 1.2,
        'cut_residual': 1.6,
        'kirkwood_buff_constraint': 'true',
        'pressure_constraint': 'changeme',
        'residual_weighting': 'r**2/(g_tgt+1e-30)',
    }
    
    votca_settings['PEphncgnt-altibiintra'] = copy.deepcopy(votca_settings['phncgnt-altibiintra'])
    votca_settings['PEphncgnt-altibiintra']['inverse']['gauss_newton'] = {
        'cut_off': 1.2,
        'cut_residual': 1.6,
        'potential_energy_constraint': -30.42,
        'pressure_constraint': 'changeme',
        'residual_weighting': 'r**2/(g_tgt+1e-30)',
    }
    
    votca_settings['KBIPEphncgnt-altibiintra'] = copy.deepcopy(votca_settings['PEphncgnt-altibiintra'])
    votca_settings['KBIPEphncgnt-altibiintra']['inverse']['gauss_newton'] = {
        'cut_off': 1.2,
        'cut_residual': 1.6,
        'kirkwood_buff_constraint': 'true',
        'potential_energy_constraint': -30.42,
        'pressure_constraint': 'changeme',
        'residual_weighting': 'r**2/(g_tgt+1e-30)',
    }
    
    # constraint comparison system
    votca_settings['hncgnt-altibiintra'] = copy.deepcopy(votca_settings['phncgnt-altibiintra'])
    votca_settings['hncgnt-altibiintra']['inverse']['gauss_newton'] = {
        'cut_off': 1.2,
        'cut_residual': 1.6,
        'residual_weighting': 'r**2/(g_tgt+1e-30)',
    }
    
    # test cut_residual
    # c = cut, r = res
    """
    votca_settings['chncgnt-altibiintra'] = copy.deepcopy(votca_settings['phncgnt-altibiintra'])
    votca_settings['chncgnt-altibiintra']['meta']['only-fg-sys-type'] = ['hexane']
    votca_settings['chncgnt-altibiintra']['non-bonded']['max'] = 1.2   # We still want to see change
    votca_settings['chncgnt-altibiintra']['inverse']['initial_guess']['cut_off'] = 0.7
    votca_settings['chncgnt-altibiintra']['inverse']['gauss_newton']['cut_off'] = 0.7
    votca_settings['chncgnt-altibiintra']['inverse']['gauss_newton']['cut_residual'] = 0.7
    del votca_settings['chncgnt-altibiintra']['inverse']['gauss_newton']['pressure_constraint']
    
    votca_settings['rhncgnt-altibiintra'] = copy.deepcopy(votca_settings['chncgnt-altibiintra'])
    votca_settings['rhncgnt-altibiintra']['non-bonded']['max'] = 1.2
    votca_settings['rhncgnt-altibiintra']['inverse']['gauss_newton']['cut_residual'] = 1.2
    """
    
    # test optimizing short potentials on long RDF
    for cut_off_10 in [4, 5, 6, 7, 8, 9, 10, 11]:
        key = f"hncgntco{cut_off_10:02d}-altibiintra"
        votca_settings[key] = copy.deepcopy(votca_settings['phncgnt-altibiintra'])
        votca_settings[key]['tags'].remove('long-md')
        votca_settings[key]['meta']['only-fg-sys-type'] = ['hexane']
        votca_settings[key]['non-bonded']['max'] = 1.2   # We still want to see change
        votca_settings[key]['inverse']['initial_guess']['cut_off'] = cut_off_10 / 10
        votca_settings[key]['inverse']['gauss_newton']['cut_off'] = cut_off_10 / 10
        votca_settings[key]['inverse']['gauss_newton']['cut_residual'] = 1.2  # optimize long range
        del votca_settings[key]['inverse']['gauss_newton']['pressure_constraint']
    
    votca_settings['imc-ibiintra'] = copy.deepcopy(votca_settings['hncn-ibiintra'])
    votca_settings['imc-ibiintra']['meta']['every-step-imc-matrix'] = True
    votca_settings['imc-ibiintra']['tags'].add('long-md')
    votca_settings['imc-ibiintra']['non-bonded']['max'] = ('cut', lambda x: x)
    votca_settings['imc-ibiintra']['inverse']['gromacs']['imc'] = {'topol': "topology.xml"}
    votca_settings['imc-ibiintra']['inverse']['method'] = 'imc'
    del votca_settings['imc-ibiintra']['inverse']['iie']
    del votca_settings['imc-ibiintra']['inverse']['newton']
    votca_settings['imc-ibiintra']['inverse']['imc'] = {'algorithm': 'gauss-newton', 'use_target_matrix': 'false'}
    votca_settings['imc-ibiintra']['inverse']['gauss_newton'] = {'cut_off': ('cut', lambda x: x), 'cut_residual': ('cut', lambda x: x)}
    
    votca_settings['imct-ibiintra'] = copy.deepcopy(votca_settings['imc-ibiintra'])
    votca_settings['imct-ibiintra']['tags'].remove('long-md')
    votca_settings['imct-ibiintra']['meta']['every-step-imc-matrix'] = False
    votca_settings['imct-ibiintra']['inverse']['imc'] = {'algorithm': 'gauss-newton', 'use_target_matrix': 'true'}
    
    votca_settings['imco-ibiintra'] = copy.deepcopy(votca_settings['imc-ibiintra'])
    votca_settings['imco-ibiintra']['inverse']['imc']['improve_jacobian_onset'] = 'true'
    votca_settings['imco-ibiintra']['inverse']['imc']['onset_thresholds'] = "0.001 0.1"
    
    votca_settings['imcot-ibiintra'] = copy.deepcopy(votca_settings['imct-ibiintra'])
    votca_settings['imcot-ibiintra']['inverse']['imc']['improve_jacobian_onset'] = 'true'
    votca_settings['imcot-ibiintra']['inverse']['imc']['onset_thresholds'] = "0.001 0.1"
    
    votca_settings['imco-altibiintra'] = copy.deepcopy(votca_settings['imco-ibiintra'])
    votca_settings['imco-altibiintra']['meta']['only-fg-sys-type'] = ['hexane']
    votca_settings['imco-altibiintra']['non-bonded']['inverse']['do_potential'] = "0 1"
    votca_settings['imco-altibiintra']['bond']['inverse']['post_update_options']['ibi'] = {'do': "1 0"}
    votca_settings['imco-altibiintra']['angle']['inverse']['post_update_options']['ibi'] = {'do': "1 0"}
    votca_settings['imco-altibiintra']['inverse']['iterations_max'] = 40
    
    votca_settings['imcot-altibiintra'] = copy.deepcopy(votca_settings['imco-altibiintra'])
    votca_settings['imcot-altibiintra']['tags'].remove('long-md')
    votca_settings['imcot-altibiintra']['meta']['every-step-imc-matrix'] = False
    votca_settings['imcot-altibiintra']['inverse']['imc'] = {'algorithm': 'gauss-newton', 'use_target_matrix': 'true'}
    votca_settings['imcot-altibiintra']['inverse']['imc']['improve_jacobian_onset'] = 'true'
    
    votca_settings['ibi-ibiintra'] = copy.deepcopy(votca_settings['hncn-ibiintra'])
    votca_settings['ibi-ibiintra']['non-bonded']['max'] = ('cut', lambda x: x)
    votca_settings['ibi-ibiintra']['inverse']['method'] = 'ibi'
    del votca_settings['ibi-ibiintra']['inverse']['iie']
    del votca_settings['ibi-ibiintra']['inverse']['newton']
    
    votca_settings['ibi-altibiintra'] = copy.deepcopy(votca_settings['ibi-ibiintra'])
    votca_settings['ibi-altibiintra']['meta']['only-fg-sys-type'] = ['hexane']
    votca_settings['ibi-altibiintra']['non-bonded']['inverse']['do_potential'] = "0 1"
    votca_settings['ibi-altibiintra']['bond']['inverse']['post_update_options']['ibi'] = {'do': "1 0"}
    votca_settings['ibi-altibiintra']['angle']['inverse']['post_update_options']['ibi'] = {'do': "1 0"}
    votca_settings['ibi-altibiintra']['inverse']['iterations_max'] = 40
    
    return votca_settings

votca_settings = gen_votca_settings()
votca_settings.keys()

In [ ]:
[k for k, v in votca_settings.items() if 'long-md' in v['tags']]

### combination specific settings

In [ ]:
combination_settings = {
    'interaction-votca-settings': {
        # fg_sys_type state mapping votca_setting. None is wildcard, list means do multiple
        #("mwater-argon", None, "unity+mw", None): [  # do not update mWater potential
            #{'type': 'substitute', 'path': ['non-bonded', 'MW-MW', 'improve_dist_near_core'], 'value': ""},
            #{'type': 'substitute', 'path': ['non-bonded', 'MW-MW', 'inverse'], 'value': {
                #'do_potential': "0",
                #'is_target_distribution': "false",
                #'imc': {'group': 'none'},
            #}},
        #],
        #("mix-ethanol+tert-butanol", "xrange2", "1bead", None): [
            #{'type': 'substitute', 'path': ['non-bonded', 'B-B', 'improve_dist_near_core', 'fit_end_g'], 'value': "0.5"},
        #],
    }
}

### cg problem generators

In [ ]:
# this function generates cg_setup['interaction-votca-settings'] for per-interaction votca settings
def gen_interaction_votca_settings(fg_sys_type_key, state_key, mapping_key, votca_setting_key, combination_interaction_votca_settings):
    
    interaction_votca_settings = {}
    input_parameters = (fg_sys_type_key, state_key, mapping_key, votca_setting_key)
    for setting_combination, adaptions in {k: v for k, v in combination_interaction_votca_settings.items()
                                           # going throuth those setting_combinations that fit the the parameters
                                          if all((key_param == key_comb or key_comb is None) for key_param, key_comb in zip(input_parameters, k))}.items():
        for adaption in (a for a in adaptions if a['type'] == 'substitute'):
            change_dict_tree_with_path(interaction_votca_settings, adaption['path'], adaption['value'])
    
    return interaction_votca_settings

In [ ]:
def is_combination_runnable(fg_sys_type_key, fg_sys_type, state_key, state, mapping_key, mapping, cg_sys_types, votca_setting_key, votca_setting, combination_settings):
    
    def _by_selected_interactions(fg_sys_type_key, state_key, mapping_key, votca_setting_key, votca_setting, combination_interaction_votca_settings):
        interaction_votca_settings = gen_interaction_votca_settings(fg_sys_type_key, state_key, mapping_key, votca_setting_key, combination_interaction_votca_settings)
        path = ['non-bonded', None, 'inverse', 'do_potential']
        has_do_potential_0 = any((v == '0' for v in get_values_in_dict_tree(interaction_votca_settings, path)))
        selected_meta_key = {True: 'selected-interactions', False: 'all-interactions'}[has_do_potential_0]
        return votca_setting['meta'][selected_meta_key]
    
    def _by_multistate(fg_sys_type_key, state, votca_setting):
        return votca_setting['meta'][f"{state['type']}state"]
    
    def _by_tag_disabled(fg_sys_type, state, mapping, cg_sys_type, votca_setting):
        for type_ in (fg_sys_type, state, mapping, cg_sys_type, votca_setting):
            if 'disabled' in type_['tags']:
                return False
        return True
    
    def _by_only_fg_sys_type(votca_setting, fg_sys_type_key):
        if 'only-fg-sys-type' in votca_setting['meta']:
            return fg_sys_type_key in votca_setting['meta']['only-fg-sys-type']
        return True
                    
        
    return all((
        _by_selected_interactions(fg_sys_type_key, state_key, mapping_key, votca_setting_key, votca_setting, combination_settings['interaction-votca-settings']),
        _by_multistate(fg_sys_type_key, state, votca_setting),
        _by_tag_disabled(fg_sys_type, state, mapping, cg_sys_types[(fg_sys_type_key, mapping_key)], votca_setting),
        _by_only_fg_sys_type(votca_setting, fg_sys_type_key),
    ))

In [ ]:
def cg_setup_generator(fg_sys_types, states, mappings, cg_sys_types, votca_settings, return_keys=False, return_indices=False,
                       print_keys=True, combination_settings=combination_settings):
    for f, (fg_sys_type_key, fg_sys_type) in enumerate(fg_sys_types.items()):
        if print_keys: print(f, fg_sys_type_key)
        for s, (state_key, state) in enumerate({state_key: state for state_key, state in states.items()
                                                if fg_sys_type_key in state.keys()}.items()):
            if print_keys: print('', s, state_key)
            for m, (mapping_key, mapping) in enumerate({mapping_key: mapping for mapping_key, mapping in mappings.items()
                                                        # filter for keys of cg_sys_types
                                                        if (fg_sys_type_key, mapping_key) in cg_sys_types.keys()}.items()):
                if print_keys: print(' ', m, mapping_key)
                v = -1
                for votca_setting_key, votca_setting in votca_settings.items():
                    if not is_combination_runnable(fg_sys_type_key, fg_sys_type, state_key, state[fg_sys_type_key], mapping_key, mapping, cg_sys_types, votca_setting_key, votca_setting, combination_settings):
                        continue
                    v += 1
                    if print_keys: print('  ', v, votca_setting_key)
                    cg_setup = {}
                    cg_setup['name'] = '-'.join((fg_sys_type_key, state_key, mapping_key, votca_setting_key))
                    cg_setup['folder'] = '/'.join((fg_sys_type_key, state_key, mapping_key, votca_setting_key))
                    cg_setup['tgt-dist-folder'] = os.path.normpath(os.path.join(cg_setup['folder'], '..', 'target-dists'))
                    cg_setup['fg-topology'] = fg_sys_type['topology']
                    cg_setup['fg-md-settings'] = fg_sys_type['md-settings']
                    cg_setup['state'] = state[fg_sys_type_key]
                    cg_setup['mapping'] = gen_mapping(fg_sys_type_key, mappings, mapping_key)
                    cg_setup['cg-sys-type'] = cg_sys_types[(fg_sys_type_key, mapping_key)]
                    cg_setup['cg-topology'] = cg_sys_types[(fg_sys_type_key, mapping_key)]['topology']
                    cg_setup['cg-md-settings'] = cg_sys_types[(fg_sys_type_key, mapping_key)]['md-settings']
                    cg_setup['votca-settings'] = copy.deepcopy(votca_setting)
                    
                    # apply per cg-sys-type votca-settings
                    if 'votca-settings' in cg_setup['cg-sys-type'].keys():
                        cg_setup['votca-settings'] = replace_dict_tree(cg_setup['votca-settings'], cg_sys_types[(fg_sys_type_key, mapping_key)]['votca-settings'])
                    # apply functional per cg-sys-type votca settings
                    cg_setup['votca-settings'] = apply_and_replace_string_function_tuples(cg_setup['votca-settings'], cg_sys_types[(fg_sys_type_key, mapping_key)]['functional-votca-settings-input'])
                    cg_setup['functional-votca-settings-input'] = cg_sys_types[(fg_sys_type_key, mapping_key)]['functional-votca-settings-input']
                    # apply per state votca-settings
                    if 'votca-settings' in cg_setup['state'].keys():
                        cg_setup['votca-settings'] = replace_dict_tree(cg_setup['votca-settings'], cg_setup['state']['votca-settings'], create_non_existing=False)
                        
                    # these will be picked up by cg.gen_votca_settings()
                    cg_setup['interaction-votca-settings'] = gen_interaction_votca_settings(fg_sys_type_key, state_key, mapping_key, votca_setting_key, combination_settings['interaction-votca-settings'])
                    
                    returns = [cg_setup]
                    if return_keys:
                        returns.extend((fg_sys_type_key, state_key, mapping_key, votca_setting_key))
                    if return_indices:
                        returns.extend((f, s, m, v))
                    if len(returns) == 1:
                        yield returns[0]
                    else:
                        yield tuple(returns)
                
                
list(cg_setup_generator(fg_sys_types, states, mappings, cg_sys_types, votca_settings, return_keys=True, return_indices=True,
                        print_keys=True));


In [ ]:
def md_iterator(fg_sys_types, states, mappings, cg_sys_types, votca_settings, return_keys=False, print_keys=True):
    for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
        fg_sys_types, states, mappings, cg_sys_types, votca_settings, return_keys=True, return_indices=True, print_keys=False):
        if m == 0 and v == 0:  # once for each state
            if print_keys:
                print(f, fg_sys_type_key)
                print('', s, state_key)
            working_dir_md = os.path.join(fg_sys_type_key, state_key, 'fg')
            statepoints = gen_statepoints(cg_problem['state'])
            if return_keys:
                yield cg_problem, fg_sys_type_key, state_key, statepoints, working_dir_md
            else:
                yield cg_problem, statepoints, working_dir_md

In [ ]:
def test_md_iterator():
    for cg_problem, fg_sys_type_key, state_key, statepoints, working_dir_md in md_iterator(
        fg_sys_types, states, mappings, cg_sys_types, votca_settings, return_keys=True):
        pass
        
test_md_iterator()

In [ ]:
def test_groupby():
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['octane']}
    
    states_to_do = states
    #states_to_do = {key: states[key] for key in ['pure']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['1bead']}
    
    votca_settings_to_do = votca_settings
    #votca_settings_to_do = {key: votca_settings[key] for key in ['hncn-ibiintra-hncinit', 'hncnt-ibiintra-hncinit']}
    
    for (fg_sys_type_key, state_key, mapping_key), group in itertools.groupby(cg_setup_generator(
        fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=False),
                                                                              key=lambda x: (x[1], x[2], x[3])):
        print(fg_sys_type_key, state_key, mapping_key)
        for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in group:
            print(' ', votca_setting_key)
        
        
test_groupby()

# Generage coarse-graining files

generate those files needed for calculating the target distributions here

## check charges

In [ ]:
def check_charges():
    votca_settings_to_do = {key: votca_settings[key] for key in ['hncn-ibiintra']}
    for cg_problem in cg_setup_generator(fg_sys_types, states, mappings, cg_sys_types, votca_settings_to_do, print_keys=False):
        cg.print_fg_mol_charge(cg_problem)

check_charges()

## generate mapping files

In [ ]:
def gen_mapping_files():
    for cg_problem in cg_setup_generator(fg_sys_types, states, mappings, cg_sys_types, votca_settings, print_keys=True):
        for moltype in cg_problem['mapping']['moltypes'].keys():
            # for some molecules we want more exclusion in the mapping file
            if 'bonds-mapping-only' in cg_problem['cg-topology']['moltypes'][moltype]:
                cg_problem_temp = copy.deepcopy(cg_problem)
                cg_problem_temp['cg-topology']['moltypes'][moltype]['bonds'] = cg_problem_temp['cg-topology']['moltypes'][moltype]['bonds-mapping-only']
                print('FOO')
            else:
                cg_problem_temp = cg_problem
            #print('   ', moltype)
            mapping_xml = cg.gen_votca_mapping(cg_problem_temp, moltype)
            mapping_unity_xml = cg.gen_votca_mapping(cg_problem_temp, moltype, cg_unity=True)
            with WorkingDir(cg_problem_temp['folder']):
                mapping_xml.write(f"map-{moltype}.xml")
                mapping_unity_xml.write(f"map-cgunity-{moltype}.xml")

gen_mapping_files()

## generate settings{,_step0}.xml

In [ ]:
def gen_settings():
    for cg_problem in cg_setup_generator(fg_sys_types, states, mappings, cg_sys_types, votca_settings):
        
        # generate settings.xml
        settings_xml = cg.gen_votca_settings(cg_problem)
        with WorkingDir(cg_problem['folder']):
            settings_xml.write(f"settings.xml")
        
        # check if settings_step0.xml needed
        max_ = cg_problem['votca-settings']['non-bonded']['max']
        max_0 = cg_problem['votca-settings']['meta']['max_step0']
        step0_different = max_ != max_0
        
        # generate settings_step0.xml if needed
        if step0_different:
            #print(max_, max_0)
            cg_problem_step0 = copy.deepcopy(cg_problem)
            cg_problem_step0['votca-settings']['non-bonded']['max'] = cg_problem_step0['votca-settings']['meta']['max_step0']
            cg_problem_step0['votca-settings']['inverse']['iterations_max'] = 0
            settings_step0_xml = cg.gen_votca_settings(cg_problem_step0)
            with WorkingDir(cg_problem['folder']):
                settings_step0_xml.write(f"settings_step0.xml")
        else:
            with WorkingDir(cg_problem['folder']):
                run_bash('rm -f settings_step0.xml')

gen_settings()

## generate fine-grained topology.xml

In [ ]:
def gen_xml_topol_fg():
    for cg_problem, fg_sys_type_key, state_key, statepoints, working_dir_md in md_iterator(
        fg_sys_types, states, mappings, cg_sys_types, votca_settings, return_keys=True):
        for statepoint in statepoints:
            print('   ', statepoint['path'])
            with WorkingDir(os.path.join(working_dir_md, statepoint['path'])):
                xml_top = cg.gen_topol_xml_fg(cg_problem, statepoint)
                xml_top.write('topology.xml')
            
gen_xml_topol_fg()

# Fine-grained MD

## prepare

### check itp files

In [ ]:
# acetone misses some dihedrals, ignoreing it because rotation of methyl group not important for CG
def check_itp():
    for cg_problem, fg_sys_type_key, state_key, statepoints, working_dir_md in md_iterator(
        fg_sys_types, states, mappings, cg_sys_types, votca_settings, return_keys=True):
        if cg_problem['fg-md-settings']['md-program'] == 'gromacs':
            template_dir = os.path.abspath('template')
            for moltype in cg_problem['fg-topology']['moltypes'].values():
                itp_file = f"{template_dir}/itp/{cg_problem['fg-topology']['ff-key']}/{moltype['itp']}"
                bonds = gt.itp.get_bonds(itp_file)
                print(gt.itp.pairs_from_bonds(bonds) == gt.itp.get_pairs(itp_file), end=' ')
                print(gt.itp.angles_from_bonds(bonds) == gt.itp.get_angles(itp_file), end=' ')
                print(gt.itp.dihedrals_from_bonds(bonds) == gt.itp.get_dihedrals(itp_file))
        else:
            print('.. not Gromacs ..')
    
check_itp()

### prepare MD Gromacs

In [ ]:
def prepare_md_gromacs():
    for cg_problem, fg_sys_type_key, state_key, statepoints, working_dir_md in md_iterator(
        {k: v for k, v in fg_sys_types.items() if v['md-settings']['md-program'] == 'gromacs'},
        states, mappings, cg_sys_types, votca_settings, return_keys=True):
        
        # iterate statepoints, only one for type == 'single'
        for statepoint in statepoints:
            print(' ', statepoint['path'])
            working_dir = os.path.join(working_dir_md, statepoint['path'])
            template_dir = os.path.abspath('template')
            with WorkingDir(working_dir):
                # make dir topol
                run_bash("mkdir -p topol")
                # itp files
                for moltype in cg_problem['fg-topology']['moltypes'].values():
                    run_bash(f"cp {template_dir}/itp/{cg_problem['fg-topology']['ff-key']}/{moltype['itp']} topol/")
                topol_moltype_includes = '\n'.join([f'#include "{moltype["itp"]}"' for moltype in cg_problem['fg-topology']['moltypes'].values()])
                topol_molecules = '\n'.join([f"{moltype['short-name']}  {statepoint['composition'][moltype_key]}" for moltype_key, moltype in cg_problem['fg-topology']['moltypes'].items()
                                            if statepoint['composition'][moltype_key] > 0])
                # if there is a forcefield.itp in the template folder (madrid)
                if os.path.exists(f"{template_dir}/itp/{cg_problem['fg-topology']['ff-key']}/forcefield.itp"):
                    run_bash(f"cp {template_dir}/itp/{cg_problem['fg-topology']['ff-key']}/forcefield.itp topol/")
                    topol = '#include "forcefield.itp"'
                else:  # if not link to gromacs shared files (oplsaa.ff)
                    topol = f"#include \"{cg_problem['fg-topology']['ff-key']}/forcefield.itp\""
                topol += f"""
{topol_moltype_includes}

[ system ]
{fg_sys_type_key}

[ molecules ]
{topol_molecules}
"""
                with open('topol/topol.top', 'w') as f:
                    f.write(topol)
                # mdp files
                # NPT
                if 'pressure-fg' in statepoint.keys():
                    stages = ['equi1', 'equi2', 'equi3', 'prod']
                    # make dirs
                    run_bash("mkdir -p " + ' '.join(stages))
                    # copy from template
                    for stage in stages:
                        run_bash(f"cp {template_dir}/mdp/fg-npt/{cg_problem['fg-md-settings']['integrator+thermostat']}/{stage}.mdp {stage}/grompp.mdp")
                    # mdp run length
                    gt.mdp.set_parameter("equi1/grompp.mdp", 'nsteps',    10_000)
                    gt.mdp.set_parameter("equi2/grompp.mdp", 'nsteps',   100_000)
                    gt.mdp.set_parameter("equi3/grompp.mdp", 'nsteps', 2_000_000)
                    gt.mdp.set_parameter("prod/grompp.mdp",  'nsteps', 2_000_000)
                    # output
                    gt.mdp.set_parameter("prod/grompp.mdp", 'nstxout-compressed', 100 if 'is-large' in states[state_key][fg_sys_type_key]['tags'] else 10)
                    # mdp temperature, pressure
                    gt.mdp.set_parameter("equi2/grompp.mdp", 'gen-temp', statepoint['temperature'])
                    gt.mdp.set_parameter("equi2/grompp.mdp", 'ref-t', statepoint['temperature'])
                    gt.mdp.set_parameter("equi3/grompp.mdp", 'ref-t', statepoint['temperature'])
                    gt.mdp.set_parameter("prod/grompp.mdp", 'ref-t', statepoint['temperature'])
                    gt.mdp.set_parameter("equi3/grompp.mdp", 'ref-p', statepoint['pressure-fg'])
                    #gt.mdp.set_parameter("prod/grompp.mdp", 'ref-p', statepoint['pressure-fg'])
                    # mdp dt, tau-t, tau-p
                    gt.mdp.set_parameter("equi2/grompp.mdp", 'dt', cg_problem['fg-md-settings']['dt'])
                    gt.mdp.set_parameter("equi3/grompp.mdp", 'dt', cg_problem['fg-md-settings']['dt'])
                    gt.mdp.set_parameter("prod/grompp.mdp", 'dt', cg_problem['fg-md-settings']['dt'])
                    gt.mdp.set_parameter("equi2/grompp.mdp", 'tau-t', cg_problem['fg-md-settings']['tau-t'])
                    gt.mdp.set_parameter("equi3/grompp.mdp", 'tau-t', cg_problem['fg-md-settings']['tau-t'])
                    gt.mdp.set_parameter("prod/grompp.mdp", 'tau-t', cg_problem['fg-md-settings']['tau-t'])
                    gt.mdp.set_parameter("equi3/grompp.mdp", 'tau-p', cg_problem['fg-md-settings']['tau-p'] / 2)  # faster equilibration
                    #gt.mdp.set_parameter("prod/grompp.mdp", 'tau-p', cg_problem['fg-md-settings']['tau-p'])
                # NVT
                if 'volume-fg' in statepoint.keys():
                    stages = ['equi1', 'equi2', 'prod']
                    # make dirs
                    run_bash("mkdir -p " + ' '.join(stages))
                    # copy from template
                    for stage in stages:
                        run_bash(f"cp {template_dir}/mdp/fg-nvt/{cg_problem['fg-md-settings']['integrator+thermostat']}/{stage}.mdp {stage}/grompp.mdp")
                    # mdp run length
                    gt.mdp.set_parameter("equi1/grompp.mdp", 'nsteps',    10_000)
                    gt.mdp.set_parameter("equi2/grompp.mdp", 'nsteps', 2_000_000)
                    gt.mdp.set_parameter("prod/grompp.mdp",  'nsteps', 2_000_000)
                    # output
                    gt.mdp.set_parameter("prod/grompp.mdp", 'nstxout-compressed', 100 if 'is-large' in states[state_key][fg_sys_type_key]['tags'] else 10)
                    # mdp temperature
                    gt.mdp.set_parameter("equi2/grompp.mdp", 'gen-temp', statepoint['temperature'])
                    gt.mdp.set_parameter("equi2/grompp.mdp", 'ref-t', statepoint['temperature'])
                    gt.mdp.set_parameter("prod/grompp.mdp", 'ref-t', statepoint['temperature'])
                    # mdp dt, tau-t
                    gt.mdp.set_parameter("equi2/grompp.mdp", 'dt', cg_problem['fg-md-settings']['dt'])
                    gt.mdp.set_parameter("prod/grompp.mdp", 'dt', cg_problem['fg-md-settings']['dt'])
                    gt.mdp.set_parameter("equi2/grompp.mdp", 'tau-t', cg_problem['fg-md-settings']['tau-t'])
                    gt.mdp.set_parameter("prod/grompp.mdp", 'tau-t', cg_problem['fg-md-settings']['tau-t'])
                else:
                    raise Exception('other ensembles not implemented here')
                # gro files
                for moltype_key in cg_problem['fg-topology']['moltypes'].keys():
                    run_bash(f"cp {template_dir}/gro/fg/single-{moltype_key}.gro equi1/")
                # mdp change columbtype if all charges close to zero
                charges = [bead['charge']
                           for mt in cg_problem['fg-topology']['moltypes'].values()
                           for bead in mt['beads'].values()]
                if np.allclose(charges, np.zeros_like(charges)):
                    for stage in stages:
                        gt.mdp.set_parameter(f"{stage}/grompp.mdp", 'coulombtype', 'Cut-off')
                
prepare_md_gromacs()

### fill box

In [ ]:
def fill_box_gromacs():
    density_init_dict = {  # g/ml
        'hexane': 0.6606 * 0.9,  # from wiki
        'neon-argon': 1.207,  # start with density of liquid neon, from wiki
    }
    
    insert_try_scale = collections.defaultdict(lambda: (100, 0.5), {
    })
    
    for cg_problem, fg_sys_type_key, state_key, statepoints, working_dir_md in md_iterator(
        {k: v for k, v in fg_sys_types.items() if v['md-settings']['md-program'] == 'gromacs'},
        states, mappings, cg_sys_types, votca_settings, return_keys=True):
        # iterate statepoints, only one for type == 'single'
        for statepoint in statepoints:
            print(' ', statepoint['path'])
            working_dir = os.path.join(working_dir_md, statepoint['path'])
            with WorkingDir(working_dir):

                # required format for gromacstools.top
                moltype_list = gen_moltype_list(cg_problem['fg-topology'], statepoint)
                top = gt.top.Topology()
                top.load_simple_top(moltype_list)
                
                # Volume
                if 'pressure-fg' in statepoint.keys():
                    volume = top.mass() / const.N_A / density_init_dict[fg_sys_type_key]
                    volume *=  1e21  # from ml to nm^3
                    box_edge = volume**(1/3)
                elif 'volume-fg' in statepoint.keys():
                    volume = statepoint['volume-fg']
                    box_edge = volume**(1/3)
                else:
                    raise Exception('other ensembles not implemented here')
                print('volume:', volume)

                # check existing
                if os.path.exists("equi1/conf.gro"):
                    n_atoms_present = gt.gro.get_natoms("equi1/conf.gro")
                    box_present = gt.gro.get_box("equi1/conf.gro")
                    n_atoms_wanted = top.natoms()
                    if n_atoms_present == n_atoms_wanted and np.allclose(box_present, [box_edge]*3):
                        print("..suitable conf.gro found, skipping..")
                        continue

                # empty box with volume
                empty_gro = f"system\n0\n{box_edge} {box_edge} {box_edge}"
                with open("equi1/conf.gro", 'w') as f:
                    f.write(empty_gro)

                # insert molecules
                for moltype in moltype_list:
                    n_mols = moltype['nmols']
                    mt_name = moltype['name']
                    try_, scale = insert_try_scale[fg_sys_type_key]
                    run_bash(f"gmx -quiet insert-molecules -f equi1/conf.gro -o equi1/conf.gro -ci equi1/single-{mt_name}.gro -nmol {n_mols} -try {try_} -scale {scale}")
                    run_bash("rm -f equi1/\#conf.gro.*")

                # check
                n_atoms_inserted = gt.gro.get_natoms("equi1/conf.gro")
                n_atoms_wanted = top.natoms()
                if n_atoms_inserted != n_atoms_wanted:
                    print(n_atoms_inserted, n_atoms_wanted)
                    raise Exception("not enough molecules inserted")
                    
fill_box_gromacs()

### prepare target-dists folder

In [ ]:
def prepare_tgt_dists_folder():
    
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['water-spce']}
    
    states_to_do = states
    #states_to_do = {key: states[key] for key in ['x0.1']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
    
    votca_settings_to_do = votca_settings
    #votca_settings_to_do = {key: votca_settings[key] for key in ['mshncgnt-ibiintra-hncinit']}
    
    # iterate fg, state, mapping
    for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in (data for data in cg_setup_generator(
        fg_sys_types, states, mappings, cg_sys_types, votca_settings, return_keys=True, return_indices=True, print_keys=False,
    ) if data[8] == 0):
                    
        # find votca-setting largest max
        votca_setting_key_largest_max = None
        largest_max = 0
        # iterate votca settings
        for cg_problem_temp, _, _, _, votca_setting_key  in cg_setup_generator(
            {fg_sys_type_key: fg_sys_types[fg_sys_type_key]},
            {state_key: states[state_key]},
            {mapping_key: mappings[mapping_key]},
            cg_sys_types, votca_settings, return_keys=True, 
        ):
            # only looking at non-bonded.max, bonded should be the same in all votca-settings
            max0_max = {field2: cg_problem_temp['votca-settings'][field1][field2] for field1, field2 in (('non-bonded', 'max'), ('meta', 'max_step0'))}
            if largest_max < max(max0_max.values()):
                print('higher!')
                largest_max = max(max0_max.values())
                votca_setting_key_largest_max = (votca_setting_key, max(max0_max, key=max0_max.get))

        print('largest max in:', votca_setting_key_largest_max)
                
        statepoints = gen_statepoints(cg_problem['state'])
        for statepoint in statepoints:
            print('   ', statepoint['path'])
            
            # mkdir and copy
            dir_tgt_dists = cg_problem['tgt-dist-folder']
            run_bash(f"mkdir -p {dir_tgt_dists}/{statepoint['path']}")
            dir_max = os.path.normpath(os.path.join(cg_problem['folder'], '..', votca_setting_key_largest_max[0]))
            settings_file = f"settings{votca_setting_key_largest_max[1].split('max')[-1]}.xml"
            run_bash(f"cp {dir_max}/{settings_file} {dir_tgt_dists}/settings.xml")
            for moltype in cg_problem['mapping']['moltypes'].keys():
                run_bash(f"cp {dir_max}/map-{moltype}.xml {dir_tgt_dists}/")
            
                        
prepare_tgt_dists_folder()

## run

### run MD and calculate distributions

In [ ]:
def run_md_dist(copy_only=False, run_if_dist_present=False):
    remote_partition = 'rtx3080'
    remote_dir_base, remote_header, remote_footer, remote_args = gen_remote_stuff(remote_host, remote_partition, ntasks=48, votca=True, gres='gpu:2')
    #remote_partition = 'milan'
    #remote_dir_base, remote_header, remote_footer, remote_args = gen_remote_stuff(remote_host, remote_partition, ntasks=96, votca=True)
    # REMEMBER to set -pin off below for non exclusive jobs
    
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['hexane']}
    
    states_to_do = states
    #states_to_do = {key: states[key] for key in ['pure-large']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
    
    votca_settings_to_do = votca_settings
    #votca_settings_to_do = {key: votca_settings[key] for key in ['mshncgnt-ibiintra-hncinit']}
    
    # iterate md setups
    for cg_problem_md, fg_sys_type_key, state_key, statepoints, working_dir_md in md_iterator(
        fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True):
        
        md_program = cg_problem_md['fg-md-settings']['md-program']
        assert md_program in ('gromacs',)
        
        statepoints = gen_statepoints(cg_problem_md['state'])
        for statepoint in statepoints:
            print('   ', statepoint['path'])
            working_dir_md = os.path.join(fg_sys_type_key, state_key, 'fg', statepoint['path'])
            remote_dir_md = os.path.join(remote_dir_base, working_dir_md)
            run_bash(f"ssh {remote_host} mkdir -p {remote_dir_md}")
            # copy simulation files to remote
            if md_program == 'gromacs':
                filelist = ["equi1/conf.gro", "*/grompp.mdp", "topol"]
            with WorkingDir(working_dir_md):
                gt.remote.push_files(filelist, remote_host, remote_dir_md)
            # check some dists are there already
            dists_done = all((glob.glob(os.path.join(cg_problem['tgt-dist-folder'], statepoint['path'], '*.dist.tgt'))
                              for cg_problem, f, s, m, v in cg_setup_generator(
                                  {fg_sys_type_key: fg_sys_types[fg_sys_type_key]},
                                  {state_key: states[state_key]},
                                  mappings, cg_sys_types, votca_settings,
                                  return_keys=False, return_indices=True, print_keys=False)
                              if v == 0))
            if dists_done:
                print('.. all target dists already present ..')
                if not run_if_dist_present:
                    continue
                
            if md_program == 'gromacs':
                mdrun_nt = remote_args['ntasks']
                mdrun_steep_flag = {
                    'batch': f"-nt {mdrun_nt}",
                    'batchgpu': f"-nt {mdrun_nt}",
                    'milan': f"-nt {mdrun_nt}",
                    'rtx3080': f"-nt {mdrun_nt}",
                }[remote_partition]
                mdrun_flag = {
                    'batch': f"-nt {mdrun_nt}",
                    'batchgpu': f"-nt {mdrun_nt} -update gpu",
                    'milan': f"-nt {mdrun_nt}",
                    'rtx3080': f"-nt {mdrun_nt} -update gpu",
                }[remote_partition]
                mdrun_flag += ' -pin on'
            local_folder = "$JOBTMP"
            # one script per md statepoint for all cg problems
            if copy_only:
                script = remote_header
            elif md_program == 'gromacs':
                script = remote_header + fr"""
pushd {remote_dir_md}
pushd equi1
    if [[ ! -f confout.gro ]]; then
        gmx grompp -p ../topol/topol.top -maxwarn 1  # FLEXIBLE might not be defined in some topologies
        gmx mdrun {mdrun_steep_flag}
    fi
    rm -f \#*
popd

pushd equi2
    if [[ ! -f confout.gro ]]; then
        gmx grompp -p ../topol/topol.top -c ../equi1/confout.gro
        gmx mdrun {mdrun_flag}
    fi
    rm -f \#*
popd

if [[ -f equi3/grompp.mdp ]]; then
pushd equi3
    if [[ ! -f confout.gro ]]; then
        gmx grompp -p ../topol/topol.top -c ../equi2/confout.gro
        gmx mdrun {mdrun_flag}
    fi
    rm -f \#*
popd
fi

[[ -f equi3/confout.gro ]] && last_conf=equi3/confout.gro || last_conf=equi2/confout.gro
pushd prod
    gmx grompp -p ../topol/topol.top -c ../$last_conf
    gmx mdrun {mdrun_flag} -x {local_folder}/traj_comp.xtc
    rm -f \#*
popd
popd

# load gromacs version of spack
spack unload gromacs
spack load $spack_gmx_for_votca

# generate tpr for votca
gmx grompp -f prod/grompp.mdp -p topol/topol.top -c $last_conf -o topol/topol-gmx-votca.tpr
rm -f topol/\#topol* mdout.mdp
"""
            # stay in statepoint but iterate mappings
            for cg_problem_td in (data[0] for data in cg_setup_generator(
                {fg_sys_type_key: fg_sys_types[fg_sys_type_key]},
                {state_key: states[state_key]},
                mappings, cg_sys_types, votca_settings, return_keys=True, print_keys=False, return_indices=True,
            ) if data[8] == 0):
                
                working_dir_td = os.path.join(cg_problem_td['tgt-dist-folder'])
                working_dir_td_state = os.path.join(cg_problem_td['tgt-dist-folder'], statepoint['path'])
                remote_dir_td = os.path.join(remote_dir_base, working_dir_td)
                remote_dir_td_state = os.path.join(remote_dir_base, working_dir_td_state)
                # mkdir
                run_bash(f"ssh {remote_host} mkdir -p {remote_dir_td_state}")
                # copy simulation files to remote
                with WorkingDir(working_dir_td):
                    filelist = ["settings.xml", "map-*.xml"]
                    gt.remote.push_files(filelist, remote_host, remote_dir_td)
                    mapping_files = ';'.join(f"{remote_dir_td}/map-{moltype_key}.xml" for moltype_key in cg_problem_td['fg-topology']['moltypes'].keys())
                    if copy_only:
                        pass
                    elif md_program == 'gromacs':
                        script += fr"""
pushd {remote_dir_td_state}
    csg_stat --top {remote_dir_md}/topol/topol-gmx-votca.tpr --options {remote_dir_td}/settings.xml --trj {local_folder}/traj_comp.xtc \
        --cg "{mapping_files}" --nt=$SLURM_JOB_CPUS_PER_NODE --ext dist.tgt --do-imc
    csg_stat --top {remote_dir_md}/topol/topol-gmx-votca.tpr --options {remote_dir_td}/settings.xml --trj {local_folder}/traj_comp.xtc \
        --cg "{mapping_files}" --nt=$SLURM_JOB_CPUS_PER_NODE --ext dist-intra.tgt --only-intra 
popd
"""
            # submit job
            script += remote_footer
            with WorkingDir(working_dir_md):
                jobid = gt.remote.run_slurm_script(script, remote_host, remote_dir_md, dry_run=False)
            print(jobid)
            if jobid != None:
                jobids.append(jobid)

run_md_dist(copy_only=False, run_if_dist_present=True)

### check job status

In [ ]:
jobids = check_job_stati(jobids, remote_host)

### pull MD files from cluster

In [ ]:
def pull_md():
    remote_dir_base, remote_header, remote_footer, remote_args = gen_remote_stuff(remote_host, 'batchgpu', ntasks=48, votca=True, gres='gpu:1')
    
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['pyridine']}
    
    for cg_problem, fg_sys_type_key, state_key, statepoints, working_dir_md in md_iterator(
        fg_sys_types_to_do, states, mappings, cg_sys_types, votca_settings, return_keys=True):
        
        md_program = cg_problem['fg-md-settings']['md-program']
        assert md_program in ('gromacs', 'lammps')
        
        # iterate statepoints, only one for type == 'single'
        for statepoint in statepoints:
            print(' ', statepoint['path'])
            working_dir = os.path.join(working_dir_md, statepoint['path'])
            remote_dir = os.path.join(remote_dir_base, working_dir)
            with WorkingDir(working_dir):
                if md_program == 'gromacs':
                    filelist = ["*/*.edr", "*/confout.gro", "*/topol.tpr", "topol/topol-gmx-votca.tpr"]
                    exclude = "traj*"
                gt.remote.pull_files(filelist, remote_host, remote_dir, exclude=exclude)
                
pull_md()

### equilibration check

In [ ]:
def show_energy_graphs(properties_list, edr_file="ener.edr"):
    run_bash("gmx energy -f {} -o energy-temp.xvg <<< '{}'".format(edr_file, "\n".join(properties_list)))
    gt.xvg.plot("energy-temp.xvg")
    run_bash("rm energy-temp.xvg")

In [ ]:
def check_equi_md():
    
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['ethanol']}
    
    states_to_do = states
    #states_to_do = {key: states[key] for key in ['Vrange3']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['1bead']}
    
    votca_settings_to_do = votca_settings
    #votca_settings_to_do = {key: votca_settings[key] for key in ['mshncgnt-ibiintra-hncinit']}
    
    for cg_problem, fg_sys_type_key, state_key, statepoints, working_dir_md in md_iterator(
        fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True):
        # iterate statepoints, only one for type == 'single'
        for statepoint in statepoints:
            print(' ', statepoint['path'])
            working_dir = os.path.join(working_dir_md, statepoint['path'])
            with WorkingDir(working_dir):
                try:
                    #print("equilibration 3")
                    #show_energy_graphs(["Temperature"], edr_file="equi3/ener.edr")
                    #show_energy_graphs(["Pressure"], edr_file="equi3/ener.edr")
                    #show_energy_graphs(["Volume"], edr_file="equi3/ener.edr")
                    print("production")
                    show_energy_graphs(["Temperature"], edr_file="prod/ener.edr")
                    #show_energy_graphs(["Pressure"], edr_file="prod/ener.edr")
                    #show_energy_graphs(["Volume"], edr_file="prod/ener.edr")
                except:
                    print('.. no data ..')
                
check_equi_md()

### pull dist files from cluster

In [ ]:
def pull_dist():
    remote_dir_base, remote_header, remote_footer, remote_args = gen_remote_stuff(remote_host, 'batchgpu', ntasks=48, votca=True, gres='gpu:1')
    
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['pyridine']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['1bead']}
    
    # iterate fg, state, mapping
    for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in (data for data in cg_setup_generator(
        fg_sys_types_to_do, states, mappings_to_do, cg_sys_types, votca_settings, return_keys=True, return_indices=True, print_keys=False,
    ) if data[8] == 0):
        print(cg_problem['name'])
        
        # iterate state points
        statepoints = gen_statepoints(cg_problem['state'])
        for statepoint in statepoints:
            #print('   ', statepoint['path'])
            
            working_dir = os.path.join(cg_problem['tgt-dist-folder'], statepoint['path'])
            remote_dir = os.path.join(remote_dir_base, working_dir)
            with WorkingDir(working_dir):
                filelist = ["*.dist.tgt", "*.dist-intra.tgt"]
                filelist += ["*.dist-short.tgt"]
                filelist += ["*.gmc", "*.idx", "*.imc"]
                exclude = "traj*"
                # does never fail
                gt.remote.pull_files(filelist, remote_host, remote_dir, exclude=exclude)
                if len(glob.glob("*.tgt")) == 0:
                    print('.. no data ..')
                
pull_dist()

# Iterative coarse-graining

## prepare

### map prod/confout.gro to conf.gro and scale volume

In [ ]:
def map_confout_gromacs():
    
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {k: fg_sys_types[k] for k in ['pyridine']}
    
    states_to_do = states
    #states_to_do = {key: states[key] for key in ['pure-large']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['1bead']}
    
    votca_settings_to_do = votca_settings
    #votca_settings_to_do = {key: votca_settings[key] for key in ['hncnt-hncinitlong']}
    
    # iterate md setups
    # gromacs to gromacs and gromacs to lammps
    for cg_problem_md, fg_sys_type_key, state_key, statepoints, working_dir_md in md_iterator(
        {k: v for k, v in fg_sys_types_to_do.items() if v['md-settings']['md-program'] == 'gromacs'},
        states_to_do, mappings_to_do, 
        #{k: v for k, v in cg_sys_types.items() if v['md-settings']['md-program'] == 'gromacs'},
        cg_sys_types,
        votca_settings_to_do, return_keys=True):
        
        statepoints = gen_statepoints(cg_problem_md['state'])
        for statepoint in statepoints:
            print('   ', statepoint['path'])
            working_dir_md = os.path.abspath(os.path.join(fg_sys_type_key, state_key, 'fg', statepoint['path']))
            
            # average volume
            if statepoint['volume-cg'] == 'fg average':
                with WorkingDir(working_dir_md), tempfile.TemporaryDirectory() as tempdir:
                    run_bash(f"gmx energy -f prod/ener.edr -o {tempdir}/energy-temp.xvg <<< 'Volume'")
                    data, _ = gt.xvg.load(f"{tempdir}/energy-temp.xvg")
                volume_cg = np.mean(data['Volume'])
            elif type(statepoint['volume-cg']) in (int, float):
                volume_cg = statepoint['volume-cg']
            elif statepoint['volume-cg'] == 'fg conf':
                with WorkingDir(working_dir_md):
                    volume_cg = np.prod(gt.gro.get_box(f"prod/conf.gro")[0:3])
            else:
                raise Exception('not implemented')
            
            # iterate cg problems
            for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
                {fg_sys_type_key: fg_sys_types[fg_sys_type_key]},
                {state_key: states[state_key]},
                mappings, cg_sys_types, votca_settings, return_keys=True, return_indices=True, print_keys=True):
                working_dir_cg = os.path.abspath(os.path.join(cg_problem['folder']))
                working_dir_cg_state = os.path.join(cg_problem['folder'], statepoint['path'])
                with WorkingDir(working_dir_cg_state), tempfile.TemporaryDirectory() as tempdir:
                    mapping_files = ';'.join(f"{working_dir_cg}/map-{moltype_key}.xml" for moltype_key in cg_problem['fg-topology']['moltypes'].keys())
                    topol_tpr = ("topol/topol-gmx-votca.tpr"
                                 if os.path.exists(f"{working_dir_md}/topol/topol-gmx-votca.tpr")
                                 else "prod/topol.tpr")
                    if cg_problem['cg-md-settings']['md-program'] == 'gromacs':
                        run_bash(f"csg_map --top {working_dir_md}/{topol_tpr} --trj {working_dir_md}/prod/confout.gro "
                                 f"--cg '{mapping_files}' --vel --out {tempdir}/conf-unscaled.gro")
                        volume_gro = np.prod(gt.gro.get_box(f"{tempdir}/conf-unscaled.gro")[0:3])
                        scale = (volume_cg / volume_gro)**(1/3)
                        # scale and make molecules whole
                        run_bash(f"gmx editconf -f {tempdir}/conf-unscaled.gro -o conf.gro -pbc -scale {scale} {scale} {scale}")
                        run_bash("rm -f \#*")
                        volume_new = np.prod(gt.gro.get_box("conf.gro")[0:3])
                        #print(volume_cg, volume_gro, volume_new)
                    
map_confout_gromacs()

### generate topol.top

In [ ]:
def gen_top():
    for cg_problem in cg_setup_generator(fg_sys_types, states, mappings,
                                         {k: v for k, v in cg_sys_types.items() if v['md-settings']['md-program'] == 'gromacs'},
                                         votca_settings):
        if cg_problem['state']['type'] == 'single':
            topol = cg.gen_gromacs_topol(cg_problem, inline_moleculetypes=True)
            with WorkingDir(cg_problem['folder']):
                with open(f"topol.top", 'w') as f:
                    f.write(topol)
        elif cg_problem['state']['type'] == 'multi':
            topols = cg.gen_gromacs_topol(cg_problem, inline_moleculetypes=True)
            for i, comp_name in enumerate(cg_problem['state']['names']):
                with WorkingDir(os.path.join(cg_problem['folder'], comp_name)):
                    with open(f"topol.top", 'w') as f:
                        f.write(topols[i])
                        
gen_top()

### generate grompp.mdp

In [ ]:
def prep_mdp():
    for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
        fg_sys_types, states, mappings,
        {k: v for k, v in cg_sys_types.items() if v['md-settings']['md-program'] == 'gromacs'},
        votca_settings, return_keys=True, return_indices=True, print_keys=True):
        template_dir = os.path.abspath('template')
        statepoints = gen_statepoints(cg_problem['state'])
        for statepoint in statepoints:
            print('   ', statepoint['path'])
            working_dir = os.path.abspath(os.path.join(cg_problem['folder'], statepoint['path']))
            with WorkingDir(working_dir):
                # mdp files
                run_bash(f"cp {template_dir}/mdp/cg-nvt/grompp.mdp grompp.mdp")
                gt.mdp.set_parameter("grompp.mdp", 'nsteps',
                                     int(2e6)
                                     if (cg_problem['votca-settings']['meta']['every-step-imc-matrix'] or 'long-md' in cg_problem['votca-settings']['tags'])
                                     else int(2e5))
                # mdp dt, tau-t
                gt.mdp.set_parameter("grompp.mdp", 'dt', cg_problem['cg-md-settings']['dt'])
                gt.mdp.set_parameter("grompp.mdp", 'tau-t', cg_problem['cg-md-settings']['tau-t'])
                # mdp temperature
                gt.mdp.set_parameter("grompp.mdp", 'ref-t', statepoint['temperature'])
                # cut_offs
                if 'gauss_newton' in cg_problem['votca-settings']['inverse'].keys():
                    cut_off = cg_problem['votca-settings']['inverse']['gauss_newton']['cut_off']
                elif 'newton' in cg_problem['votca-settings']['inverse'].keys():
                    cut_off = cg_problem['votca-settings']['inverse']['newton']['cut_off']
                else:
                    cut_off = cg_problem['votca-settings']['non-bonded']['max']
                for key in ('rlist', 'rcoulomb', 'rvdw'):
                    gt.mdp.set_parameter("grompp.mdp", key, cut_off)
                # energygrp fields
                energygrps, energygrp_table = cg.gen_grompp_fields(cg_problem)
                gt.mdp.set_parameter("grompp.mdp", 'energygrps', energygrps)
                gt.mdp.set_parameter("grompp.mdp", 'energygrp-table', energygrp_table)
            
prep_mdp()

### generate index.ndx

In [ ]:
# needed for the pair interactions in mdp file
# temporarily create .tpr file without energytables to allow selection by atom type
def prep_ndx():
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {k: fg_sys_types[k] for k in ['pyridine']}
    
    states_to_do = states
    #states_to_do = {key: states[key] for key in ['pure-large']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['1bead']}
    
    votca_settings_to_do = votca_settings
    #votca_settings_to_do = {key: votca_settings[key] for key in ['mshncgnt-ibiintra-hncinit']}
    
    for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
        fg_sys_types_to_do, states_to_do, mappings_to_do, 
        {k: v for k, v in cg_sys_types.items() if v['md-settings']['md-program'] == 'gromacs'},
        votca_settings_to_do, return_keys=True, return_indices=True, print_keys=True):
        statepoints = gen_statepoints(cg_problem['state'])
        for statepoint in statepoints:
            print('   ', statepoint['path'])
            working_dir = os.path.abspath(os.path.join(cg_problem['folder'], statepoint['path']))
            with WorkingDir(working_dir):
                # create topol-notables.tpr
                run_bash("cp grompp.mdp /tmp/grompp-notables.mdp")
                gt.mdp.set_parameter("/tmp/grompp-notables.mdp", 'energygrps', '')
                gt.mdp.set_parameter("/tmp/grompp-notables.mdp", 'energygrp-table', '')
                run_bash("gmx grompp -p topol.top -c conf.gro -f /tmp/grompp-notables.mdp -o /tmp/topol-notables.tpr")
                run_bash("rm -f \#* /tmp/grompp-notables.mdp")
                # commands for gmx make_ndx
                commands = 'keep 0\n'  # clear all groups except System
                commands += ''.join(list(set((fr"t {bead['type']}\n"
                                              for moltype in cg_problem['mapping']['moltypes'].values()
                                              for bead in moltype.values()))))
                commands += 'q'
                run_bash(f"echo -e '{commands}' | gmx make_ndx -f /tmp/topol-notables.tpr")
                run_bash("rm -f \#* /tmp/topol-notables.tpr")
            
prep_ndx()

### copy table.xvg

In [ ]:
def copy_table():
    for cg_problem in cg_setup_generator(fg_sys_types, states, mappings, 
                                         {k: v for k, v in cg_sys_types.items() if v['md-settings']['md-program'] == 'gromacs'},
                                         votca_settings):
        template_dir = os.path.abspath('template')
        statepoints = gen_statepoints(cg_problem['state'])
        for statepoint in statepoints:
            print('   ', statepoint['path'])
            working_dir = os.path.abspath(os.path.join(cg_problem['folder'], statepoint['path']))
            with WorkingDir(working_dir):
                # copy table.xvg
                run_bash(f"cp {template_dir}/xvg/table.xvg table.xvg")
            
copy_table()

### generate topology.xml

(used everywhere, needed for IMC's csg_stat and IIE)

In [ ]:
def gen_xml_topol_():
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {k: fg_sys_types[k] for k in ['pyridine']}
    
    states_to_do = states
    #states_to_do = {key: states[key] for key in ['pure-large']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['1bead']}
    
    votca_settings_to_do = votca_settings
    #votca_settings_to_do = {key: votca_settings[key] for key in ['mshncgnt-ibiintra-hncinit']}
    
    for cg_problem in cg_setup_generator(fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do):
        statepoints = gen_statepoints(cg_problem['state'])
        for statepoint in statepoints:
            print('   ', statepoint['path'])
            working_dir = os.path.abspath(os.path.join(cg_problem['folder'], statepoint['path']))
            with WorkingDir(working_dir):
                if cg_problem['cg-md-settings']['md-program'] == 'gromacs':
                    xml_top = cg.gen_topol_xml_cg(cg_problem, statepoint, box=gt.gro.get_box('conf.gro'))
                xml_top.write('topology.xml')
            
gen_xml_topol_()

### generate settings.xml with correct pressure constraint

In [ ]:
def gen_settings_with_pressure_constraint():
    for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
        fg_sys_types, states, mappings, cg_sys_types, votca_settings, return_keys=True, return_indices=True, print_keys=True):
        
        # not implemented for multiple statepoints
        statepoints = gen_statepoints(cg_problem['state'])
        if len(statepoints) > 1:
            print(" .. NOT IMPLEMENTED ..")
            continue
        
        try:
            p_constraint = cg_problem['votca-settings']['inverse']['gauss_newton']['pressure_constraint']
        except KeyError:
            p_constraint = None
        if (p_constraint is None or p_constraint == 'none'):
            print('no pressure correction')
            pass
        elif type(p_constraint) in (int, float):
            print('fixed value pressure correction:', p_constraint)
            pass
        elif type(p_constraint) is str:
            print(p_constraint)
            if p_constraint == "fg average minus dispersion correction":
                # average pressure and dispersion correction
                working_dir = os.path.abspath(os.path.join(cg_problem['folder'], '..', '..', 'fg'))
                with WorkingDir(working_dir), tempfile.TemporaryDirectory() as tempdir:
                    run_bash(f"gmx energy -f prod/ener.edr -o {tempdir}/energy-temp.xvg <<< 'pres.-dc'")
                    data, _ = gt.xvg.load(f"{tempdir}/energy-temp.xvg")
                    pressure_dc = np.mean(data['Pres. DC'])
                    run_bash(f"gmx energy -f prod/ener.edr -o {tempdir}/energy-temp.xvg <<< 'pressure'")
                    data, _ = gt.xvg.load(f"{tempdir}/energy-temp.xvg")
                    pressure_avg = np.mean(data['Pressure'])
                    p_constraint_val = pressure_avg + pressure_dc
                # write value to xml
                cg_problem['votca-settings']['inverse']['iie']['pressure_constraint'] = p_constraint_val
                settings_xml = cg.gen_votca_settings(cg_problem)
                with WorkingDir(cg_problem['folder']):
                    settings_xml.write(f"settings.xml")
            else:
                raise Exception("unknown pressure constraint: " + p_constraint)
        else:
            raise Exception("unknown pressure constraint: " + p_constraint)
            
gen_settings_with_pressure_constraint()

### symlink to target-dists from cg dir

In [ ]:
def link_dist_tgt():
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['water-spce']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['1bead']}
    
    # iterate all
    for cg_problem in cg_setup_generator(
        fg_sys_types_to_do, states, mappings_to_do, cg_sys_types, votca_settings,  print_keys=True,
    ):
        
        # iterate state points
        statepoints = gen_statepoints(cg_problem['state'])
        for statepoint in statepoints:
            print('   ', statepoint['path'])
            
            working_dir_cg = os.path.join(cg_problem['folder'], statepoint['path'])
            working_dir_td = os.path.abspath(os.path.join(cg_problem['tgt-dist-folder'], statepoint['path']))
            with WorkingDir(working_dir_cg):
                dir_td_rel = os.path.relpath(working_dir_td)
                for f in glob.glob(dir_td_rel + '/*.tgt'):
                    run_bash(f"rm -f {os.path.basename(f)}")
                    run_bash(f"ln -s {f} {os.path.basename(f)}")
                try:
                    if cg_problem['votca-settings']['inverse']['imc']['use_target_matrix'] == 'true':
                        for ext in ['gmc', 'idx']:
                            for f in glob.glob(dir_td_rel + f'/*.{ext}'):
                                run_bash(f"rm -f {os.path.basename(f)}")
                                run_bash(f"ln -s {f} {os.path.basename(f)}")
                    else:
                        raise Exception()
                except:
                    print('.. not target imc ..')
                
link_dist_tgt()

## run

### run votca

In [ ]:
# Careful: shortly deletes settings_*.xml, so running things may stop
def run_inv():
    remote_partition = 'milan'
    remote_dir_base, remote_header, remote_footer, remote_args = gen_remote_stuff(remote_host, remote_partition, ntasks=96, votca=True, exclude='node01')  #, exclude='node47,node48')
    # REMEMBER: `-pin on` might be set in votca_settings
    
    #fg_sys_types_to_do = fg_sys_types
    fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['hexane']}
    
    states_to_do = states
    #states_to_do = {key: states[key] for key in ['pure-large']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
    
    #votca_settings_to_do = votca_settings
    votca_settings_to_do = {key: votca_settings[key] for key in [
        #'imc-ibiintra',
        #'imco-ibiintra',
        #'imct-ibiintra',
        #'imcot-ibiintra',
        #'imco-altibiintra',
        'imcot-altibiintra',
        #'ibi-altibiintra',
        #'hncn-altibiintra',
        'hncnt-altibiintra',
        #'hncgnt-altibiintra',
        #'phncgnt-altibiintra',
        #'PEhncgnt-altibiintra',
        #'KBIhncgnt-altibiintra',
        #'KBIphncgnt-altibiintra',
        #'PEphncgnt-altibiintra',
        #'KBIPEphncgnt-altibiintra',
        #f'hncgntco{cut_off_10:02d}-altibiintra' for cut_off_10 in range(4, 12)
    ]}
    
    
    for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
        fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=True):
        md_program = cg_problem['cg-md-settings']['md-program']
        assert md_program in ('gromacs', 'lammps')
        working_dir = os.path.join(cg_problem['folder'])
        remote_dir = os.path.join(remote_dir_base, working_dir)
        with WorkingDir(working_dir):
            # remove old settings files
            run_bash(f"ssh {remote_host} rm -f {remote_dir}/settings_*.xml")
            # push files
            filelist = ["settings*.xml", "map-cgunity-*.xml"]
            if cg_problem['votca-settings']['inverse']['initial_guess']['method'] == 'table':
                filelist += ["*.pot.in"]
            if cg_problem['state']['type'] == 'single':
                filelist += ["*.dist*.tgt"]
                if cg_problem['votca-settings']['inverse']['method'] == 'imc' and cg_problem['votca-settings']['inverse']['imc']['use_target_matrix'] == 'true':
                    filelist += ["*.gmc", "*.idx"]
                if md_program == 'gromacs':
                    filelist += ["conf.gro", "grompp.mdp", "index.ndx", "table.xvg", "topol.top", "topology.xml"]
            elif cg_problem['state']['type'] == 'multi':
                statepoints = gen_statepoints(cg_problem['state'])
                for statepoint in statepoints:
                    filelist += [statepoint['path'] + '/' + fn
                                for fn in ["conf.gro", "grompp.mdp", "index.ndx", "table.xvg", "topol.top", "topology.xml", "*.dist*.tgt"]]
            else:
                raise NotImplementedError(f"state type {cg_problem['state']['type']} not implemented")
            try:
                gt.remote.push_files(filelist, remote_host, remote_dir)
            except subprocess.CalledProcessError:
                print(".. not all needed files found, skipping this job .. ")
                continue
            # script to run
            script = remote_header + f"""
# load gromacs version of spack
spack unload gromacs
spack load $spack_gmx_for_votca

rm -f jobtmp
ln -s $JOBTMP jobtmp
# if not present votca cant continue steps, says they are in a strange state
touch jobtmp/traj.xtc
# rm done file to extend
rm -f done
""" 
            if os.path.exists('settings_step0.xml'):
                script += f"""
csg_inverse --options settings_step0.xml
rm done
""" 
            script += f"""
csg_inverse --options settings.xml
unlink jobtmp
""" 
            script += remote_footer

            jobid = gt.remote.run_slurm_script(script, remote_host, remote_dir, dry_run=False)
            print(jobid)
            if jobid != None:
                jobids.append(jobid)
run_inv()

### check job status

In [ ]:
jobids = check_job_stati(jobids, remote_host)

### pull files from cluster

In [ ]:
def pull_cg():
    remote_dir_base, remote_header, remote_footer, remote_args = gen_remote_stuff(remote_host, 'batch', ntasks=24, votca=False)
    
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['neon-argon']}
    
    states_to_do = states
    #states_to_do = {key: states[key] for key in ['pure']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['4to5heavy', 'unity']}
    
    votca_settings_to_do = votca_settings
    #votca_settings_to_do = {key: votca_settings[key] for key in [
        #'hncnt-hncinit',
        #'hncnt0.67-hncinit',
    #]}
    
    for cg_problem in cg_setup_generator(fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do):
        working_dir = os.path.join(cg_problem['folder'])
        remote_dir = os.path.join(remote_dir_base, working_dir)
        with WorkingDir(working_dir):
            filelist = []
            #if cg_problem['votca-settings']['inverse']['method'] == 'iie':
            #filelist += ["step_00{0,1}/*.npz", "dcdh.npz"]
            filelist += ["step_000/calc_u_matrix-calc_c_matrix.npz"]  # to inspect c
            filelist += ["step_000/*.pot.new" , "step_*/*.pot.cur", "step_001/*.dpot.new"]
            #if cg_problem['votca-settings']['inverse']['method'] == 'imc':
            #filelist += ["step_001/*.gmc", "step_001/*.imc", "step_001/*.idx"]
            statepoints = gen_statepoints(cg_problem['state'])
            for statepoint in statepoints:
                sp = statepoint['path']
                #print('   ', sp)
                filelist += [f"step_0??/{sp}/*.dist.new", f"step_0??/{sp}/confout.gro", f"step_0??/{sp}/ener.edr"]
                filelist += [f"step_00{{0,1,2}}/{sp}/*.dist*.tgt"]
                #filelist += [f"step_001/{sp}/topol.tpr"]
            exclude = "traj*"
            try:
                gt.remote.pull_files(filelist, remote_host, remote_dir, exclude=exclude)
            except subprocess.CalledProcessError:
                print('.. no data ..')
                
pull_cg()

### equilibration check

In [ ]:
def check_equi_cg():
    
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['neon-argon']}
    
    states_to_do = states
    #states_to_do = {key: states[key] for key in ['pure']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['4to5heavy']}
    
    #votca_settings_to_do = votca_settings
    votca_settings_to_do = {key: votca_settings[key] for key in [
        #'hncnt-hncinit',
        #'hncnt0.67-hncinit',
        #f'hncgntco{cut_off_10:02d}-altibiintra' for cut_off_10 in range(4, 12)
        'KBIhncgnt-altibiintra',
        'KBIphncgnt-altibiintra',
    ]}
    
    for cg_problem in cg_setup_generator(fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do):
        # iterate statepoints, only one for type == 'single'
        working_dir = os.path.join(cg_problem['folder'])
        statepoints = gen_statepoints(cg_problem['state'])
        with WorkingDir(working_dir):
            fig, ax = plt.subplots()
            for statepoint in statepoints:
                sp = statepoint['path']
                print(' ', sp)
                all_temps = np.array([])
                for step in range(1, cg_problem['votca-settings']['inverse']['iterations_max'] + 1):
                    try:
                        if os.path.exists(f"step_{step:03d}/{sp}/ener.edr"):
                            run_bash(f"gmx energy -f step_{step:03d}/{sp}/ener.edr -o /tmp/energy-temp.xvg <<< 'temp'")
                            data, _ = gt.xvg.load("/tmp/energy-temp.xvg")
                            run_bash(f"rm -f /tmp/energy-temp.xvg")
                            temperature = np.asarray(data['Temperature'])
                            #temperature_blocks = np.reshape(temperature[1:], (10, -1))
                            temperature_blocks = np.pad(temperature[1:].astype(float), (0, 10 - temperature[1:].size % 10), 
                                                        mode='constant', constant_values=np.nan).reshape(10, -1)[:, :-1]
                            temperature_block_avg = np.average(temperature_blocks, axis=1)
                            all_temps = np.append(all_temps, temperature_block_avg, axis=0)
                        else:
                            print(f".. step_{step:03d}, no data ..")
                    except:
                        raise
                ax.plot(all_temps, label=sp)
                print(np.mean(all_temps) - statepoint['temperature'])
            ax.axhline(statepoint['temperature'], linestyle=':', color='k')
            ax.legend(frameon=False)
            plt.show()

check_equi_cg()

# Analysis

## matplotlib settings

In [ ]:
SMALL_SIZE = 10
MEDIUM_SIZE = 10
BIGGER_SIZE = 12
mpl_rc_global = {
    'figure.dpi': 120,
    'legend.frameon': False,
    'font.size': SMALL_SIZE,          # controls default text sizes
    'axes.titlesize': SMALL_SIZE,     # fontsize of the axes title
    'axes.labelsize': SMALL_SIZE,    # fontsize of the x and y labels
    'xtick.labelsize': SMALL_SIZE,    # fontsize of the tick labels
    'ytick.labelsize': SMALL_SIZE,    # fontsize of the tick labels
    'legend.fontsize': SMALL_SIZE,    # legend fontsize
    'figure.titlesize': MEDIUM_SIZE,  # fontsize of the figure title
    'xtick.top': True,
    'ytick.right': True,
    'xtick.direction': 'in',
    'ytick.direction': 'in',
    'text.usetex': True,  # otherwise \epsilon is same as \varepsilon. Also nice font
    'text.latex.preamble': r"\usepackage[version=4]{mhchem} \usepackage{siunitx}",
    'legend.labelspacing': 0.2,
    'mathtext.fontset': 'stix',
    'font.family': 'STIXGeneral',
}

In [ ]:
label_of_method = collections.defaultdict(lambda: 'foo', {
    # (method, target_dcdh, GN): label
    'ibi': 'IBI',
    'imc': 'IMC ni',
    'imct': 't-IMC ni',
    'imco': 'IMC',
    'imcot': 't-IMC',
    'hncn': 'HNCN',
    'hncnl': 'HNCN\nlong MD',
    'hncnt': 't-HNCN',
    'hncgnt': r't-HNCGN',
    'phncgnt': r'$p\hspace{0.07em}$-t-HNCGN',
    'PEhncgnt': r'$P\!E$-t-HNCGN',
    'KBIhncgnt': r'$K\!B\!I$-t-HNCGN',
    'KBIphncgnt': r'$K\!B\!I$-$p\hspace{0.07em}$-t-HNCGN',
    'PEphncgnt': r'$P\!E$-$p\hspace{0.07em}$-t-HNCGN',
    **{f'hncgntco{cut_off_10:02d}': f"{cut_off_10/10:.1f}" for cut_off_10 in range(4, 12)}
})

cyan_dark = '#438989'
cyan_normal = '#51A4A4'
#red_dark = '#75485E'
#red_normal = '#AA748D'
red_dark = '#BB0930'
red_normal = '#eb6363'
red_alt_dark = '#a45cff'
red_alt_normal = '#c496ff'
orange_dark = '#BE7F37'
orange_normal = '#CD9351'

color_of_method = collections.defaultdict(lambda: 'grey', {
    'ibi': orange_dark,
    'imc': red_alt_dark,
    'imct': red_alt_normal,
    'imco': red_dark,
    'imcot': red_normal,
    'hncn': cyan_dark,
    'hncnl': cyan_normal,
    'hncnt': cyan_normal,
    'hncgnt': cyan_dark,
    'phncgnt': '#21FA90',
    'PEhncgnt': '#4ba10b',  #'#94CF69',
    'KBIhncgnt': '#6ccae9', #'#00E0CA',
    'KBIphncgnt': '#ff68c1', #'#50C0CA',
    'PEphncgnt': '#3838ad',  #'#94CF69',
    **{f'hncgntco{cut_off_10:02d}': plt.get_cmap("plasma")((cut_off_10-4)/8) for cut_off_10 in range(4, 12)}
})

linestyle_of_method = collections.defaultdict(lambda: ':', {
    'ibi': '-',
    'imc': '-.',
    'imct': (0, (4, 1, 4, 1, 1, 1)),
    'imco': '-',
    'imcot': '--',
    'hncn': '-',
    'hncnl': ':',
    'hncnt': '--',
    'hncgnt': '-',
    'phncgnt': (0, (1, 1)),
    'PEhncgnt': (0, (2, 1)),
    'KBIhncgnt': (0, (4, 2)),
    'PEphncgnt': '-.',
    **{f'hncgntco{cut_off_10:02d}': '-' for cut_off_10 in range(4, 12)}
})

In [ ]:
def test_plot_settings():
        
    mpl_rc_local = {'legend.handlelength': 4.5}
    with plt.rc_context({**mpl_rc_global, **mpl_rc_local}):
        fig, ax = plt.subplots(constrained_layout=True, dpi=200)
        line_label_dict = {}
        for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
            fg_sys_types, states, mappings, cg_sys_types, votca_settings, return_keys=True, return_indices=True, print_keys=False):
            if f != 0 or m != 0:  # only one system and mapping
                continue
            label = label_of_method[votca_setting_key.split('-')[0]]
            color = color_of_method[votca_setting_key.split('-')[0]]
            linestyle = linestyle_of_method[votca_setting_key.split('-')[0]]
            abs_v = list(votca_settings).index(votca_setting_key)
            ax.plot([0, 1], [-abs_v, -abs_v], color=color, label=label, linewidth=2, linestyle=linestyle)
        ax.set_xlim(0, 1.6)
        ax.legend(loc='upper right')
        plt.show()

test_plot_settings()

## show target distributions

### show in tgt folder

In [ ]:
def plot_tgt(ia_to_show=['non-bonded', 'bonds', 'angles', 'dihs'], show_intra=False):
    
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['octane']}
    
    states_to_do = states
    #states_to_do = {key: states[key] for key in ['xrange3']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
    
    votca_settings_to_do = votca_settings
    #votca_settings_to_do = {key: votca_settings[key] for key in ['ibi-ibiintra-hncinit', 'mshncgnt-ibiintra-hncinit']}
    
    for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
        fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=True):
        
        # only one votca setting
        if v > 0:
            continue
        
        #working_dir = os.path.join(cg_problem['folder'])
        #with WorkingDir(working_dir):
        statepoints = gen_statepoints(cg_problem['state'])
        
        fig, axes = plt.subplots(nrows=1, ncols=len(ia_to_show), figsize=[6, 2], constrained_layout=True, squeeze=False, dpi=96)

        color_dict = collections.defaultdict(lambda: None)
        for s, statepoint in enumerate(statepoints):
            sp = statepoint['path']
            print('   ', sp)
            linestyle = ['-', '--', ':'][s]


            dir_tgt = os.path.relpath(f"{cg_problem['tgt-dist-folder']}/{sp}")

            # non-bonded
            if 'non-bonded' in ia_to_show:
                ax = axes[0][0]
                #ax.set_title('non-bonded')
                onset_min, onset_max = (np.inf, 0)
                for i, cg_beadtype_pair in enumerate(itertools.combinations_with_replacement(
                    cg.core.gen_cg_beadtypes(cg_problem['fg-topology'], cg_problem['mapping']).keys(), 2
                )):
                    ia_name = '-'.join(sorted(cg_beadtype_pair))
                    dist_tgt_file = f"{dir_tgt}/{ia_name}.dist.tgt"
                    dist_tgt_r, dist_tgt_g, dist_tgt_flag = readin_table(dist_tgt_file)
                    color = color_dict[(ia_name, None)]
                    label = ia_name if color is None else None
                    line_tgt, = ax.plot(dist_tgt_r, dist_tgt_g, label=label, color=color, linestyle=linestyle)
                    color_dict[(ia_name, None)] = line_tgt.get_color()
                    if show_intra:
                        dist_intra_tgt_file = f"{dir_tgt}/{ia_name}.dist-intra.tgt"
                        dist_intra_tgt_r, dist_intra_tgt_g, dist_intra_tgt_flag = readin_table(dist_intra_tgt_file)
                        line_intra_tgt, = ax.plot(dist_intra_tgt_r, dist_intra_tgt_g, linestyle='-', color='darkred')
                        color_dict[(ia_name, 'intra')] = line_intra_tgt.get_color()
                ax.set_xlim(0)
                ax.set_xlabel(r'$r$ in nm')
                ax.set_ylabel(r'$g$')
                ax.set_ylabel(r'$g$')
                ax.legend(frameon=False, loc='upper right', ncol=4)
            # bonds
            ia_bonded = ia_to_show.copy()
            ia_bonded.remove('non-bonded')
            for i, ia in enumerate(ia_bonded):
                ax = axes[0][i+1]
                ax.set_title(ia)
                dist_files = sorted(glob.glob(f"{dir_tgt}/{ia[:-1]}*.dist.tgt"))
                for i, dist_file in enumerate(dist_files):
                    #print(i, dist_file)
                    ia_name = dist_file.split('/')[-1].split('.')[0]
                    dist_r, dist_p, dist_flag = readin_table(dist_file)
                    label = ia_name if (ia_name, None) not in color_dict.keys() else None
                    line_tgt, = ax.plot(dist_r, dist_p, label=label)
                    color_dict[(ia_name, None)] = line_tgt.get_color()
                ax.set_ylabel(r'$p$')
                if len(dist_files) > 0:
                    ax.legend(frameon=False, loc='upper right', ncol=4)
        plt.show()
            
plot_tgt(ia_to_show=['non-bonded'])

### show in votca folder

In [ ]:
def plot_tgt_votca(ia_to_show=['non-bonded', 'bonds', 'angles', 'dihs'], show_onset=False, show_step0tgt=False, show_step1new=False, show_intra=False):
    
    #fg_sys_types_to_do = fg_sys_types
    fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['neon-argon']}
    
    states_to_do = states
    #states_to_do = {key: states[key] for key in ['xrange3']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
    
    votca_settings_to_do = votca_settings
    #votca_settings_to_do = {key: votca_settings[key] for key in ['ibi-ibiintra-hncinit', 'mshncgnt-ibiintra-hncinit']}
    
    for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
        fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=True):
        
        working_dir = os.path.join(cg_problem['folder'])
        with WorkingDir(working_dir):
            statepoints = gen_statepoints(cg_problem['state'])
            for statepoint in statepoints:
                sp = statepoint['path']
                print('   ', sp)

                fig, axes = plt.subplots(nrows=1, ncols=len(ia_to_show), figsize=[6, 2], constrained_layout=True, squeeze=False, dpi=96)
            
                # non-bonded
                if 'non-bonded' in ia_to_show:
                    ax = axes[0][0]
                    #ax.set_title('non-bonded')
                    onset_min, onset_max = (np.inf, 0)
                    for i, cg_beadtype_pair in enumerate(itertools.combinations_with_replacement(
                        cg.core.gen_cg_beadtypes(cg_problem['fg-topology'], cg_problem['mapping']).keys(), 2
                    )):
                        ia_name = '-'.join(sorted(cg_beadtype_pair))
                        #print(ia_name)
                        dist_tgt_file = f"{sp}/{ia_name}.dist.tgt"
                        dist_tgt_r, dist_tgt_g, dist_tgt_flag = readin_table(dist_tgt_file)
                        line_tgt, = ax.plot(dist_tgt_r, dist_tgt_g, linestyle='-', label=ia_name)
                        if show_intra:
                            dist_intra_tgt_file = f"{sp}/{ia_name}.dist-intra.tgt"
                            dist_intra_tgt_r, dist_intra_tgt_g, dist_intra_tgt_flag = readin_table(dist_intra_tgt_file)
                            line_intra_tgt, = ax.plot(dist_intra_tgt_r, dist_intra_tgt_g, linestyle='-', color='darkred')
                        if min(np.nonzero(dist_tgt_g)[0]) < onset_min:
                            onset_min = min(np.nonzero(dist_tgt_g)[0])
                        if min(np.nonzero(dist_tgt_g)[0]) > onset_max:
                            onset_max = min(np.nonzero(dist_tgt_g)[0])
                        if show_step0tgt:
                            dist_tgt0_file = f"step_000/{sp}/{ia_name}.dist.tgt"
                            dist_tgt0_r, dist_tgt0_g, dist_tgt0_flag = readin_table(dist_tgt0_file)
                            line_tgt0, = ax.plot(dist_tgt0_r, dist_tgt0_g, linestyle='--', color=line_tgt.get_color())
                        if show_step1new:
                            dist_new1_file = f"step_001/{sp}/{ia_name}.dist.new"
                            dist_new1_r, dist_new1_g, dist_new1_flag = readin_table(dist_new1_file)
                            line_new1, = ax.plot(dist_new1_r, dist_new1_g, linestyle=':', color=line_tgt.get_color())
                    if show_onset:
                        ax.set_xlim(0.9 * dist_tgt_r[onset_min], 1.1 * dist_tgt_r[onset_max])
                        ax.set_ylim(1e-6, 1)
                        ax.set_yscale('log')
                    else:
                        ax.set_xlim(0)
                    ax.set_xlabel(r'$r$ in nm')
                    ax.set_ylabel(r'$g$')
                    ax.set_ylabel(r'$g$')
                    ax.legend(frameon=False, loc='upper right', ncol=4)
                # bonds
                ia_bonded = ia_to_show.copy()
                ia_bonded.remove('non-bonded')
                for i, ia in enumerate(ia_bonded):
                    ax = axes[0][i+1]
                    ax.set_title(ia)
                    dist_files = sorted(glob.glob(f"{sp}/{ia[:-1]}*.dist.tgt"))
                    for i, dist_file in enumerate(dist_files):
                        #print(i, dist_file)
                        ia_name = dist_file.split('/')[-1].split('.')[0]
                        dist_r, dist_p, dist_flag = readin_table(dist_file)
                        line_tgt, = ax.plot(dist_r, dist_p, label=ia_name)
                        if show_step1new:
                            dist_new1_file = f"step_001/{sp}/{ia_name}.dist.new"
                            dist_new1_r, dist_new1_g, dist_new1_flag = readin_table(dist_new1_file)
                            line_new1, = ax.plot(dist_new1_r, dist_new1_g, linestyle=':', color=line_tgt.get_color())
                    ax.set_ylabel(r'$p$')
                    if len(dist_files) > 0:
                        ax.legend(frameon=False, loc='upper right', ncol=4)
                plt.show()
            
#plot_tgt_votca(ia_to_show=['non-bonded', 'bonds', 'angles', 'dihs'])
#plot_tgt_votca(ia_to_show=['non-bonded'], show_intra=True)
#plot_tgt_votca(ia_to_show=['non-bonded', 'bonds'], show_step1new=True)
plot_tgt_votca(ia_to_show=['non-bonded'], show_onset=True, show_step0tgt=True)
#plot_tgt_votca(ia_to_show=['non-bonded'], show_step1new=True)
#plot_tgt_votca(ia_to_show=['non-bonded', 'bonds', 'angles', 'dihs'], show_step1new=True)

## show initial guess

In [ ]:
def show_initial_guess(ia_to_show=['non-bonded', 'bonds', 'angles', 'dihedrals']):
    
    #fg_sys_types_to_do = fg_sys_types
    fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['neon-argon']}
    
    states_to_do = states
    #states_to_do = {key: states[key] for key in ['pure']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['1bead']}
    
    votca_settings_to_do = votca_settings
    #votca_settings_to_do = {key: votca_settings[key] for key in ['hncnt-hncinitshort', 'hncnt-hncinit']}
    
    for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
        fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=True):
        
        fig, axes = plt.subplots(nrows=1, ncols=len(ia_to_show), figsize=[16, 3], constrained_layout=True, squeeze=False)
        
        working_dir = os.path.join(cg_problem['folder'])
        with WorkingDir(working_dir):
            # non-bonded
            if 'non-bonded' in ia_to_show:
                ax = axes[0][0]
                ax.set_title('non-bonded')
                min_pot = 0
                for i, cg_beadtype_pair in enumerate(itertools.combinations_with_replacement(
                    cg.core.gen_cg_beadtypes(cg_problem['fg-topology'], cg_problem['mapping']).keys(), 2
                )):
                    ia_name = '-'.join(sorted(cg_beadtype_pair))
                    #print(ia_name)
                    pot_file = f"step_000/{ia_name}.pot.new"
                    pot_r, pot_U, pot_flag = readin_table(pot_file)
                    line_tgt, = ax.plot(pot_r, pot_U, linestyle='-', label=ia_name)
                    if min(pot_U) < min_pot:
                        min_pot = min(pot_U)
                    cut_off = (cg_problem['votca-settings']['inverse']['gauss_newton']['cut_off']
                               if 'gauss_newton' in cg_problem['votca-settings']['inverse']
                               else cg_problem['votca-settings']['inverse']['newton']['cut_off'])
                ax.set_xlim(0, cut_off+0.1)
                #ax.set_ylim(1.05 * min_pot, -2.05 * min_pot)
                ax.set_ylim(1.05 * min_pot, 100)
                ax.axhline(0, linestyle=':', color='grey')
                #ax.set_xlabel(r'$r$ in nm')
                ax.set_ylabel(r'$U$ in kJ/mol')
                ax.legend(loc='upper right', frameon=False)
            # bonds
            for i, ia in enumerate(ia_to_show):
                ax = axes[0][i]
                ax.set_title(ia)
                pot_files = sorted(glob.glob(f"step_000/{ia[:-1]}-*.pot.new"))
                for i, pot_file in enumerate(pot_files):
                    ia_name = pot_file.split('/')[-1].split('.')[0]
                    pot_r, pot_U, pot_flag = readin_table(pot_file)
                    ax.plot(pot_r, pot_U, label=ia_name)
                    ax.set_ylim(0, 50)
                    ax.set_ylabel(r'$U$ in kJ/mol')
                    ax.legend(frameon=False)
        plt.show()

#show_initial_guess(ia_to_show=['non-bonded', 'bonds', 'angles', 'dihedrals'])
show_initial_guess(ia_to_show=['non-bonded'])

## show potential update

In [ ]:
def show_potential_update(ia_to_show=['non-bonded'], step=1, compare_votca_settings=False):
    step_dir = f"step_{step:03d}"
    
    #fg_sys_types_to_do = fg_sys_types
    fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['octane']}
    
    states_to_do = states
    #states_to_do = {key: states[key] for key in ['xrange3', 'Trange3', 'Trange3high']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['1bead']}
    
    #votca_settings_to_do = votca_settings
    votca_settings_to_do = {key: votca_settings[key] for key in ['hncn-ibiintra-hncinit', 'hncnt-ibiintra-hncinit']}
    
    for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
        fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=True):
        
        if (not compare_votca_settings) or v == 0:
            fig, axes = plt.subplots(nrows=1, ncols=len(ia_to_show), figsize=[10, 2], constrained_layout=True, squeeze=False)
            color_ia_dict = {}
        
        working_dir = os.path.join(cg_problem['folder'])
        with WorkingDir(working_dir):
            # non-bonded
            if 'non-bonded' in ia_to_show:
                ax = axes[0][0]
                ax.set_title('non-bonded')
                min_pot = 0
                for i, cg_beadtype_pair in enumerate(itertools.combinations_with_replacement(
                    cg.core.gen_cg_beadtypes(cg_problem['fg-topology'], cg_problem['mapping']).keys(), 2
                )):
                    ia_name = '-'.join(sorted(cg_beadtype_pair))
                    #print(ia_name)
                    pot_file = f"{step_dir}/{ia_name}.dpot.new"
                    pot_r, pot_U, pot_flag = readin_table(pot_file)
                    linestyle = ['-', '--', '-.', ':'][v%4] if compare_votca_settings else '-'
                    label = (ia_name if v == 0 else None) if compare_votca_settings else ia_name
                    color = color_ia_dict[ia_name] if ia_name in color_ia_dict else None
                    line, = ax.plot(pot_r, pot_U, linestyle=linestyle, label=label, color=color)
                    if ia_name not in color_ia_dict:
                        color_ia_dict[ia_name] = line.get_color()
                    if min(pot_U) < min_pot:
                        min_pot = min(pot_U)
                    cut_off = (cg_problem['votca-settings']['inverse']['iie']['cut_off']
                               if 'iie' in cg_problem['votca-settings']['inverse']
                               else cg_problem['votca-settings']['non-bonded']['max'])
                ax.set_xlim(0, cut_off+0.1)
                #ax.set_ylim(1.05 * min_pot, -2.05 * min_pot)
                #ax.set_ylim(1.05 * min_pot, 3)
                ax.set_ylim(-15, 2)
                ax.axhline(0, linestyle=':', color='grey')
                #ax.set_xlabel(r'$r$ in nm')
                ax.set_ylabel(r'$\Delta U$ in kJ/mol')
                ax.legend(loc='upper right', frameon=False)
                #ax.grid()
                    
        if (not compare_votca_settings) or votca_setting_key == list(votca_settings_to_do.keys())[-1]:
            plt.show()

show_potential_update(ia_to_show=['non-bonded'], compare_votca_settings=True)

## show first step Jacobian

In [ ]:
def load_jac_ibi(cg_problem, step=1):
    """Load IBI Jacobian for all interactions."""

    def load_jacpart_ibi(g_tgt, g_k, beta):
        """Load Jacobian part for one interaction."""
        with np.errstate(invalid='ignore', divide='ignore'):
            ibi_diag = np.nan_to_num(1 / (1/beta * np.log(g_tgt/g_k) / (g_k - g_tgt)))
            ibi_jacpart = np.nan_to_num(np.diag(ibi_diag))
        return ibi_jacpart

    if cg_problem['state']['type'] == 'single':
        n_nonbonded = sum(1 for _ in cg.gen_beadtype_pairs(cg_problem))
        n_gridpoints = (cg_problem['votca-settings']['non-bonded']['max']
                      - cg_problem['votca-settings']['non-bonded']['min']) / cg_problem['votca-settings']['non-bonded']['step'] 
        n_gridpoints = int(n_gridpoints) + 1  # boundary is included in votca
        n_jac = n_nonbonded * n_gridpoints
        ibi_jac = np.zeros((n_jac, n_jac))
        for i, cg_beadtype_pair in enumerate(cg.gen_beadtype_pairs(cg_problem)):
            nb_name = '-'.join(cg_beadtype_pair)
            with WorkingDir(cg_problem['folder']):
                r, g_k, _ = readin_table(f'step_{step:03d}/{nb_name}.dist.new')
                r, g_tgt, _ = readin_table(f'{nb_name}.dist.tgt')
            beta = 1 / oconst.k_gro / cg_problem['state']['temperature']
            jac_part = load_jacpart_ibi(g_tgt, g_k, beta)
            jac_slice = slice(i*n_gridpoints, (i+1)*n_gridpoints)  # same for row and column
            ibi_jac[jac_slice, jac_slice] = jac_part
    else:
        raise Exception('not implemented')
    return ibi_jac

In [ ]:
def load_jac_imc(cg_problem, fg_sys_type_key, step=1):
    """Load IMC Jacobian for all interactions."""
    
    def gen_dudg_from_imc_matrix(A, S, indices, volume, N_n, temperature):
        first_index = list(indices.values())[0]
        r = S[first_index[0]:first_index[1], 0]
        Delta_r = r[1] - r[0]
        beta = 1 / oconst.k_gro / temperature
        #print(n, N, Delta_r, V, beta)
        dudg = np.zeros_like(A)
        with np.errstate(divide='ignore', invalid='ignore'):
            for (in1, index1), (in2, index2) in itertools.product(indices.items(), indices.items()):
                dudg[index1[0]:index1[1], index2[0]:index2[1]] = beta * 1 / (
                    (N_n)**2 / volume / 2 * 4 * np.pi *Delta_r
                ) * np.diag(1/r**2) @ A[index1[0]:index1[1], index2[0]:index2[1]]
        dudg = np.delete(dudg, [index[0] for index in indices.values()], axis=0)
        dudg = np.delete(dudg, [index[0] for index in indices.values()], axis=1)
        return dudg

    if cg_problem['state']['type'] == 'single':
        statepoint = gen_statepoints(cg_problem['state'])[0]
        n_nonbonded = len(list(cg.gen_beadtype_pairs(cg_problem)))
        n_gridpoints = (cg_problem['votca-settings']['non-bonded']['max']
                      - cg_problem['votca-settings']['non-bonded']['min']) / cg_problem['votca-settings']['non-bonded']['step'] 
        n_gridpoints = int(n_gridpoints) + 1  # boundary is included in votca
        n_jac = n_nonbonded * n_gridpoints
        step_dir = f"step_{step:03d}"
        imc_group_name = cg_problem['votca-settings']['non-bonded']['inverse']['imc']['group']
        matrix_file = os.path.join(step_dir, f"{imc_group_name}.gmc")
        index_file = os.path.join(step_dir, f"{imc_group_name}.idx")
        dist_file = os.path.join(step_dir, f"{imc_group_name}.imc")
        with WorkingDir(cg_problem['folder']):
            A = np.loadtxt(matrix_file)
            S = np.loadtxt(dist_file)
            indices = {}
            with open(index_file, 'r') as f:
                for line in f.readlines():
                    interaction, start_end = line.split()
                    start, end = map(int, start_end.split(':'))
                    start -= 1  # votca counts from 1, i count from 0
                    indices[interaction] = (start, end)
            if cg_problem['cg-sys-type']['md-settings']['md-program'] == 'gromacs':
                volume = np.prod(gt.gro.get_box("conf.gro"))
            else:
                volume = {
                    'mwater-argon-1solute-unity+mw-imc-ibiintra-hncinit': 63.334001,
                }[cg_problem['name']]
        T = statepoint['temperature']
        # TODO, N should be a list for mixtures, obtain from states
        N_n = {  # N * n
            'ethanol-water': 1000,
            'neon-argon': 1000,
            'naphtalene': 4000,
            'water-spc': 2000,
            'methanol': 2000,
            'octane': 2000,
            'mwater-argon': 2000,
        }[fg_sys_type_key]
        imc_jac = gen_dudg_from_imc_matrix(A, S, indices, volume, N_n, T)
    else:
        raise Exception('not implemented')
    return imc_jac

In [ ]:
def load_jac_iie(cg_problem, step=1, remove_redundant=True):
    """Load IMC Jacobian for all interactions."""
    if cg_problem['state']['type'] == 'single':
        step_dir = f"step_{step:03d}"
        with WorkingDir(cg_problem['folder']):
            if cg_problem['votca-settings']['inverse']['iie']['method'] == 'newton':
                data = np.load(f"{step_dir}/newton_update-calc_jacobian.npz", allow_pickle=True)
            else:
                data = np.load(f"{step_dir}/gauss_newton_update-calc_jacobian.npz", allow_pickle=True)
            _, jac_inv_mat = data['return_value']
            # number of atom types
            n_t = len(data['settings'][()]['rhos'])
            # number of interactions
            n_i = int(n_t**2)
            n_ir = (n_t * (n_t + 1)) // 2  # without equivalents, i.e. reduced
            # number of grid points in r
            n_r = len(data['input_arrays'][()]['r'])
                        
            # generate inverse jacobian as a 2D matrix
            # this is the form in which the inverse is taken
            jac_inv_mat_2D = csg.make_matrix_2D(jac_inv_mat)
            #jac_mat_2D = csg.make_matrix_2D(jac_mat)
            jac_mat_2D = np.linalg.inv(np.nan_to_num(jac_inv_mat_2D, neginf=-1e30, posinf=1e30))
            jac_mat = csg.make_matrix_4D(jac_mat_2D, n_r, n_r, n_i, n_i)
            
            # reduce (add) columns which are derivatives with respect to the same Δg, e.g. Δg_ab and Δg_ba
            jac_red = jac_mat.copy()
            identical_cols = []
            for alpha in range(n_t):
                for beta in range(n_t):
                    if beta < alpha:
                        identical_cols.append((n_t*alpha + beta, n_t*beta + alpha))
            for col1, col2 in identical_cols:
                jac_red[:, :, :, col1] += jac_red[:, :, :, col2]
                jac_red = np.delete(jac_red, [col2], axis=-1)
            # afterwards reduce (add) rows, which produce the same Δu, e.g. e.g. Δu_ab and Δu_ba, but iie thinks it adds them individually, so we have to sum!
            for col1, col2 in identical_cols:  # actually rows
                jac_red[:, :, col1, :] += jac_red[:, :, col2, :]
                jac_red = np.delete(jac_red, [col2], axis=-2)
            # make 2D
            jac_mat_2D_red = csg.make_matrix_2D(jac_red)
            
            # remove redundant rows
            #to_remove = []
            #for beta in range(n_t):
                #for alpha in range(n_t):
                    #if beta < alpha:
                        #for k in range(n_r):
                            #to_remove.append((n_t*alpha + beta)*n_r + k)
                    #else:
                        #pass
                        # remove after cut_off
                        #for k in range(n_r, n_r):
                            #to_remove.append((n_t*alpha + beta)*n_r + k)
            #jac_mat_2D_red = jac_mat_2D
            #print(to_remove)
            #jac_mat_2D_red = np.delete(jac_mat_2D, to_remove, axis=-1)
            #jac_mat_2D_red = np.delete(jac_mat_2D_red, to_remove, axis=-2)

    else:
        step_dir = f"step_{step:03d}"
        with WorkingDir(cg_problem['folder']):
            data = np.load(f"{step_dir}/multistate_gauss_newton_update-calc_multistate_jacobian.npz", allow_pickle=True)
            jac_mat = data['return_value']
            jac_mat_2D = csg.make_matrix_2D(jac_mat)
            # HACK
            jac_mat_2D_red = jac_mat_2D
    if remove_redundant:
        return jac_mat_2D_red
    else:
        return jac_mat_2D

In [ ]:
vlim_dict = collections.defaultdict(
    lambda: 2e-2, 
    naphtalene=2e-2,
    methanol=2e-2,
)

In [ ]:
def show_jacobians(difference_of_two=False):
    #fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['water-spc']}
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['mwater-argon']}
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['neon-argon']}
    fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['hexane']}
    
    states_to_do = states
    #states_to_do = {key: states[key] for key in ['xrange3', 'Trange3', 'Trange3high']}
    #states_to_do = {key: states[key] for key in ['pure']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['1bead']}
    
    #votca_settings_to_do = votca_settings
    votca_settings_to_do = {key: votca_settings[key] for key in [
        'imco-altibiintra',
        'imcot-altibiintra',
        'hncn-altibiintra',
    ]}
    
    jac_diff = None
    for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
        fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=True):
        try:
            if cg_problem['votca-settings']['inverse']['method'] == 'ibi':
                jac = load_jac_ibi(cg_problem)
                fig, ax = plt.subplots()
                ax.plot(np.diagonal(jac))
                plt.show()
            elif cg_problem['votca-settings']['inverse']['method'] in ['imc', 'iie']:
                if cg_problem['votca-settings']['inverse']['method'] == 'imc':
                    jac = load_jac_imc(cg_problem, fg_sys_type_key)
                elif cg_problem['votca-settings']['inverse']['method'] == 'iie':
                    jac = load_jac_iie(cg_problem, remove_redundant=True)
                # show whole Jacobian
                fig, ax = plt.subplots(figsize=(6, 6), dpi=150)
                mappable = ax.imshow(jac, interpolation='none', vmin=-vlim_dict[fg_sys_type_key], vmax=vlim_dict[fg_sys_type_key], cmap='RdBu_r')
                #fig.colorbar(mappable, fraction=0.04)
                ax.get_xaxis().set_ticks([])
                ax.get_yaxis().set_ticks([])
                plt.show()
                # show diagonal of Jacobian
                fig, ax = plt.subplots(figsize=(6, 1), dpi=150)
                ax.plot(np.diag(jac))
                plt.show()
                if difference_of_two:
                    if jac_diff is None:
                        jac_diff = jac
                    else:
                        jac_diff = jac_diff - jac
            else:
                print('.. not implemented ..')
                # TODO, get it from numpy dump
                continue
        except OSError:
            print('.. no data found ..')
            raise
            
        #print(jac.shape)
        #print(np.min(jac))
        #print(np.max(jac))
        #print(np.count_nonzero(jac - np.diag(np.diagonal(jac))))
        
    if difference_of_two:
        print('difference 1 - 2:')
        fig, ax = plt.subplots(figsize=(2, 6), dpi=150)
        mappable = ax.imshow(jac_diff, interpolation='none', vmin=-vlim_dict[fg_sys_type_key], vmax=vlim_dict[fg_sys_type_key], cmap='RdBu_r')
        #fig.colorbar(mappable, fraction=0.04)
        ax.get_xaxis().set_ticks([])
        ax.get_yaxis().set_ticks([])
        plt.show()
        # show diagonal of Jacobian
        fig, ax = plt.subplots(figsize=(6, 1), dpi=150)
        ax.plot(np.diag(jac_diff))
        plt.show()

show_jacobians(difference_of_two=True)

## show RDF convergence

In [ ]:
def show_rdf_convergence(plot_sum=True):
    #fg_sys_types_to_do = fg_sys_types
    fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['hexane']}
    
    states_to_do = states
    #states_to_do = {key: states[key] for key in ['pure']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
    
    #votca_settings_to_do = votca_settings
    votca_settings_to_do = {key: votca_settings[key] for key in [
        'ibi-altibiintra',
        'imco-altibiintra',
        'imcot-altibiintra',
        'hncn-altibiintra',
        #'phncgnt-altibiintra',
        #'PEhncgnt-altibiintra',
        #'KBIhncgnt-altibiintra',
        #'KBIphncgnt-altibiintra',
    ]}
    
    ia_to_show = 'all'
    #ia_to_show = ['AR-AR']
    
    mpl_rc_local = {'legend.handlelength': 2.0}
    with plt.rc_context({**mpl_rc_global, **mpl_rc_local}):
        
        # groupby fg, state, mapping
        for (fg_sys_type_key, state_key, mapping_key), group in itertools.groupby(cg_setup_generator(
            fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=False),
                                                                                  lambda x: (x[1], x[2], x[3])):

            # create figure
            fig, ax = plt.subplots(nrows=1, ncols=1, figsize=[3.2, 2.1], constrained_layout=True, dpi=300)
            fig.set_constrained_layout_pads(w_pad=0.01, h_pad=0.01, hspace=0., wspace=0.)

            # iterate in group
            print(fg_sys_type_key, state_key, mapping_key)
            for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in group:
                print(' ', votca_setting_key)

                # stuff for label, color, linestyle
                init_method = cg_problem['votca-settings']['inverse']['initial_guess']['method']
                label = label_of_method[votca_setting_key.split('-')[0]]
                color = color_of_method[votca_setting_key.split('-')[0]]
                linestyle = linestyle_of_method[votca_setting_key.split('-')[0]]

                # iterate files
                working_dir = os.path.join(cg_problem['folder'])
                with WorkingDir(working_dir):
                    err_g_sum = 0
                    for i, cg_beadtype_pair in enumerate(cg.gen_beadtype_pairs(cg_problem)):
                        ia_name = '-'.join(sorted(cg_beadtype_pair))
                        if ia_to_show != 'all' and ia_name not in ia_to_show:
                            continue
                        # load tgt
                        try:
                            if os.path.exists(f"step_001/{ia_name}.dist.tgt"):
                                dist_tgt_r, dist_tgt_g, _ = readin_table(f"step_001/{ia_name}.dist.tgt")
                            else:
                                dist_tgt_r, dist_tgt_g, _ = readin_table(f"step_002/{ia_name}.dist.tgt")
                        except:
                            print(f".. could not load {ia_name}.dist.tgt, continue ..")
                            empty = mpl.patches.Rectangle((0,0), 1, 1, fill=False, edgecolor='none', visible=False)
                            continue
                        # load new
                        dist_files = sorted(glob.glob(f"step_*/{ia_name}.dist.new"))
                        err_g = []
                        for dist_file in dist_files:
                            step = int(re.search('step_(\d+)', dist_file).group(1))
                            try:
                                dist_new_r, dist_new_g, _ = readin_table(dist_file)
                            except:
                                print(f".. could not load {dist_file} ..")
                            cut_off = cg_problem['functional-votca-settings-input']['cut']
                            cut, _ = csg.calc_slices(dist_new_r, cut_off)
                            err_g.append((step, np.sqrt(1/max(dist_new_r[cut]) * np.trapz(x=dist_new_r[cut], y=(dist_new_g - dist_tgt_g)[cut]**2))))
                        if not plot_sum:
                            label = label if i == 0 else None
                            line, = ax.plot(*np.array(err_g).T, label=label, color=color, linestyle=linestyle)
                        # add to sum
                        err_g_sum += np.array(err_g)[:, 1]
                        steps = np.array(err_g)[:, 0]
                        
                    if plot_sum:
                        line, = ax.plot(steps, err_g_sum, label=label, color=color, linestyle=linestyle, marker='.', markersize=3.5)

            # after group iteration
            ax.set_xlabel('iteration')
            #ax.set_ylabel(r'$\sqrt{\frac{1}{r_c} \int_0^{r_c} (g - g_\mathrm{tgt})^2 dr}$')
            if plot_sum:
                ax.set_ylabel(r'$\Sigma_i \sigma(g_i)$')
            else:
                ax.set_ylabel(r'$\sigma(g)$')
            ax.set_yscale('log')
            ax.set_xlim(0, 40)
            #ax.set_ylim(None, 1e-1)
            #ax.set_xticks([0, 5, 10, 15, 20])
            ax.legend(loc='upper right')
            plt.show()

#show_rdf_convergence(plot_sum=False)
show_rdf_convergence(plot_sum=True)

## show potential update convergence

In [ ]:
def show_potential_update_convergence(show_legend=True):
    #fg_sys_types_to_do = fg_sys_types
    fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['neon-argon']}
    
    states_to_do = states
    #states_to_do = {key: states[key] for key in ['pure']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
    
    #votca_settings_to_do = votca_settings
    votca_settings_to_do = {key: votca_settings[key] for key in [
        'ibi-ibiintra',
        'imco-ibiintra',
        'imcot-ibiintra',
        'hncn-ibiintra',
        'hncnt-ibiintra',
    ]}
    
    ia_to_show = 'all'
    #ia_to_show = ['AR-MW']
    
    mpl_rc_local = {'legend.handlelength': 4.0}
    with plt.rc_context({**mpl_rc_global, **mpl_rc_local}):
        
        # groupby fg, state, mapping
        for (fg_sys_type_key, state_key, mapping_key), group in itertools.groupby(cg_setup_generator(
            fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=False),
                                                                                  lambda x: (x[1], x[2], x[3])):

            # create figure
            fig, ax = plt.subplots(nrows=1, ncols=1, figsize=[3.2, 2.1], constrained_layout=True, dpi=300)
            line_label_dict = {}

            # iterate in group
            print(fg_sys_type_key, state_key, mapping_key)
            for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in group:
                print(' ', votca_setting_key)

                # stuff for label, color, linestyle
                init_method = cg_problem['votca-settings']['inverse']['initial_guess']['method']
                label = label_of_method[votca_setting_key.split('-')[0]]
                color = color_of_method[votca_setting_key.split('-')[0]]
                linestyle = linestyle_of_method[votca_setting_key.split('-')[0]]

                # iterate files
                working_dir = os.path.join(cg_problem['folder'])
                with WorkingDir(working_dir):
                    min_pot = 0
                    for i, cg_beadtype_pair in enumerate(cg.gen_beadtype_pairs(cg_problem)):
                        ia_name = '-'.join(sorted(cg_beadtype_pair))
                        if ia_to_show != 'all' and ia_name not in ia_to_show:
                            continue
                        # load tgt
                        try:
                            dist_tgt_r, dist_tgt_g, _ = readin_table(f"step_001/{ia_name}.dist.tgt")
                        except:
                            print(f".. could not load {ia_name}.dist.tgt, continue ..")
                            empty = mpl.patches.Rectangle((0,0), 1, 1, fill=False, edgecolor='none', visible=False)
                            line_label_dict[(label, init_method)] = (empty, label)  # first row, second column
                            continue
                        # load new
                        pot_files = sorted(glob.glob(f"step_*/{ia_name}.pot.cur"))
                        pot_std = []
                        for pot_file_a, pot_file_b in zip(pot_files[:-1], pot_files[1:]):
                            step = int(re.search('step_(\d+)', pot_file_b).group(1))
                            try:
                                pot_cur_r_a, pot_cur_u_a, _ = readin_table(pot_file_a)
                                pot_cur_r_b, pot_cur_u_b, _ = readin_table(pot_file_b)
                            except:
                                print(f".. could not load {pot_file_a} or {pot_file_b} ..")
                            np.testing.assert_allclose(pot_cur_r_a, pot_cur_r_b)
                            np.testing.assert_allclose(pot_cur_r_a, dist_tgt_r)
                            pot_std.append((step, np.sqrt(1/max(pot_cur_r_a) * np.trapz(x=pot_cur_r_a, y=dist_tgt_g * (pot_cur_u_b - pot_cur_u_a)**2))))
                        if len(pot_std) == 0:
                            print('.. no data, skipping ..')
                        else:
                            line, = ax.plot(*zip(*pot_std), label=label, color=color, linestyle=linestyle)
                            line_label_dict[(label, init_method)] = (line, label)  # first row, second column

            # after group iteration
            ax.set_xlabel('step')
            ax.set_ylabel(r'$\Delta u$')
            ax.set_yscale('log')
            #ax.set_xlim(0, 20)
            ax.set_ylim(None, 4e-0)
            init_methods = uniquify((im for _, im in line_label_dict.keys()))
            label_list = uniquify((label for label, _ in line_label_dict.keys()))
            if show_legend:
                empty = mpl.patches.Rectangle((0,0), 1, 1, fill=False, edgecolor='none',
                                              visible=False)
                leg = fig.legend([tuple([(line_label_dict[(label, init_method)][0] if (label, init_method) in line_label_dict.keys() else empty) for init_method in init_methods])
                                  for label in label_list], label_list, handler_map={tuple: mpl.legend_handler.HandlerTuple(ndivide=2, pad=0.5)},
                                 title=r'$\text{BI}\quad\text{HNC}$', loc=(0.60, 0.5))
                leg.get_title().set_position((-110, 0))
            plt.show()

show_potential_update_convergence(show_legend=True)

## show last potential

In [ ]:
def show_last_potential(show_legend=True):
    mpl_rc_local = {'legend.handlelength': 2.0}
    with plt.rc_context({**mpl_rc_global, **mpl_rc_local}):
        
        #fg_sys_types_to_do = fg_sys_types
        #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['neon-argon']}
        fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['hexane']}
        
        mappings_to_do = mappings
        #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
        
        states_to_do = states
        #states_to_do = {key: states[key] for key in ['pure']}
        
        votca_settings_to_do = {key: votca_settings[key] for key in [
            #'ibi-ibiintra',
            #'imco-ibiintra',
            #'imcot-ibiintra',
            'imco-altibiintra',
            'imcot-altibiintra',
            #'imcot-ibiintra',
            #'hncn-ibiintra',
            #'hncn-altibiintra',
            #*[f'hncgntco{cut_off_10:02d}-altibiintra' for cut_off_10 in range(5, 12, 2)]
        ]}
        
        ia_to_show = 'all'
        #ia_to_show = ['AR-MW']
        #ia_to_show = ['AR-MW', 'AR-AR']

        # groupby fg, state, mapping
        for (fg_sys_type_key, state_key, mapping_key), group in itertools.groupby(cg_setup_generator(
            fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=True),
                                                                                  lambda x: (x[1], x[2], x[3])):

            # create figure
            fig, ax = plt.subplots(nrows=1, ncols=1, figsize=[4, 2.3], constrained_layout=True, dpi=300)

            # iterate in group
            print(fg_sys_type_key, state_key, mapping_key)
            for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in group:
                print(' ', votca_setting_key)

                init_method = cg_problem['votca-settings']['inverse']['initial_guess']['method']
                label = label_of_method[votca_setting_key.split('-')[0]]
                color = color_of_method[votca_setting_key.split('-')[0]]
                linestyle = linestyle_of_method[votca_setting_key.split('-')[0]]

                # plot last potential
                working_dir = os.path.join(cg_problem['folder'])
                with WorkingDir(working_dir):
                    min_pot = 0
                    # iterate interactions
                    for i, cg_beadtype_pair in enumerate(cg.gen_beadtype_pairs(cg_problem, return_dict=True)):
                        ia_name = '-'.join(sorted((key for key, value in cg_beadtype_pair)))
                        if ia_to_show != 'all' and ia_name not in ia_to_show:
                            continue

                        print(ia_name)

                        # load new
                        pot_files = sorted(glob.glob(f"step_???/{ia_name}.pot.cur"))
                        pot_file = pot_files[-1]  # only last one
                        step = int(re.search('step_(\d+)', pot_file).group(1)) - 1  # -1 because we use .pot.cur
                        try:
                            pot_new_r, pot_new_u, _ = readin_table(pot_file)
                        except:
                            print(f".. could not load {pot_file} ..")
                            continue
                        print(step)
                        label = label if i == 0 else None
                        line, = ax.plot(pot_new_r, pot_new_u, label=label, color=color, linestyle=linestyle)

            # plot tgt potentials
            # iterate interactions
            for i, cg_beadtype_pair in enumerate(cg.gen_beadtype_pairs(cg_problem, return_dict=True)):
                ia_name = '-'.join(sorted((key for key, value in cg_beadtype_pair)))
                if ia_to_show != 'all' and ia_name not in ia_to_show:
                    continue
                print(cg_beadtype_pair)
                if mapping_key.startswith('unity'):  # otherwise there can be no known target potential
                    fg_bead1_name = cg_problem['mapping']['moltypes'][cg_beadtype_pair[0][1]['map_mol_name']][cg_beadtype_pair[0][0]]['fg-beads'][0]
                    fg_bead2_name = cg_problem['mapping']['moltypes'][cg_beadtype_pair[1][1]['map_mol_name']][cg_beadtype_pair[1][0]]['fg-beads'][0]
                    fg_bead1 = cg_problem['fg-topology']['moltypes'][cg_beadtype_pair[0][1]['map_mol_name']]['beads'][fg_bead1_name]
                    fg_bead2 = cg_problem['fg-topology']['moltypes'][cg_beadtype_pair[1][1]['map_mol_name']]['beads'][fg_bead2_name]
                    r = pot_new_r
                    cut_off = cg_problem['functional-votca-settings-input']['cut']
                    with np.errstate(divide='ignore', invalid='ignore'):
                        pot_tgt_u = calc_potential(
                            r,
                            fg_bead1,
                            fg_bead2,
                            combination_rule[fg_sys_types['neon-argon']['topology']['ff-key']], cut_off,
                            cg_problem['fg-topology']['non-mixing-rule-factors'] if 'non-mixing-rule-factors' in cg_problem['fg-topology'] else {},
                            potential_shift=True)
                        ax.plot(r, pot_tgt_u, label='target', color='black', linestyle=':')

            ax.set_xlabel(r'$r$')
            ax.set_ylabel(r'$u(r)$')
            ax.legend()
            plt.xlim(0.25, 1.25)
            #plt.ylim(-0.1, 0.1)
            plt.ylim(-1.5, 0.8)
            plt.show()

show_last_potential()

## show last RDF

In [ ]:
def show_last_rdf(show_target=True):
    mpl_rc_local = {
        'legend.handlelength': 1.2,
        'legend.handletextpad': 0.5,
        'legend.columnspacing': 1.4,
    }
    with plt.rc_context({**mpl_rc_global, **mpl_rc_local}):
        
        #fg_sys_types_to_do = fg_sys_types
        fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['hexane']}
        
        mappings_to_do = mappings
        #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
        
        states_to_do = states
        #states_to_do = {key: states[key] for key in ['pure']}
        
        votca_settings_to_do = {key: votca_settings[key] for key in [
            'hncgnt-altibiintra',
            'phncgnt-altibiintra',
            'PEhncgnt-altibiintra',
            'KBIhncgnt-altibiintra',
            'KBIphncgnt-altibiintra',
            'PEphncgnt-altibiintra',
            #*[f'hncgntco{cut_off_10:02d}-altibiintra' for cut_off_10 in range(5, 12, 2)]
            #*[f'hncgntco{cut_off_10:02d}-altibiintra' for cut_off_10 in range(5, 12, 3)]
            #*[f'hncgntco{cut_off_10:02d}-altibiintra' for cut_off_10 in [5, 7, 9]],
            #'hncn-altibiintra',
            #*[f'hncgntco{cut_off_10:02d}-altibiintra' for cut_off_10 in [5, 6, 7]]
        ]}
        
        ia_to_show = 'all'
        #ia_to_show = ['AR-MW']
        #ia_to_show = ['AR-MW', 'AR-AR']

        # groupby fg, state, mapping
        for (fg_sys_type_key, state_key, mapping_key), group in itertools.groupby(cg_setup_generator(
            fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=False),
                                                                                  lambda x: (x[1], x[2], x[3])):

            # create figure
            fig, axes = plt.subplots(nrows=3, ncols=1, figsize=[3.2, 2.0], constrained_layout=True, dpi=300, sharex='col')

            # iterate in group
            print(fg_sys_type_key, state_key, mapping_key)
            for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in group:
                print(' ', votca_setting_key)

                init_method = cg_problem['votca-settings']['inverse']['initial_guess']['method']
                label = label_of_method[votca_setting_key.split('-')[0]]
                color = color_of_method[votca_setting_key.split('-')[0]]
                linestyle = linestyle_of_method[votca_setting_key.split('-')[0]]

                # plot last potential
                working_dir = os.path.join(cg_problem['folder'])
                with WorkingDir(working_dir):
                    min_pot = 0
                    # iterate interactions
                    for i, cg_beadtype_pair in enumerate(cg.gen_beadtype_pairs(cg_problem, return_dict=True)):
                        ia_name = '-'.join(sorted((key for key, value in cg_beadtype_pair)))
                        if ia_to_show != 'all' and ia_name not in ia_to_show:
                            continue
                        
                        # label
                        if v == 0:
                            axes[i].text(0.75, 0.15, ia_name, transform=axes[i].transAxes)
                        
                        # RDF target
                        if show_target and v == 0:
                            label_tgt = 'tgt' if i == 0 else None
                            dist_tgt_r, dist_tgt_g, _ = readin_table(f"{ia_name}.dist.tgt")
                            axes[i].plot(dist_tgt_r, dist_tgt_g, label=label_tgt, color='k', linestyle=':', linewidth=1.0, zorder=10)
                            
                        # RDF
                        dist_files = sorted(glob.glob(f"step_???/{ia_name}.dist.new"))
                        dist_file = dist_files[-1]  # only last one
                        step_dist = int(re.search('step_(\d+)', dist_file).group(1)) - 1  # -1 because we use .pot.cur
                        try:
                            dist_new_r, dist_new_g, _ = readin_table(dist_file)
                        except:
                            print(f".. could not load {dist_file} ..")
                            continue
                        #print(step_dist)
                        label = label if i == 0 else None
                        line, = axes[i].plot(dist_new_r, dist_new_g, label=label, color=color, linestyle=linestyle, linewidth=1.0, zorder=i)
                            
                        
            axes[-1].set_xlabel(r'$r$ in \si{\nano\meter}')
            axes[1].set_ylabel(r'$g(r)$')
            axes[-1].set_xlim(0.25, 1.2)
            for ax in axes:
                ax.set_ylim(0.0, 1.9)
                ax.set_yticks([0.5, 1.0, 1.5])
            leg = fig.legend(ncol=3, loc='center left',
                             bbox_to_anchor=(-0.2, 1.6), bbox_transform=axes[0].transAxes)
            fig.set_constrained_layout_pads(w_pad=0.02, h_pad=0.00, hspace=0., wspace=0.)
            plt.show()

show_last_rdf(show_target=True)

## show direct correlation function

In [ ]:
def show_c(ia_to_show=['non-bonded', 'bonds', 'angles', 'dihs'], show_intra=False):
    
    #fg_sys_types_to_do = fg_sys_types
    fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['pyridine']}
    
    #states_to_do = states
    states_to_do = {key: states[key] for key in ['pure', 'pure-large']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
    
    #votca_settings_to_do = votca_settings
    votca_settings_to_do = {key: votca_settings[key] for key in [
        #'hncnt-hncinitshort',
        'hncnt-hncinitlong',
    ]}
    
    for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
        fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=True):
        
        statepoints = gen_statepoints(cg_problem['state'])
        
        fig, ax = plt.subplots(figsize=[6, 2], constrained_layout=True, dpi=96)

        color_dict = collections.defaultdict(lambda: None)
        for s, statepoint in enumerate(statepoints):
            sp = statepoint['path']
            print('   ', sp)
            linestyle = ['-', '--', ':'][s]
            
            try:
                data = np.load(f"{cg_problem['folder']}/step_000/{sp}/calc_u_matrix-calc_c_matrix.npz")
                #print(data.__dict__)
                r = data['r']
                c_mat = data['return_value']
                
                for i, cg_beadtype_pair in enumerate(itertools.combinations_with_replacement(
                    cg.core.gen_cg_beadtypes(cg_problem['fg-topology'], cg_problem['mapping']).keys(), 2
                )):
                    print(cg_beadtype_pair)
                    # TODO: indexin is likely not correct
                    ax.plot(r, c_mat[:, i, i])
                
            except FileNotFoundError:
                print(".. no data ..")
            
            #ax.set_ylim(-0.1, 0.1)
            ax.set_ylim(-0.5, 0.5)
            ax.set_xlabel(r'$r$ in nm')
            ax.set_ylabel(r'$c(r)$')
            #ax.legend(frameon=False, loc='upper right', ncol=4)
        plt.show()
            
show_c(ia_to_show=['non-bonded'])

## plot bond + angle hexane

In [ ]:
def plot_bond_angle():
    mpl_rc_local = {'legend.handlelength': 2.0}
    with plt.rc_context({**mpl_rc_global, **mpl_rc_local}):
        
        #fg_sys_types_to_do = fg_sys_types
        fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['hexane']}
        
        mappings_to_do = mappings
        #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
        
        states_to_do = states
        #states_to_do = {key: states[key] for key in ['pure']}
        
        votca_settings_to_do = {key: votca_settings[key] for key in [
            'ibi-altibiintra',
            'imco-altibiintra',
            'hncn-altibiintra',
            #'phncgnt-altibiintra',
            #'PEhncgnt-altibiintra',
            #'KBIhncgnt-altibiintra',
        ]}
        
        # groupby fg, state, mapping
        for (fg_sys_type_key, state_key, mapping_key), group in itertools.groupby(cg_setup_generator(
            fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=False),
                                                                                  lambda x: (x[1], x[2], x[3])):

            # create figure
            fig, axes = plt.subplots(nrows=1, ncols=2, figsize=[3.2, 2.1], constrained_layout=True, dpi=300, sharey='row')
            line_label_dict = {}
            #line_label_dict[(label, init_method)] = (empty, label)  # first row, second column
            #line_label_dict = collections.defaultdict(lambda label, _: (empty, label))

            # iterate in group
            #print(fg_sys_type_key, state_key, mapping_key)
            for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in group:
                print(' ', votca_setting_key)

                label = label_of_method[votca_setting_key.split('-')[0]]
                color = color_of_method[votca_setting_key.split('-')[0]]
                linestyle = linestyle_of_method[votca_setting_key.split('-')[0]]

                # plot last potential
                working_dir = os.path.join(cg_problem['folder'])
                with WorkingDir(working_dir):
                    min_pot = 0
                    # iterate interactions
                    for i, ia_name in enumerate(['bond-A-B', 'angle-A-B-A']):
                        ax = axes[i]
                        #print(ia_name)

                        # load new
                        pot_files = sorted(glob.glob(f"step_???/{ia_name}.pot.cur"))
                        pot_file = pot_files[-1]  # only last one
                        step = int(re.search('step_(\d+)', pot_file).group(1)) - 1  # -1 because we use .pot.cur
                        pot_new_r, pot_new_u, _ = readin_table(pot_file)
                        print(step)
                        label = label if i == 0 else None
                        line, = ax.plot(pot_new_r, pot_new_u, label=label, color=color, linestyle=linestyle)

            axes[0].set_xlabel(r'$r$ in \si{\nano\meter}')
            axes[0].set_ylabel(r'$u(r)$ in \si{\kilo\joule\per\mole}')
            axes[1].set_xlabel(r'$\phi$ in \si{\radian}')
            axes[0].set_title('bond')
            axes[1].set_title('angle')
            axes[0].set_xlim(0.21, 0.29)
            axes[0].set_ylim(0, 20)
            axes[1].set_xlim(1.3, np.pi)
            #axes[1].set_ylim(0, 30)
            axes[0].legend()
            fig.set_constrained_layout_pads(w_pad=0.00, h_pad=0.01, hspace=0., wspace=0.)
            fig.savefig('../figures/bond-angle.pdf')
            fig.set_constrained_layout_pads(w_pad=0.00, h_pad=0.01, hspace=0., wspace=0.)
            plt.show()

plot_bond_angle()

# paper plots

## plot neon-argon imc artifact

In [ ]:
def plot_imc_artifact(show_rdf=False, show_u1=False):
    mpl_rc_local = {
        'legend.handlelength': 3.0,
        'legend.labelspacing': 0.7,
    }
    with plt.rc_context({**mpl_rc_global, **mpl_rc_local}):
        
        #fg_sys_types_to_do = fg_sys_types
        fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['neon-argon']}
        
        mappings_to_do = mappings
        #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
        
        states_to_do = states
        #states_to_do = {key: states[key] for key in ['pure']}
        
        #votca_settings_to_do = votca_settings
        votca_settings_to_do = {key: votca_settings[key] for key in [
            'imc-ibiintra',
            #'imct-ibiintra',
            'imco-ibiintra',
            #'imcot-ibiintra',
        ]}
        
        #ia_to_show = 'all'
        ia_to_show = ['AR-AR']

        # create figure
        fig, ax = plt.subplots(nrows=1, ncols=1, figsize=[3.2, 2.1], constrained_layout=True, dpi=300)
        fig.set_constrained_layout_pads(w_pad=0.01, h_pad=0.01, hspace=0., wspace=0.)
        
        for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
            fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=True):

            label = label_of_method[votca_setting_key.split('-')[0]]
            label = fr"$u_2^\text{{{label}}}$"
            color = color_of_method[votca_setting_key.split('-')[0]]
            linestyle = linestyle_of_method[votca_setting_key.split('-')[0]]

            working_dir = os.path.join(cg_problem['folder'])
            with WorkingDir(working_dir):
                min_pot = 0
                # iterate interactions
                for i, cg_beadtype_pair in enumerate(cg.gen_beadtype_pairs(cg_problem, return_dict=True)):
                    ia_name = '-'.join(sorted((key for key, value in cg_beadtype_pair)))
                    if ia_to_show != 'all' and ia_name not in ia_to_show:
                        continue
                    #print(ia_name)
                    
                    if show_u1 and v == 0:
                        pot_2_r, pot_2_u, _ = readin_table(f"step_001/{ia_name}.pot.cur")
                        ax.plot(pot_2_r, pot_2_u, label=r'$u_1$', color='k', linestyle='-')

                    # load step_002
                    pot_cur_r, pot_cur_u, _ = readin_table(f"step_002/{ia_name}.pot.cur")
                    ax.plot(pot_cur_r, pot_cur_u, label=label, color=color, linestyle=linestyle)
                    
                    g_tgt_r, g_tgt_g, _ = readin_table(f"step_001/{ia_name}.dist.tgt")
                    g_new_r, g_new_g, _ = readin_table(f"step_001/{ia_name}.dist.new")
                    if show_rdf and v == 0:
                        ax2 = ax.twinx()
                        ax2.plot(g_tgt_r, g_tgt_g, label=r'$g_\text{tgt}$', color='k', linestyle=':')
                        ax2.plot(g_new_r, g_new_g, label=r'$g_{1}$', color='k', linestyle='--')
                        ax2.set_ylabel(r'$g_\text{Ar-Ar}(r)$')
                        
                    if 'onset_thresholds' in cg_problem['votca-settings']['inverse']['imc'].keys():
                        print(cg_problem['votca-settings']['inverse']['imc']['onset_thresholds'])
                        t1, t2 = cg_problem['votca-settings']['inverse']['imc']['onset_thresholds'].split()
                        nx1 = np.asarray(g_new_g > float(t1)).nonzero()[0][0] - 1
                        nx2 = np.asarray(g_new_g > float(t2)).nonzero()[0][0]
                        ax.axvline(g_tgt_r[nx1], color='grey', linestyle=':')
                        ax.axvline(g_tgt_r[nx2], color='grey', linestyle=':')

        ax.set_xlabel(r'$r$ in \si{\nano\meter}')
        ax.set_ylabel(r'$u_\text{Ar-Ar}(r)$ in \si{\kilo\joule\per\mole}')
        ax.set_xlim(0.27, 0.39)
        ax.set_ylim(-4, 22)
        if show_rdf:
            ax2.set_ylim(1e-8, 3)
            ax2.set_yscale('log')
            fig.legend(loc=(0.49, 0.35))
        else:
            fig.legend(loc=(0.5, 0.67))
        fig.savefig('../figures/imc-onset-instability.pdf')
        plt.show()
    
plot_imc_artifact(show_rdf=True, show_u1=True)

In [ ]:
!cp ../figures/imc-onset-instability.pdf /home/marvin/research/output/iie-general-paper/figures/

## plot potential convergence neon-argon

## plot last potential neon-argon

In [ ]:
def plot_last_potential(show_std5=False):
    mpl_rc_local = {'legend.handlelength': 2.0}
    with plt.rc_context({**mpl_rc_global, **mpl_rc_local}):
        
        #fg_sys_types_to_do = fg_sys_types
        fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['neon-argon']}
        
        mappings_to_do = mappings
        #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
        
        states_to_do = states
        #states_to_do = {key: states[key] for key in ['pure']}
        
        votca_settings_to_do = {key: votca_settings[key] for key in [
            'ibi-ibiintra',
            'imco-ibiintra',
            'imcot-ibiintra',
            'hncn-ibiintra',
            'hncnt-ibiintra',
        ]}
        
        ia_to_show = 'all'
        #ia_to_show = ['AR-MW']
        #ia_to_show = ['AR-MW', 'AR-AR']

        # groupby fg, state, mapping
        for (fg_sys_type_key, state_key, mapping_key), group in itertools.groupby(cg_setup_generator(
            fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=False),
                                                                                  lambda x: (x[1], x[2], x[3])):

            # create figure
            fig, ax = plt.subplots(nrows=1, ncols=1, figsize=[3.2, 2.1], constrained_layout=True, dpi=300)
            fig.set_constrained_layout_pads(w_pad=0.01, h_pad=0.01, hspace=0., wspace=0.)
            line_label_dict = {}
            #line_label_dict[(label, init_method)] = (empty, label)  # first row, second column
            #line_label_dict = collections.defaultdict(lambda label, _: (empty, label))

            # iterate in group
            #print(fg_sys_type_key, state_key, mapping_key)
            for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in group:
                #print(' ', votca_setting_key)

                label = label_of_method[votca_setting_key.split('-')[0]]
                color = color_of_method[votca_setting_key.split('-')[0]]
                linestyle = linestyle_of_method[votca_setting_key.split('-')[0]]

                # plot last potential
                working_dir = os.path.join(cg_problem['folder'])
                with WorkingDir(working_dir):
                    min_pot = 0
                    # iterate interactions
                    for i, cg_beadtype_pair in enumerate(cg.gen_beadtype_pairs(cg_problem, return_dict=True)):
                        ia_name = '-'.join(sorted((key for key, value in cg_beadtype_pair)))
                        if ia_to_show != 'all' and ia_name not in ia_to_show:
                            continue
                        #print(ia_name)

                        # load new
                        pot_files = sorted(glob.glob(f"step_???/{ia_name}.pot.cur"))
                        pot_file = pot_files[-1]  # only last one
                        step = int(re.search('step_(\d+)', pot_file).group(1)) - 1  # -1 because we use .pot.cur
                        pot_new_r, pot_new_u, _ = readin_table(pot_file)
                        label = label if i == 0 else None
                        line, = ax.plot(pot_new_r, pot_new_u, label=label, color=color, linestyle=linestyle)
                        if show_std5:
                            for pot_file in pot_files[-5:]:  # only last 5
                                pot_new_r, pot_new_u, _ = readin_table(pot_file)
                                label = label if i == 0 else None
                                line, = ax.plot(pot_new_r, pot_new_u, label=None, color=color, linestyle=linestyle, linewidth=0.1)

            # plot tgt potentials
            # iterate interactions
            for i, cg_beadtype_pair in enumerate(cg.gen_beadtype_pairs(cg_problem, return_dict=True)):
                ia_name = '-'.join(sorted((key for key, value in cg_beadtype_pair)))
                if ia_to_show != 'all' and ia_name not in ia_to_show:
                    continue
                if mapping_key.startswith('unity'):  # otherwise there can be no known target potential
                    fg_bead1_name = cg_problem['mapping']['moltypes'][cg_beadtype_pair[0][1]['map_mol_name']][cg_beadtype_pair[0][0]]['fg-beads'][0]
                    fg_bead2_name = cg_problem['mapping']['moltypes'][cg_beadtype_pair[1][1]['map_mol_name']][cg_beadtype_pair[1][0]]['fg-beads'][0]
                    fg_bead1 = cg_problem['fg-topology']['moltypes'][cg_beadtype_pair[0][1]['map_mol_name']]['beads'][fg_bead1_name]
                    fg_bead2 = cg_problem['fg-topology']['moltypes'][cg_beadtype_pair[1][1]['map_mol_name']]['beads'][fg_bead2_name]
                    r = pot_new_r
                    cut_off = cg_problem['functional-votca-settings-input']['cut']
                    with np.errstate(divide='ignore', invalid='ignore'):
                        pot_tgt_u = calc_potential(
                            r,
                            fg_bead1,
                            fg_bead2,
                            combination_rule[fg_sys_types['neon-argon']['topology']['ff-key']], cut_off,
                            cg_problem['fg-topology']['non-mixing-rule-factors'] if 'non-mixing-rule-factors' in cg_problem['fg-topology'] else {},
                            potential_shift=True)
                        label = 'LJ' if i == 0 else None
                        ax.plot(r, pot_tgt_u, label=label, color='black', linestyle=':')

            ax.set_xlabel(r'$r$ in \si{\nano\meter}')
            ax.set_ylabel(r'$u(r)$ in \si{\kilo\joule\per\mole}')
            ax.set_xlim(0.2, 0.93)
            ax.set_ylim(-1, 0.2)
            ax.legend()
            fig.savefig('../figures/last-potential-neon-argon.pdf')
            plt.show()

plot_last_potential(show_std5=False)

In [ ]:
!cp ../figures/last-potential-neon-argon.pdf /home/marvin/research/output/iie-general-paper/figures/

In [ ]:
def show_potential_convergence(show_real_time=True, plot_sum=False):
    #fg_sys_types_to_do = fg_sys_types
    fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['neon-argon']}
    
    states_to_do = states
    #states_to_do = {key: states[key] for key in ['pure']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
    
    #votca_settings_to_do = votca_settings
    votca_settings_to_do = {key: votca_settings[key] for key in [
        'ibi-ibiintra',
        'imco-ibiintra',
        'imcot-ibiintra',
        'hncn-ibiintra',
        'hncnt-ibiintra',
    ]}
    
    # real time per iteration with dual socket AMD EPYC 7413
    real_iteration_minutes = {
        'ibi-ibiintra': 19 / 19,
        'imco-ibiintra': 14 / 1,
        'imcot-ibiintra': 21 / 19,
        'hncn-ibiintra': 34 / 19,
        'hncnt-ibiintra': 19 / 19,
    }
    
    ia_to_show = 'all'
    
    mpl_rc_local = {
        'legend.handlelength': 2.0,
        #'legend.framealpha': 0.0,
    }
    with plt.rc_context({**mpl_rc_global, **mpl_rc_local}):
        
        # groupby fg, state, mapping
        for (fg_sys_type_key, state_key, mapping_key), group in itertools.groupby(cg_setup_generator(
            fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=False),
                                                                                  lambda x: (x[1], x[2], x[3])):

            # create figure
            fig, ax = plt.subplots(nrows=1, ncols=1, figsize=[3.2, 2.1], constrained_layout=True, dpi=300)
            fig.set_constrained_layout_pads(w_pad=0.01, h_pad=0.01, hspace=0., wspace=0.)
            line_label_dict = {}

            # iterate in group
            #print(fg_sys_type_key, state_key, mapping_key)
            for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in group:
                #print(' ', votca_setting_key)

                # stuff for label, color, linestyle
                label = label_of_method[votca_setting_key.split('-')[0]]
                color = color_of_method[votca_setting_key.split('-')[0]]
                linestyle = linestyle_of_method[votca_setting_key.split('-')[0]]
                
                if show_real_time:
                    label += f" ({real_iteration_minutes[votca_setting_key]:.1f})"

                # iterate files
                working_dir = os.path.join(cg_problem['folder'])
                with WorkingDir(working_dir):
                    err_u_sum = 0
                    for i, cg_beadtype_pair in enumerate(cg.gen_beadtype_pairs(cg_problem, return_dict=True)):
                        ia_name = '-'.join(sorted((key for key, value in cg_beadtype_pair)))
                        if ia_to_show != 'all' and ia_name not in ia_to_show:
                            continue
                            
                        # load tgt
                        dist_tgt_r, dist_tgt_g, _ = readin_table(f"step_001/{ia_name}.dist.tgt")
                        r = dist_tgt_r
                        
                        # calc slice
                        cut_off = cg_problem['functional-votca-settings-input']['cut']
                        cut, _ = csg.calc_slices(r, cut_off)
                        cut = slice(1, cut.stop)
                        #print(cut_off)
                        
                        # calculate true potential
                        fg_bead1_name = cg_problem['mapping']['moltypes'][cg_beadtype_pair[0][1]['map_mol_name']][cg_beadtype_pair[0][0]]['fg-beads'][0]
                        fg_bead2_name = cg_problem['mapping']['moltypes'][cg_beadtype_pair[1][1]['map_mol_name']][cg_beadtype_pair[1][0]]['fg-beads'][0]
                        fg_bead1 = cg_problem['fg-topology']['moltypes'][cg_beadtype_pair[0][1]['map_mol_name']]['beads'][fg_bead1_name]
                        fg_bead2 = cg_problem['fg-topology']['moltypes'][cg_beadtype_pair[1][1]['map_mol_name']]['beads'][fg_bead2_name]
                        with np.errstate(divide='ignore', invalid='ignore'):
                            pot_tgt_u = calc_potential(
                                r,
                                fg_bead1,
                                fg_bead2,
                                combination_rule[fg_sys_types['neon-argon']['topology']['ff-key']], cut_off,
                                cg_problem['fg-topology']['non-mixing-rule-factors'] if 'non-mixing-rule-factors' in cg_problem['fg-topology'] else {},
                                potential_shift=True)
                            
                        # calculate potential mismatch
                        # load pot cur
                        pot_files = sorted(glob.glob(f"step_*/{ia_name}.pot.cur"))
                        err_u = []
                        for pot_file in pot_files:
                            step = int(re.search('step_(\d+)', pot_file).group(1))
                            pot_cur_r, pot_cur_u, _ = readin_table(pot_file)
                            np.testing.assert_allclose(pot_cur_r, dist_tgt_r)
                            err_u.append((step, np.sqrt(1/max(r[cut]) * np.trapz(x=r[cut], y=dist_tgt_g[cut] * (pot_cur_u - pot_tgt_u)[cut]**2))))
                            
                        if not plot_sum:
                            label = label if i == 0 else None
                            line, = ax.plot(*np.array(err_u).T, label=label, color=color, linestyle=linestyle)
                        # add to sum
                        err_u_sum += np.array(err_u)[:, 1]
                        steps = np.array(err_u)[:, 0]
                        
                    if plot_sum:
                        line, = ax.plot(steps, err_u_sum, label=label, color=color, linestyle=linestyle, marker='.')

            # after group iteration
            ax.set_xlabel('iteration $k$')
            if plot_sum:
                #ax.set_ylabel(r'$\Sigma_{\alpha < \beta} \ \chi(u_{\alpha\beta})$ in \si{\kilo\joule\per\mole}')
                ax.set_ylabel(r'$\chi(u_k)$ in \si{\kilo\joule\per\mole}')
            else:
                ax.set_ylabel(r'$\chi(u_k)$')
            ax.set_yscale('log')
            ax.set_xlim(0, 20)
            #ax.set_ylim(None, 4e-0)
            leg = ax.legend(loc=(0.4, 0.4), frameon=True, framealpha=0.7)
            leg.get_frame().set_linewidth(0.0)
            fig.savefig('../figures/potential-convergence.pdf')
            plt.show()

#show_potential_convergence(show_real_time=True, plot_sum=False)
show_potential_convergence(show_real_time=True, plot_sum=True)

In [ ]:
!cp ../figures/potential-convergence.pdf /home/marvin/research/output/iie-general-paper/figures/

## plot oscillating behaviour for hexane 

In [ ]:
def plot_oscillating():
    #fg_sys_types_to_do = fg_sys_types
    fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['hexane']}
    
    states_to_do = states
    #states_to_do = {key: states[key] for key in ['pure']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
    
    #votca_settings_to_do = votca_settings
    votca_settings_to_do = {key: votca_settings[key] for key in [
        'hncn-ibiintra',
    ]}
    
    mpl_rc_local = {'legend.handlelength': 1.3}
    with plt.rc_context({**mpl_rc_global, **mpl_rc_local}):
        
        # groupby fg, state, mapping
        for (fg_sys_type_key, state_key, mapping_key), group in itertools.groupby(cg_setup_generator(
            fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=False),
                                                                                  lambda x: (x[1], x[2], x[3])):
            # create figure
            fig, axes = plt.subplots(nrows=1, ncols=2, figsize=[3.2, 2.1], constrained_layout=True, dpi=300)
            fig.set_constrained_layout_pads(w_pad=0.01, h_pad=0.01, hspace=0., wspace=0.)

            # iterate in group (over votca settings)
            print(fg_sys_type_key, state_key, mapping_key)
            for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in group:
                print(' ', votca_setting_key)

                # iterate files
                working_dir = os.path.join(cg_problem['folder'])
                with WorkingDir(working_dir):
                    min_pot = 0
                    for i, ia_name in enumerate(['A-A', 'bond-A-B']):
                    #for i, ia_name in enumerate(['A-A', 'angle-A-B-A']):
                        ax = axes[i]
                        # load tgt
                        dist_tgt_r, dist_tgt_g, _ = readin_table(f"step_001/{ia_name}.dist.tgt")
                        # load new
                        dist_files = sorted(glob.glob(f"step_*/{ia_name}.dist.new"))[14:20]
                        for d, dist_file in enumerate(dist_files):
                            step = int(re.search('step_(\d+)', dist_file).group(1))
                            dist_new_r, dist_new_g, _ = readin_table(dist_file)
                            offset = 4
                            if d % 2 == 0:
                                color = plt.get_cmap('GnBu')((d + offset) / (len(dist_files) + offset))
                            else:
                                color = plt.get_cmap('YlOrRd')((d + offset) / (len(dist_files) + offset))
                            line, = ax.plot(dist_new_r, dist_new_g, label=step, color=color, linestyle='--')
                            
                        line, = ax.plot(dist_tgt_r, dist_tgt_g, label='tgt', color='k', linestyle=':')

            # after group iteration
            axes[0].set_xlabel(r'$r$ in \si{\nano\meter}')
            axes[0].set_ylabel(r'$g(r)$')
            axes[0].set_xlim(0.4, 0.86)
            axes[0].set_ylim(0.68, 1.88)
            axes[1].set_xlim(0.22, 0.28)
            axes[1].set_xlabel(r'$r$ in \si{\nano\meter}')
            axes[1].set_ylabel(r'$p(r)$ in \si{\per\nano\meter}')
            axes[1].yaxis.tick_right()
            axes[1].yaxis.set_label_position("right")
            axes[0].legend(loc=(0.38, 0.3), ncol=1)
            fig.savefig('../figures/oscillating.pdf')
            plt.show()

plot_oscillating()

In [ ]:
!cp ../figures/oscillating.pdf /home/marvin/research/output/iie-general-paper/figures/

## plot RDF convergence hexane

In [ ]:
def plot_rdf_convergence(plot_sum=True):
    #fg_sys_types_to_do = fg_sys_types
    fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['hexane']}
    
    states_to_do = states
    #states_to_do = {key: states[key] for key in ['pure']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
    
    #votca_settings_to_do = votca_settings
    votca_settings_to_do = {key: votca_settings[key] for key in [
        'ibi-altibiintra',
        'imco-altibiintra',
        'imcot-altibiintra',
        'hncn-altibiintra',
        'hncnt-altibiintra',
        'hncnl-altibiintra',
        #'phncgnt-altibiintra',
        #'PEhncgnt-altibiintra',
        #'KBIhncgnt-altibiintra',
        #'KBIphncgnt-altibiintra',
    ]}
    
    ia_to_show = 'all'
    #ia_to_show = ['AR-AR']
    
    mpl_rc_local = {
        'legend.handlelength': 1.8,
        'legend.labelspacing': 0.3,
    }
    with plt.rc_context({**mpl_rc_global, **mpl_rc_local}):
        
        # groupby fg, state, mapping
        for (fg_sys_type_key, state_key, mapping_key), group in itertools.groupby(cg_setup_generator(
            fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=False),
                                                                                  lambda x: (x[1], x[2], x[3])):

            # create figure
            fig, ax = plt.subplots(nrows=1, ncols=1, figsize=[3.2, 2.1], constrained_layout=True, dpi=300)
            fig.set_constrained_layout_pads(w_pad=0.01, h_pad=0.01, hspace=0., wspace=0.)

            # iterate in group
            print(fg_sys_type_key, state_key, mapping_key)
            for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in group:
                print(' ', votca_setting_key)

                # stuff for label, color, linestyle
                init_method = cg_problem['votca-settings']['inverse']['initial_guess']['method']
                label = label_of_method[votca_setting_key.split('-')[0]]
                color = color_of_method[votca_setting_key.split('-')[0]]
                linestyle = linestyle_of_method[votca_setting_key.split('-')[0]]

                # iterate files
                working_dir = os.path.join(cg_problem['folder'])
                with WorkingDir(working_dir):
                    err_g_sum = 0
                    for i, cg_beadtype_pair in enumerate(cg.gen_beadtype_pairs(cg_problem)):
                        ia_name = '-'.join(sorted(cg_beadtype_pair))
                        if ia_to_show != 'all' and ia_name not in ia_to_show:
                            continue
                        # load tgt
                        try:
                            if os.path.exists(f"step_001/{ia_name}.dist.tgt"):
                                dist_tgt_r, dist_tgt_g, _ = readin_table(f"step_001/{ia_name}.dist.tgt")
                            else:
                                dist_tgt_r, dist_tgt_g, _ = readin_table(f"step_002/{ia_name}.dist.tgt")
                        except:
                            print(f".. could not load {ia_name}.dist.tgt, continue ..")
                            empty = mpl.patches.Rectangle((0,0), 1, 1, fill=False, edgecolor='none', visible=False)
                            continue
                        # load new
                        dist_files = sorted(glob.glob(f"step_*/{ia_name}.dist.new"))
                        err_g = []
                        for dist_file in dist_files:
                            step = int(re.search('step_(\d+)', dist_file).group(1))
                            try:
                                dist_new_r, dist_new_g, _ = readin_table(dist_file)
                            except:
                                print(f".. could not load {dist_file} ..")
                            cut_off = cg_problem['functional-votca-settings-input']['cut']
                            cut, _ = csg.calc_slices(dist_new_r, cut_off)
                            err_g.append((step, np.sqrt(1/max(dist_new_r[cut]) * np.trapz(x=dist_new_r[cut], y=(dist_new_g - dist_tgt_g)[cut]**2))))
                        if not plot_sum:
                            label = label if i == 0 else None
                            line, = ax.plot(*np.array(err_g).T, label=label, color=color, linestyle=linestyle)
                        # add to sum
                        err_g_sum += np.array(err_g)[:, 1]
                        steps = np.array(err_g)[:, 0]
                        
                    if plot_sum:
                        if err_g_sum is 0:
                            continue
                        line, = ax.plot(steps, err_g_sum, label=label, color=color, linestyle=linestyle, marker='.', markersize=3.5)

            # after group iteration
            ax.set_xlabel('iteration $k$')
            #ax.set_ylabel(r'$\sqrt{\frac{1}{r_c} \int_0^{r_c} (g - g_\mathrm{tgt})^2 dr}$')
            if plot_sum:
                ax.set_ylabel(r'$\chi(g_k)$')
            else:
                ax.set_ylabel(r'$\sigma(g_k)$')
            ax.set_yscale('log')
            ax.set_xlim(0, 40)
            #ax.set_ylim(None, 1e-1)
            #ax.set_xticks([0, 5, 10, 15, 20])
            ax.legend(loc='upper right', ncol=2)
            fig.savefig('../figures/rdf-convergence-hexane.pdf')
            plt.show()

#plot_rdf_convergence(plot_sum=False)
plot_rdf_convergence(plot_sum=True)

In [ ]:
!cp ../figures/rdf-convergence-hexane.pdf /home/marvin/research/output/iie-general-paper/figures/

## plot last potential hexane

In [ ]:
#OLD VERSION

In [ ]:
def plot_last_potential(show_std5=False, show_annotations=False):
    mpl_rc_local = {'legend.handlelength': 2.0}
    with plt.rc_context({**mpl_rc_global, **mpl_rc_local}):
        
        #fg_sys_types_to_do = fg_sys_types
        fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['hexane']}
        
        mappings_to_do = mappings
        #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
        
        states_to_do = states
        #states_to_do = {key: states[key] for key in ['pure']}
        
        votca_settings_to_do = {key: votca_settings[key] for key in [
            'ibi-altibiintra',
            'imco-altibiintra',
            'imcot-altibiintra',
            'hncn-altibiintra',
            'hncnt-altibiintra',
            #'hncnl-altibiintra',
            #'hncgnt-altibiintra',
            #'PEhncgnt-altibiintra',
            #'KBIhncgnt-altibiintra',
        ]}
        
        ia_to_show = 'all'
        #ia_to_show = ['AR-MW']
        #ia_to_show = ['AR-MW', 'AR-AR']

        # groupby fg, state, mapping
        for (fg_sys_type_key, state_key, mapping_key), group in itertools.groupby(cg_setup_generator(
            fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=False),
                                                                                  lambda x: (x[1], x[2], x[3])):

            # create figure
            fig, ax = plt.subplots(nrows=1, ncols=1, figsize=[3.2, 2.1], constrained_layout=True, dpi=300)
            fig.set_constrained_layout_pads(w_pad=0.01, h_pad=0.01, hspace=0., wspace=0.)
            line_label_dict = {}
            #line_label_dict[(label, init_method)] = (empty, label)  # first row, second column
            #line_label_dict = collections.defaultdict(lambda label, _: (empty, label))

            # iterate in group
            #print(fg_sys_type_key, state_key, mapping_key)
            for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in group:
                print(' ', votca_setting_key)

                label = label_of_method[votca_setting_key.split('-')[0]]
                color = color_of_method[votca_setting_key.split('-')[0]]
                linestyle = linestyle_of_method[votca_setting_key.split('-')[0]]

                # plot last potential
                working_dir = os.path.join(cg_problem['folder'])
                with WorkingDir(working_dir):
                    min_pot = 0
                    # iterate interactions
                    for i, cg_beadtype_pair in enumerate(cg.gen_beadtype_pairs(cg_problem, return_dict=True)):
                        ia_name = '-'.join(sorted((key for key, value in cg_beadtype_pair)))
                        if ia_to_show != 'all' and ia_name not in ia_to_show:
                            continue
                        #print(ia_name)

                        # load new
                        pot_files = sorted(glob.glob(f"step_???/{ia_name}.pot.cur"))
                        pot_file = pot_files[-1]  # only last one
                        step = int(re.search('step_(\d+)', pot_file).group(1)) - 1  # -1 because we use .pot.cur
                        pot_new_r, pot_new_u, _ = readin_table(pot_file)
                        print(step)
                        label = label if i == 0 else None
                        line, = ax.plot(pot_new_r, pot_new_u, label=label, color=color, linestyle=linestyle)
                        if show_annotations:
                            ndx = 128
                            ax.annotate(
                                ia_name,
                                xy=(pot_new_r[ndx], pot_new_u[ndx]), xycoords='data',
                                xytext=[(0.5, -0.5), (0.8, -0.7), (0.68, -0.75)][i], textcoords='data',
                                arrowprops=dict(width=0.2,
                                                headlength=2,
                                                headwidth=2,
                                                shrink=0.05,
                                                alpha=0.4,
                                                fc="k"
                                               ),
                            )
                        if show_std5:
                            for pot_file in pot_files[-5:]:  # only last 5
                                pot_new_r, pot_new_u, _ = readin_table(pot_file)
                                label = label if i == 0 else None
                                line, = ax.plot(pot_new_r, pot_new_u, label=None, color=color, linestyle=linestyle, linewidth=0.3)

            ax.set_xlabel(r'$r$')
            ax.set_ylabel(r'$u(r)$ in kJ/mol')
            ax.set_xlim(0.38, 1.24)
            ax.set_ylim(-1.3, 0.6)
            ax.legend()
            #fig.savefig('../figures/last-potential-hexane.pdf')
            plt.show()

plot_last_potential(show_std5=False, show_annotations=True)

In [ ]:
from mpl_toolkits.axes_grid1.inset_locator import zoomed_inset_axes, mark_inset

def plot_last_potential(show_std5=False, show_annotations=False, show_inset=False):
    mpl_rc_local = {
        'legend.handlelength': 1.8,
        'legend.labelspacing': 0.1,
        'legend.columnspacing': 1.0,
    }
    with plt.rc_context({**mpl_rc_global, **mpl_rc_local}):
        
        #fg_sys_types_to_do = fg_sys_types
        fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['hexane']}
        
        mappings_to_do = mappings
        #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
        
        states_to_do = states
        #states_to_do = {key: states[key] for key in ['pure']}
        
        votca_settings_to_do = {key: votca_settings[key] for key in [
            'ibi-altibiintra',
            'imco-altibiintra',
            'imcot-altibiintra',
            'hncn-altibiintra',
            'hncnt-altibiintra',
            #'hncnl-altibiintra',
            #'hncgnt-altibiintra',
        ]}
        
        ia_to_show = 'all'
        #ia_to_show = ['AR-MW']
        #ia_to_show = ['AR-MW', 'AR-AR']

        # groupby fg, state, mapping
        for (fg_sys_type_key, state_key, mapping_key), group in itertools.groupby(cg_setup_generator(
            fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=False),
                                                                                  lambda x: (x[1], x[2], x[3])):

            # create figure
            fig, axes = plt.subplots(nrows=3, ncols=1, sharex='all', figsize=[3.2, 2.9], constrained_layout=True, dpi=300)
            fig.set_constrained_layout_pads(w_pad=0.00, h_pad=0.00, hspace=0., wspace=0.)
            #left, bottom, width, height = [0.75, 0.75, 0.2, 0.2]
            
            if show_inset:
                axins = zoomed_inset_axes(ax, 30, loc='upper right')
                # sub region of the original image
                x1, x2, y1, y2 = 1.190, 1.201, -0.02, 0.02
                axins.set_xlim(x1, x2)
                axins.set_ylim(y1, y2)
                # fix the number of ticks on the inset axes
                axins.yaxis.get_major_locator().set_params(nbins=2)
                axins.xaxis.get_major_locator().set_params(nbins=2)
                plt.setp(axins.get_xticklabels(), visible=False)
                #plt.setp(axins.get_yticklabels(), visible=False)
                # draw a bbox of the region of the inset axes in the parent axes and
                # connecting lines between the bbox and the inset axes area
                mark_inset(ax, axins, loc1=3, loc2=4, fc="none", ec="0.5")

            #ax2 = fig.add_axes([left, bottom, width, height])
            line_label_dict = {}
            #line_label_dict[(label, init_method)] = (empty, label)  # first row, second column
            #line_label_dict = collections.defaultdict(lambda label, _: (empty, label))

            # iterate in group
            #print(fg_sys_type_key, state_key, mapping_key)
            for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in group:
                print(' ', votca_setting_key)

                label = label_of_method[votca_setting_key.split('-')[0]]
                color = color_of_method[votca_setting_key.split('-')[0]]
                linestyle = linestyle_of_method[votca_setting_key.split('-')[0]]

                # plot last potential
                working_dir = os.path.join(cg_problem['folder'])
                with WorkingDir(working_dir):
                    min_pot = 0
                    # iterate interactions
                    for i, cg_beadtype_pair in enumerate(cg.gen_beadtype_pairs(cg_problem, return_dict=True)):
                        ia_name = '-'.join(sorted((key for key, value in cg_beadtype_pair)))
                        if ia_to_show != 'all' and ia_name not in ia_to_show:
                            continue
                        ax = axes[i]
                        #print(ia_name)
                        if v == 0:
                            ax.text(0.15, 0.80, ia_name, transform=ax.transAxes)

                        # load new
                        pot_files = sorted(glob.glob(f"step_???/{ia_name}.pot.cur"))
                        try:
                            pot_file = pot_files[-1]  # only last one
                        except:
                            continue
                        step = int(re.search('step_(\d+)', pot_file).group(1))
                        pot_new_r, pot_new_u, _ = readin_table(pot_file)
                        print(step)
                        label = label if i == 0 else None
                        line, = ax.plot(pot_new_r, pot_new_u, label=label, color=color, linestyle=linestyle)
                        if show_inset:
                            axins.plot(pot_new_r, pot_new_u, label=label, color=color, linestyle=linestyle)
                        if show_annotations:
                            ndx = 128
                            ax.annotate(
                                ia_name,
                                xy=(pot_new_r[ndx], pot_new_u[ndx]), xycoords='data',
                                xytext=[(0.5, -0.5), (0.8, -0.7), (0.68, -0.75)][i], textcoords='data',
                                arrowprops=dict(
                                    width=0.2,
                                    headlength=2,
                                    headwidth=2,
                                    shrink=0.05,
                                    alpha=0.4,
                                    fc="k"
                                ),
                            )
                        if show_std5:
                            for pot_file in pot_files[-5:]:  # only last 5
                                pot_new_r, pot_new_u, _ = readin_table(pot_file)
                                label = label if i == 0 else None
                                line, = ax.plot(pot_new_r, pot_new_u, label=None, color=color, linestyle=linestyle, linewidth=0.3)
                                if show_inset:
                                    axins.plot(pot_new_r, pot_new_u, label=None, color=color, linestyle=linestyle, linewidth=0.3)

            axes[2].set_xlabel(r'$r$ in \si{\nano\meter}')
            axes[1].set_ylabel(r'$u_{40}(r)$ in \si{\kilo\joule\per\mole}')
            for ax in axes:
                ax.set_xlim(0.36, 1.24)
            axes[0].set_ylim(-1.4, 0.4)
            axes[1].set_ylim(-1.4, 0.4)
            axes[2].set_ylim(-1.4, 0.4)
            
            # legend
            legend = fig.legend(loc=(0.42, 0.43), ncol=2)
            #shift = max([t.get_window_extent().width for t in legend.get_texts()])
            #for t in legend.get_texts():
                #t.set_ha('right')
                #t.set_position((shift, 0))
                
            fig.savefig('../figures/last-potential-hexane.pdf')
            fig.set_constrained_layout_pads(w_pad=0.00, h_pad=0.00, hspace=0., wspace=0.)
            plt.show()

plot_last_potential(show_std5=False, show_annotations=False, show_inset=False)

In [ ]:
!cp ../figures/last-potential-hexane.pdf /home/marvin/research/output/iie-general-paper/figures/

## plot last potential hexane cut-off

In [ ]:
def plot_gn_cut_variations(show_target=False):
    mpl_rc_local = {
        'legend.handlelength': 1.2,
        'legend.handletextpad': 0.5,
        'legend.columnspacing': 1.4,
    }
    with plt.rc_context({**mpl_rc_global, **mpl_rc_local}):
        
        #fg_sys_types_to_do = fg_sys_types
        fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['hexane']}
        
        mappings_to_do = mappings
        #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
        
        states_to_do = states
        #states_to_do = {key: states[key] for key in ['pure']}
        
        votca_settings_to_do = {key: votca_settings[key] for key in [
            #'ibi-ibiintra',
            #'imco-ibiintra',
            #'imcot-ibiintra',
            #'hncn-ibiintra',
            #*[f'hncgntco{cut_off_10:02d}-altibiintra' for cut_off_10 in range(5, 12, 2)]
            #*[f'hncgntco{cut_off_10:02d}-altibiintra' for cut_off_10 in range(5, 12, 3)]
            *[f'hncgntco{cut_off_10:02d}-altibiintra' for cut_off_10 in [5, 7, 9]],
            'hncn-altibiintra',
            #*[f'hncgntco{cut_off_10:02d}-altibiintra' for cut_off_10 in [5, 6, 7]]
        ]}
        
        ia_to_show = 'all'
        #ia_to_show = ['AR-MW']
        #ia_to_show = ['AR-MW', 'AR-AR']

        # groupby fg, state, mapping
        for (fg_sys_type_key, state_key, mapping_key), group in itertools.groupby(cg_setup_generator(
            fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=False),
                                                                                  lambda x: (x[1], x[2], x[3])):

            # create figure
            fig, axes = plt.subplots(nrows=3, ncols=2, figsize=[3.2, 2.0], constrained_layout=True, dpi=300, sharex='col')

            # iterate in group
            print(fg_sys_type_key, state_key, mapping_key)
            for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in group:
                print(' ', votca_setting_key)

                init_method = cg_problem['votca-settings']['inverse']['initial_guess']['method']
                label = label_of_method[votca_setting_key.split('-')[0]]
                color = color_of_method[votca_setting_key.split('-')[0]]
                linestyle = linestyle_of_method[votca_setting_key.split('-')[0]]

                # plot last potential
                working_dir = os.path.join(cg_problem['folder'])
                with WorkingDir(working_dir):
                    min_pot = 0
                    # iterate interactions
                    for i, cg_beadtype_pair in enumerate(cg.gen_beadtype_pairs(cg_problem, return_dict=True)):
                        ia_name = '-'.join(sorted((key for key, value in cg_beadtype_pair)))
                        if ia_to_show != 'all' and ia_name not in ia_to_show:
                            continue
                        #print(ia_name)
                        #if v != 0:
                            #color = color_of_method[votca_setting_key.split('-')[0]]
                            #color = np.array(color)
                            #color[0:3] *= [0.75, 0.85, 1.0][i]
                            #color = tuple(color)
                        
                        # potential
                        pot_files = sorted(glob.glob(f"step_???/{ia_name}.pot.cur"))
                        pot_file = pot_files[-1]  # only last one
                        step = int(re.search('step_(\d+)', pot_file).group(1)) - 1  # -1 because we use .pot.cur
                        try:
                            pot_new_r, pot_new_u, _ = readin_table(pot_file)
                        except:
                            print(f".. could not load {pot_file} ..")
                            continue
                        #print(step)
                        label = label if i == 0 else None
                        #linestyle = ['-', '--', ':'][i]
                        axes[i, 0].plot(pot_new_r, pot_new_u, label=label, color=color, linestyle=linestyle, linewidth=1.0)
                        if v == 0:
                            axes[i, 0].text(0.75, 0.15, ia_name, transform=axes[i, 0].transAxes)
                        
                        # RDF target
                        if show_target and v == 0:
                            label = 'tgt' if i == 0 else None
                            dist_tgt_r, dist_tgt_g, _ = readin_table(f"{ia_name}.dist.tgt")
                            axes[i][1].plot(dist_tgt_r, dist_tgt_g, label=label, color='k', linestyle=':', linewidth=1.0, zorder=10)
                            
                        # RDF
                        dist_files = sorted(glob.glob(f"step_???/{ia_name}.dist.new"))
                        dist_file = dist_files[-1]  # only last one
                        step_dist = int(re.search('step_(\d+)', dist_file).group(1)) - 1  # -1 because we use .pot.cur
                        try:
                            dist_new_r, dist_new_g, _ = readin_table(dist_file)
                        except:
                            print(f".. could not load {dist_file} ..")
                            continue
                        #print(step_dist)
                        label = label if i == 0 else None
                        line, = axes[i][1].plot(dist_new_r, dist_new_g, label=None, color=color, linestyle=linestyle, linewidth=1.0, zorder=i)
                            
                        
            axes[-1][0].set_xlabel(r'$r$ in \si{\nano\meter}')
            axes[0][0].set_title(r'$u_{40}(r)$ in \si{\kilo\joule\per\mole}')
            axes[-1][1].set_xlabel(r'$r$ in \si{\nano\meter}')
            #axes[1].set_ylabel(r'$g(r)$')
            axes[0][1].set_title(r'$g_{40}(r)$')
            axes[-1][0].set_xlim(0.35, 1.2)
            axes[-1][1].set_xlim(0.35, 1.2)
            for ax in axes[:, 0]:
                ax.set_ylim(-1.5, 0.5)
            for ax in axes[:, 1]:
                ax.set_ylim(0.7, 1.7)
                ax.set_yticks([1.0, 1.5])
                ax.yaxis.tick_right()
            #leg = fig.legend(ncol=5, loc=(0.1, 0.92))
            leg = fig.legend(ncol=5, loc='center left',
                 bbox_to_anchor=(-0.2, 1.6), bbox_transform=axes[0, 0].transAxes)
            print(leg.get_in_layout())
            fig.set_constrained_layout_pads(w_pad=0.02, h_pad=0.00, hspace=0., wspace=0.)
            fig.savefig('../figures/cut-off-variation.pdf', bbox_inches='tight', pad_inches=0.01)
            fig.set_constrained_layout_pads(w_pad=0.02, h_pad=0.00, hspace=0., wspace=0.)
            plt.show()

plot_gn_cut_variations(show_target=True)

In [ ]:
!cp ../figures/cut-off-variation.pdf /home/marvin/research/output/iie-general-paper/figures/

## plot last potential hexane constraints

In [ ]:
from mpl_toolkits.axes_grid1.inset_locator import zoomed_inset_axes, mark_inset

def plot_last_potential2(show_std5=False, show_annotations=False, show_inset=False):
    mpl_rc_local = {
        'legend.handlelength': 2.0,
        'legend.labelspacing': -0.1,
    }
    with plt.rc_context({**mpl_rc_global, **mpl_rc_local}):
        
        #fg_sys_types_to_do = fg_sys_types
        fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['hexane']}
        
        mappings_to_do = mappings
        #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
        
        states_to_do = states
        #states_to_do = {key: states[key] for key in ['pure']}
        
        votca_settings_to_do = {key: votca_settings[key] for key in [
            'hncgnt-altibiintra',
            'phncgnt-altibiintra',
            'PEhncgnt-altibiintra',
            'KBIhncgnt-altibiintra',
            'KBIphncgnt-altibiintra',
            'PEphncgnt-altibiintra',
        ]}
        
        ia_to_show = 'all'
        #ia_to_show = ['AR-MW']
        #ia_to_show = ['AR-MW', 'AR-AR']

        # groupby fg, state, mapping
        for (fg_sys_type_key, state_key, mapping_key), group in itertools.groupby(cg_setup_generator(
            fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=False),
                                                                                  lambda x: (x[1], x[2], x[3])):

            # create figure
            fig, axes = plt.subplots(nrows=3, ncols=1, sharex='all', figsize=[3.2, 3.1], constrained_layout=True, dpi=300)
            fig.set_constrained_layout_pads(w_pad=0.01, h_pad=0.00, hspace=0., wspace=0.)
            #left, bottom, width, height = [0.75, 0.75, 0.2, 0.2]
            
            if show_inset:
                axins = zoomed_inset_axes(ax, 30, loc='upper right')
                # sub region of the original image
                x1, x2, y1, y2 = 1.190, 1.201, -0.02, 0.02
                axins.set_xlim(x1, x2)
                axins.set_ylim(y1, y2)
                # fix the number of ticks on the inset axes
                axins.yaxis.get_major_locator().set_params(nbins=2)
                axins.xaxis.get_major_locator().set_params(nbins=2)
                plt.setp(axins.get_xticklabels(), visible=False)
                #plt.setp(axins.get_yticklabels(), visible=False)
                # draw a bbox of the region of the inset axes in the parent axes and
                # connecting lines between the bbox and the inset axes area
                mark_inset(ax, axins, loc1=3, loc2=4, fc="none", ec="0.5")

            #ax2 = fig.add_axes([left, bottom, width, height])
            line_label_dict = {}
            #line_label_dict[(label, init_method)] = (empty, label)  # first row, second column
            #line_label_dict = collections.defaultdict(lambda label, _: (empty, label))

            # iterate in group
            #print(fg_sys_type_key, state_key, mapping_key)
            for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in group:
                print(' ', votca_setting_key)

                label = label_of_method[votca_setting_key.split('-')[0]]
                color = color_of_method[votca_setting_key.split('-')[0]]
                linestyle = linestyle_of_method[votca_setting_key.split('-')[0]]

                # plot last potential
                working_dir = os.path.join(cg_problem['folder'])
                with WorkingDir(working_dir):
                    min_pot = 0
                    # iterate interactions
                    for i, cg_beadtype_pair in enumerate(cg.gen_beadtype_pairs(cg_problem, return_dict=True)):
                        ia_name = '-'.join(sorted((key for key, value in cg_beadtype_pair)))
                        if ia_to_show != 'all' and ia_name not in ia_to_show:
                            continue
                        ax = axes[i]
                        #print(ia_name)
                        if v == 0:
                            ax.text(0.15, 0.85, ia_name, transform=ax.transAxes)

                        # load new
                        pot_files = sorted(glob.glob(f"step_???/{ia_name}.pot.cur"))
                        pot_file = pot_files[-1]  # only last one
                        step = int(re.search('step_(\d+)', pot_file).group(1))
                        pot_new_r, pot_new_u, _ = readin_table(pot_file)
                        print(step)
                        label = label if i == 0 else None
                        line, = ax.plot(pot_new_r, pot_new_u, label=label, color=color, linestyle=linestyle)
                        if show_inset:
                            axins.plot(pot_new_r, pot_new_u, label=label, color=color, linestyle=linestyle)
                        if show_annotations:
                            ndx = 128
                            ax.annotate(
                                ia_name,
                                xy=(pot_new_r[ndx], pot_new_u[ndx]), xycoords='data',
                                xytext=[(0.5, -0.5), (0.8, -0.7), (0.68, -0.75)][i], textcoords='data',
                                arrowprops=dict(
                                    width=0.2,
                                    headlength=2,
                                    headwidth=2,
                                    shrink=0.05,
                                    alpha=0.4,
                                    fc="k"
                                ),
                            )
                        if show_std5:
                            for pot_file in pot_files[-5:]:  # only last 5
                                pot_new_r, pot_new_u, _ = readin_table(pot_file)
                                label = label if i == 0 else None
                                line, = ax.plot(pot_new_r, pot_new_u, label=None, color=color, linestyle=linestyle, linewidth=0.3)
                                if show_inset:
                                    axins.plot(pot_new_r, pot_new_u, label=None, color=color, linestyle=linestyle, linewidth=0.3)

            axes[2].set_xlabel(r'$r$ in \si{\nano\meter}')
            axes[1].set_ylabel(r'$u_{40}(r)$ in \si{\kilo\joule\per\mole}')
            for ax in axes:
                ax.set_xlim(0.36, 1.24)
            axes[0].set_ylim(-2.6, 0.7)
            axes[1].set_ylim(-1.8, 0.3)
            axes[2].set_ylim(-1.8, 0.3)
            
            # legend
            legend = fig.legend(loc=(0.5, 0.41), ncol=1)
            #shift = max([t.get_window_extent().width for t in legend.get_texts()])
            #for t in legend.get_texts():
                #t.set_ha('right')
                #t.set_position((shift, 0))
                
            fig.savefig('../figures/last-potential-hexane2.pdf')
            fig.set_constrained_layout_pads(w_pad=0.01, h_pad=0.00, hspace=0., wspace=0.)
            plt.show()

plot_last_potential2(show_std5=False, show_annotations=False, show_inset=False)

In [ ]:
!cp ../figures/last-potential-hexane2.pdf /home/marvin/research/output/iie-general-paper/figures/

## table properties hexane

In [ ]:
def table_properties():

    #fg_sys_types_to_do = fg_sys_types
    fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['hexane']}

    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}

    states_to_do = states
    #states_to_do = {key: states[key] for key in ['pure']}

    votca_settings_to_do = {key: votca_settings[key] for key in [
        'hncgnt-altibiintra',
        'phncgnt-altibiintra',
        'PEhncgnt-altibiintra',
        'KBIhncgnt-altibiintra',
        'KBIphncgnt-altibiintra',
        'PEphncgnt-altibiintra',
    ]}

    index = ['atomistic'] + [vskey for vskey in votca_settings_to_do.keys()]
    index_final = ['target'] + [label_of_method[vskey.split('-')[0]] for vskey in votca_settings_to_do.keys()]
    index_translation_dict = {ff: ff_final for ff, ff_final in zip(index, index_final)}
    columns = ['p', 'PE', 'G_AA', 'G_AB', 'G_BB', 'sigma_g_1e3']
    columns_final = [
        r'{\begin{tabular}{@{}c@{}}$p$\\in \si{bar}\end{tabular}}',
        r'{\begin{tabular}{@{}c@{}}$P\!E_\text{inter}$\\in \si{\kilo\joule\per\mole}\end{tabular}}',
        r'{\begin{tabular}{@{}c@{}}$G_\text{AA}$\\in \si{\angstrom\cubed}\end{tabular}}',
        r'{\begin{tabular}{@{}c@{}}$G_\text{AB}$\\in \si{\angstrom\cubed}\end{tabular}}',
        r'{\begin{tabular}{@{}c@{}}$G_\text{BB}$\\in \si{\angstrom\cubed}\end{tabular}}',
        r'{\begin{tabular}{@{}c@{}}$\chi(g)$\\$\times 1000$\end{tabular}}',
    ]
    columns_translation_dict = {prop: prop_final for prop, prop_final in zip(columns, columns_final)}
    
    df = pd.DataFrame(
        index=index,
        columns=columns,
    )
    df.at['atomistic', 'p'] = f"{1.0:.1f}"
    df.at['atomistic', 'PE'] = f"{-30.42:.1f}"
    df.at['atomistic', 'G_AA'] = f"{-0.2074236 * 1000:.1f}"
    df.at['atomistic', 'G_AB'] = f"{-0.1933343 * 1000:.1f}"
    df.at['atomistic', 'G_BB'] = f"{-0.2019402 * 1000:.1f}"
    df.at['atomistic', 'sigma_g_1e3'] = r"\texendash"
        
    for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
        fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=True):

        working_dir = os.path.join(cg_problem['folder'])
        with WorkingDir(working_dir):

            # pressure
            pressures = []
            #for step in range(36, 41):
            #step = f"step_{step:03d}"
            for step in sorted(glob.glob("step_???"))[-6:]:
                print(step)
                run_bash(f"gmx energy -f {step}/ener.edr -o /tmp/energy-temp.xvg <<< 'pressure'")
                data, _ = gt.xvg.load("/tmp/energy-temp.xvg")
                run_bash(f"rm -f /tmp/energy-temp.xvg")
                pressure_data = np.asarray(data['Pressure'])
                pressures.append(np.mean(pressure_data))
            df.at[votca_setting_key, 'p'] = f"{np.mean(pressures):.1f} +- {np.std(pressures):.1f}"
            
            # Potential energy
            PEs = []
            for step in sorted(glob.glob("step_???"))[-6:]:
                run_bash(f"gmx energy -f {step}/ener.edr -nmol 3000 -o /tmp/energy-temp.xvg <<< 'LJ-(SR)'")
                data, _ = gt.xvg.load("/tmp/energy-temp.xvg")
                run_bash(f"rm -f /tmp/energy-temp.xvg")
                PE_data = np.asarray(data['LJ (SR)'])
                PE_mean = np.mean(PE_data)
                PEs.append(PE_mean)
            df.at[votca_setting_key, 'PE'] = f"{np.mean(PEs):.1f} +- {max(0.1, np.std(PEs)):.1f}"
            
            # Kirkwood-Buff integrals
            kbis = {'AA': [], 'AB': [], 'BB': []}
            for step in sorted(glob.glob("step_???"))[-6:]:
                for i, cg_beadtype_pair in enumerate(cg.gen_beadtype_pairs(cg_problem, return_dict=True)):
                    ia_name = '-'.join(sorted((key for key, value in cg_beadtype_pair)))
                    ia_name_short = ia_name.replace('-', '')

                    # load RDF
                    dist_file = f"{step}/{ia_name}.dist.new"
                    r, g, _ = readin_table(dist_file)
                    Delta_r = r[1] - r[0]
                    kbi = 4 * np.pi * np.sum(r**2 * (g - 1)) * Delta_r
                    kbis[ia_name_short].append(kbi)
            for ia_name_short, kbi in kbis.items():
                df.at[votca_setting_key, f'G_{ia_name_short}'] = f"{np.mean(kbi) * 1000:.1f} +- {max(0.1, np.std(kbi) * 1000):.1f}"
                
            # RDF convergence
            sigmas = {'AA': [], 'AB': [], 'BB': []}
            for i, cg_beadtype_pair in enumerate(cg.gen_beadtype_pairs(cg_problem, return_dict=True)):
                ia_name = '-'.join(sorted((key for key, value in cg_beadtype_pair)))
                ia_name_short = ia_name.replace('-', '')
                
                # load RDF tgt
                dist_file_tgt = f"step_001/{ia_name}.dist.tgt"
                r_tgt, g_tgt, _ = readin_table(dist_file_tgt)
                # cut-off
                cut_off = cg_problem['functional-votca-settings-input']['cut']
                cut, _ = csg.calc_slices(r_tgt, cut_off)
                
                for step in sorted(glob.glob("step_???"))[-6:]:
                    # load RDF new
                    dist_file = f"{step}/{ia_name}.dist.new"
                    r, g, _ = readin_table(dist_file)
                    
                    sigma = np.sqrt(1/max(r[cut]) * np.trapz(x=r[cut], y=(g - g_tgt)[cut]**2))
                    sigmas[ia_name_short].append(sigma)
            sigmas_sum = [s_AA + s_AB + s_BB for s_AA, s_AB, s_BB in zip(sigmas['AA'], sigmas['AB'], sigmas['BB'])]
            df.at[votca_setting_key, 'sigma_g_1e3'] = f"{np.mean(sigmas_sum) * 1e3:.1f} +- {max(0.0001, np.std(sigmas_sum)) * 1e3:.1f}"
                
    df.rename(index=index_translation_dict, inplace=True)
    df.rename(columns=columns_translation_dict, inplace=True)
    print(df.to_latex(escape=False, #formatters=formatters,  #.astype(float)
                      column_format=(r"l "
                                     r"S[table-format=4.1(3),separate-uncertainty=false] "
                                     r"S[table-format=2.1(1),separate-uncertainty=false] "
                                     r"S[table-format=3.1(1),separate-uncertainty=false] "
                                     r"S[table-format=3.1(1),separate-uncertainty=false] "
                                     r"S[table-format=3.1(1),separate-uncertainty=false] "
                                     r"S[table-format=2.1(1),separate-uncertainty=false]")))
    return df

table_properties()

# various tests

In [ ]:
g = np.array([0.00195192, 0.00391822, 0.00721423, 0.01245533, 0.0203828,  0.03172717, 0.04715085, 0.06725381, 0.09230073])
ot, mt = 0.001, 0.1
ot_ = g[0]
mt_ = g[-1]

In [ ]:
plt.figure(dpi=200)
merge_scaling_vector = np.sqrt(g - ot) / np.sqrt(mt - ot)
plt.plot(merge_scaling_vector, label='sqrt')
merge_scaling_vector = np.log(g - ot + 1) / np.log(mt - ot + 1)
plt.plot(merge_scaling_vector, label='log')
merge_scaling_vector = (g - ot) / (mt - ot)
plt.plot(merge_scaling_vector, label='linear')
x = np.linspace(start=0, stop=1, num=len(g))
merge_scaling_vector = 3 * x**2 - 2 * x**3
plt.plot(merge_scaling_vector, label='new')
plt.legend()
plt.show()